In [174]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import xgboost as xgb
import lightgbm as lgb
import statsmodels.api as sm
import warnings
import shap
from sklearn.model_selection import StratifiedKFold
#from pycaret.regression import *
from pycaret.classification import *
from xgboost import XGBRegressor
from xgboost import XGBClassifier
from sklearn.tree import ExtraTreeClassifier
from sklearn.tree import ExtraTreeRegressor
from sklearn.experimental import enable_iterative_imputer 
from sklearn.impute import KNNImputer
from sklearn.impute import IterativeImputer
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.tree import DecisionTreeClassifier
from sklearn.svm import SVC
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import OneHotEncoder
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import train_test_split
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import RandomizedSearchCV
from sklearn.ensemble import RandomForestClassifier
from sklearn.ensemble import RandomForestRegressor
from catboost import CatBoostClassifier, Pool
from sklearn.ensemble import AdaBoostClassifier
from sklearn.ensemble import AdaBoostRegressor
from catboost import CatBoostRegressor
from catboost import CatBoostClassifier
from sklearn.metrics import mean_squared_error
from sklearn.impute import KNNImputer

In [175]:
warnings.simplefilter(action='ignore')
pd.set_option('display.max_columns', None)

# Data

In [176]:
train_data = pd.read_csv("./train.csv")
train_data

PRODUCT_ID  Y_Class  Y_Quality         TIMESTAMP     LINE PRODUCT_CODE  \
0    TRAIN_000        1   0.533433   2022-06-13 5:14  T050304         A_31   
1    TRAIN_001        2   0.541819   2022-06-13 5:22  T050307         A_31   
2    TRAIN_002        1   0.531267   2022-06-13 5:30  T050304         A_31   
3    TRAIN_003        2   0.537325   2022-06-13 5:39  T050307         A_31   
4    TRAIN_004        1   0.531590   2022-06-13 5:47  T050304         A_31   
..         ...      ...        ...               ...      ...          ...   
593  TRAIN_593        1   0.526546  2022-09-08 14:30  T100306         T_31   
594  TRAIN_594        0   0.524022  2022-09-08 22:38  T050304         A_31   
595  TRAIN_595        0   0.521289  2022-09-08 22:47  T050304         A_31   
596  TRAIN_596        1   0.531375  2022-09-08 14:38  T100304         O_31   
597  TRAIN_597        1   0.533702  2022-09-08 14:46  T100306         O_31   

      X_1   X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  X_10   X_11   X_12  \
0     NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN   NaN   NaN    NaN    NaN   
1     NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN   NaN   NaN    NaN    NaN   
2     NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN   NaN   NaN    NaN    NaN   
3     NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN   NaN   NaN    NaN    NaN   
4     NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN   NaN   NaN    NaN    NaN   
..    ...   ...  ...   ...   ...  ...   ...   ...   ...   ...    ...    ...   
593   2.0  95.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0   2.0  468.9  473.9   
594   NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN   NaN   NaN    NaN    NaN   
595   NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN   NaN   NaN    NaN    NaN   
596  40.0  94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   2.0  505.8  510.9   
597  21.0  87.0  0.0  45.0  10.0  0.0  61.0  10.0  52.0   2.0  470.6  474.9   

      X_13  X_14  X_15   X_16   X_17   X_18   X_19   X_20   X_21   X_22  X_23  \
0      NaN   NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
1      NaN   NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
2      NaN   NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
3      NaN   NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
4      NaN   NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
..     ...   ...   ...    ...    ...    ...    ...    ...    ...    ...   ...   
593  459.2   0.0   0.0  247.5  248.0  247.3  250.0  527.0  538.0  522.0  0.19   
594    NaN   NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
595    NaN   NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
596  497.1   0.0   0.0  247.5  248.1  247.3  250.0  489.0  498.0  485.0  0.19   
597  462.9   0.0   0.0  247.5  248.0  247.3  250.0  525.0  534.0  520.0  0.19   

     X_24  X_25   X_26   X_27   X_28   X_29   X_30   X_31   X_32   X_33  \
0     NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
1     NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2     NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
3     NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
4     NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
..    ...   ...    ...    ...    ...    ...    ...    ...    ...    ...   
593  0.19  0.19  155.0  155.0  155.0  155.0  185.0  185.0  185.0  185.0   
594   NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
595   NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
596  0.19  0.19  155.0  155.0  155.0  155.0  185.0  185.0  185.0  185.0   
597  0.20  0.19  155.0  155.0  155.0  155.0  185.0  185.0  185.0  185.0   

      X_34   X_35   X_36   X_37   X_38  X_39  X_40  X_41  X_42  X_43  X_44  \
0      NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN   NaN   NaN   NaN   
1      NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN   NaN   NaN   NaN   
2      NaN

In [135]:
train_data['YEAR'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.year
train_data['MONTH'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.month
train_data['DAY'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.day
train_data['HOUR'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.hour
train_data['MINUTE'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.minute
train_data['DAY_OF_WEEK'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.day_name()

In [177]:
colls = []
for coll in train_data :
    if 'X' in coll and train_data[coll].isna().sum() == 598 :
        colls.append(coll)
print(len(colls))

82


In [178]:
train_data.drop(colls, inplace = True, axis = 1)

In [139]:
train_data = train_data.drop(['MONTH', 'MINUTE', 'DAY', 'YEAR'], axis = 1)

KeyError: "['MONTH', 'MINUTE', 'DAY', 'YEAR'] not found in axis"

In [179]:
#train_data.loc[train_data.DAY_OF_WEEK == 'Monday','DAY_OF_WEEK'] = 1
#train_data.loc[train_data.DAY_OF_WEEK == 'Tuesday','DAY_OF_WEEK'] = 2
#train_data.loc[train_data.DAY_OF_WEEK == 'Wednesday','DAY_OF_WEEK'] = 3
#train_data.loc[train_data.DAY_OF_WEEK == 'Thursday','DAY_OF_WEEK'] = 4
#train_data.loc[train_data.DAY_OF_WEEK == 'Friday','DAY_OF_WEEK'] = 5
#train_data.loc[train_data.DAY_OF_WEEK == 'Saturday','DAY_OF_WEEK'] = 6
#train_data.loc[train_data.DAY_OF_WEEK == 'Sunday','DAY_OF_WEEK'] = 7

train_data.loc[train_data.PRODUCT_CODE == 'A_31','PRODUCT_CODE'] = 1
train_data.loc[train_data.PRODUCT_CODE == 'T_31','PRODUCT_CODE'] = 2
train_data.loc[train_data.PRODUCT_CODE == 'O_31','PRODUCT_CODE'] = 3

train_data.drop(['PRODUCT_ID', 'TIMESTAMP'], axis = 1, inplace = True)
train_data

Y_Class  Y_Quality     LINE PRODUCT_CODE   X_1   X_2  X_3   X_4   X_5  \
0          1   0.533433  T050304            1   NaN   NaN  NaN   NaN   NaN   
1          2   0.541819  T050307            1   NaN   NaN  NaN   NaN   NaN   
2          1   0.531267  T050304            1   NaN   NaN  NaN   NaN   NaN   
3          2   0.537325  T050307            1   NaN   NaN  NaN   NaN   NaN   
4          1   0.531590  T050304            1   NaN   NaN  NaN   NaN   NaN   
..       ...        ...      ...          ...   ...   ...  ...   ...   ...   
593        1   0.526546  T100306            2   2.0  95.0  0.0  45.0  10.0   
594        0   0.524022  T050304            1   NaN   NaN  NaN   NaN   NaN   
595        0   0.521289  T050304            1   NaN   NaN  NaN   NaN   NaN   
596        1   0.531375  T100304            3  40.0  94.0  0.0  45.0  11.0   
597        1   0.533702  T100306            3  21.0  87.0  0.0  45.0  10.0   

     X_6   X_7   X_8   X_9  X_10   X_11   X_12   X_13  X_14  X_15   X_16  \
0    NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
1    NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
2    NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
3    NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
4    NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
..   ...   ...   ...   ...   ...    ...    ...    ...   ...   ...    ...   
593  0.0  50.0  10.0  52.0   2.0  468.9  473.9  459.2   0.0   0.0  247.5   
594  NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
595  NaN   NaN   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN   
596  0.0  45.0  10.0  31.0   2.0  505.8  510.9  497.1   0.0   0.0  247.5   
597  0.0  61.0  10.0  52.0   2.0  470.6  474.9  462.9   0.0   0.0  247.5   

      X_17   X_18   X_19   X_20   X_21   X_22  X_23  X_24  X_25   X_26   X_27  \
0      NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
1      NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
2      NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
3      NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
4      NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
..     ...    ...    ...    ...    ...    ...   ...   ...   ...    ...    ...   
593  248.0  247.3  250.0  527.0  538.0  522.0  0.19  0.19  0.19  155.0  155.0   
594    NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
595    NaN    NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN   
596  248.1  247.3  250.0  489.0  498.0  485.0  0.19  0.19  0.19  155.0  155.0   
597  248.0  247.3  250.0  525.0  534.0  520.0  0.19  0.20  0.19  155.0  155.0   

      X_28   X_29   X_30   X_31   X_32   X_33   X_34   X_35   X_36   X_37  \
0      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
1      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
3      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
4      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
593  155.0  155.0  185.0  185.0  185.0  185.0  155.0  155.0  155.0  155.0   
594    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
595    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
596  155.0  155.0  185.0  185.0  185.0  185.0  155.0  155.0  155.0  155.0   
597  155.0  155.0  185.0  185.0  185.0  185.0  155.0  155.0  155.0  155.0   

      X_38  X_39  X_40  X_41  X_42  X_43  X_44  X_45  X_46  X_47  X_48  X_49  \
0      NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
1      NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
2      NaN   NaN 

In [180]:
T050304 = train_data[train_data['LINE'] == 'T050304']
T050307 = train_data[train_data['LINE'] == 'T050307']
T010305 = train_data[train_data['LINE'] == 'T010305']
T010306 = train_data[train_data['LINE'] == 'T010306']
T100304 = train_data[train_data['LINE'] == 'T100304']
T100306 = train_data[train_data['LINE'] == 'T100306']

In [181]:
T050304.drop(['LINE'], axis = 1, inplace = True)
T050307.drop(['LINE'], axis = 1, inplace = True)
T010305.drop(['LINE'], axis = 1, inplace = True)
T010306.drop(['LINE'], axis = 1, inplace = True)
T100304.drop(['LINE'], axis = 1, inplace = True)
T100306.drop(['LINE'], axis = 1, inplace = True)

In [182]:
T050304_col = []
for col in T050304 :
    if 'X' in col and T050304[col].isna().sum() == 78 :
        T050304_col.append(col)
print(len(T050304_col))

T050304.drop(T050304_col, inplace = True, axis = 1)

825


In [183]:
T050307_col = []
for col in T050307 :
    if 'X' in col and T050307[col].isna().sum() == 42 :
        T050307_col.append(col)
print(len(T050307_col))

T050307.drop(T050307_col, inplace = True, axis = 1)

818


In [184]:
T010305_col = []
for col in T010305 :
    if 'X' in col and T010305[col].isna().sum() == 59 :
        T010305_col.append(col)
print(len(T010305_col))

T010305.drop(T010305_col, inplace = True, axis = 1)

1907


In [185]:
T010306_col = []
for col in T010306 :
    if 'X' in col and T010306[col].isna().sum() == 70 :
        T010306_col.append(col)
print(len(T010306_col))

T010306.drop(T010306_col, inplace = True, axis = 1)

1907


In [186]:
T100304_col = []
for col in T100304 :
    if 'X' in col and T100304[col].isna().sum() == 175 :
        T100304_col.append(col)
print(len(T100304_col))

T100304.drop(T100304_col, inplace = True, axis = 1)

2122


In [187]:
T100306_col = []
for col in T100306 :
    if 'X' in col and T100306[col].isna().sum() == 174 :
        T100306_col.append(col)
print(len(T100306_col))

T100306.drop(T100306_col, inplace = True, axis = 1)

2122


In [143]:
T050304 = T050304.fillna(0)
T050307 = T050307.fillna(0)
T010305 = T010305.fillna(0)
T010306 = T010306.fillna(0)
T100304 = T100304.fillna(0)
T100306 = T100306.fillna(0)

In [188]:
T050304 = T050304.fillna(T050304.mean())
T050307 = T050307.fillna(T050307.mean())
T010305 = T010305.fillna(T010305.mean())
T010306 = T010306.fillna(T010306.mean())
T100304 = T100304.fillna(T100304.mean())
T100306 = T100306.fillna(T100306.mean())

In [189]:
zero_one = (train_data[train_data['Y_Class'] == 1]['Y_Quality'].min() + train_data[train_data['Y_Class'] == 0]['Y_Quality'].max())/2
one_two = (train_data[train_data['Y_Class'] == 2]['Y_Quality'].min() + train_data[train_data['Y_Class'] == 1]['Y_Quality'].max())/2
print(zero_one, one_two)

0.5250761905000001 0.5348968255


# T050304

In [190]:
T050304_class = T050304['Y_Class']
T050304_target = T050304['Y_Quality']
T050304_data = T050304.drop(['Y_Class', 'Y_Quality'], axis = 1)
T050304_data

PRODUCT_CODE    X_128    X_129  X_132  X_133  X_134  X_135  X_136  X_137  \
0               1   7813.0   7813.0   0.19    0.2   0.19    0.2  228.0  228.0   
2               1   7815.0   7815.0   0.19    0.2   0.19    0.2  228.0  228.0   
4               1   7817.0   7817.0   0.19    0.2   0.18    0.2  228.0  228.0   
6               1   7820.0   7820.0   0.19    0.2   0.19    0.2  228.0  228.0   
8               1   7822.0   7822.0   0.19    0.2   0.19    0.2  228.0  228.0   
..            ...      ...      ...    ...    ...    ...    ...    ...    ...   
581             1  11864.0  11864.0   0.19    0.2   0.19    0.2  230.0  230.0   
582             1  11898.0  11898.0   0.18    0.2   0.18    0.2  230.0  230.0   
583             1  11920.0  11920.0   0.19    0.2   0.19    0.2  230.0  230.0   
594             1  14810.0  14810.0   0.19    0.2   0.19    0.2  304.0  304.0   
595             1  14813.0  14813.0   0.19    0.2   0.19    0.2  304.0  304.0   

     X_138  X_139  X_140  X_141  X_142  X_143   X_144   X_145   X_146  X_147  \
0    225.0  582.9  587.1  567.3    0.0    0.0  249.96  249.99  247.46  250.0   
2    225.0  583.8  587.6  572.9    0.0    0.0  249.97  249.99  249.10  250.0   
4    225.0  583.2  587.3  565.9    0.0    0.0  249.96  249.99  246.46  250.0   
6    225.0  583.4  587.3  543.9    0.0    0.0  249.95  249.99  235.56  250.0   
8    225.0  583.3  587.2  571.9    0.0    0.0  249.97  249.99  248.96  250.0   
..     ...    ...    ...    ...    ...    ...     ...     ...     ...    ...   
581  230.0  584.0  588.7  558.2    0.0    0.0  249.96  249.99  241.22  250.0   
582  230.0  583.3  588.4  570.1    0.0    0.0  249.96  249.99  248.11  250.0   
583  230.0  583.5  588.3  555.9    0.0    0.0  249.97  249.99  240.71  250.0   
594  304.0  588.9  594.6  574.8    0.0    0.0  249.97  249.99  247.79  250.0   
595  304.0  588.8  594.6  570.8    0.0    0.0  249.96  249.99  245.61  250.0   

     X_148  X_149  X_150  X_151  X_152  X_153  X_154  X_155  X_156  X_157  \
0    428.0  435.0  426.0  179.9  180.0  179.9  180.0  215.0  215.0  214.9   
2    427.0  434.0  425.0  179.9  180.0  179.8  180.0  215.0  215.0  214.9   
4    428.0  434.0  426.0  180.0  180.0  179.8  180.0  215.0  215.1  215.0   
6    428.0  434.0  425.0  180.0  180.1  179.9  180.0  214.9  215.0  214.9   
8    428.0  434.0  426.0  180.0  180.0  179.9  180.0  215.0  215.0  214.9   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
581  427.0  434.0  424.0  180.0  180.0  179.9  180.0  214.9  215.0  214.9   
582  428.0  437.0  425.0  180.0  180.0  179.9  180.0  214.9  215.0  214.9   
583  428.0  435.0  425.0  180.0  180.0  179.9  180.0  214.9  215.0  214.9   
594  424.0  431.0  420.0  179.9  180.0  179.9  180.0  215.0  215.0  214.9   
595  424.0  431.0  420.0  180.0  180.0  179.9  180.0  215.0  215.1  215.0   

     X_158  X_159  X_160  X_161  X_162  X_163  X_164  X_165  X_166  X_167  \
0    215.0  214.9  215.0  214.9  215.0  209.9  210.0  209.9  210.0  209.9   
2    215.0  215.0  215.0  214.9  215.0  209.9  210.0  209.9  210.0  209.9   
4    215.0  214.9  215.0  214.9  215.0  210.0  210.1  210.0  210.0  209.9   
6    215.0  215.0  215.0  214.9  215.0  210.0  210.0  209.9  210.0  210.0   
8    215.0  215.0  215.0  214.9  215.0  210.0  210.1  210.0  210.0  210.0   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
581  215.0  215.0  215.0  214.9  215.0  210.0  210.1  210.0  210.0  210.0   
582  215.0  215.0  215.0  214.9  215.0  210.0  210.1  210.0  210.0  210.0   
583  215.0  214.9  215.0  214.9  215.0  210.0  210.1  210.0  210.0  209.9   
594  215.0  214.9  215.0  214.9  215.0  210.0  210.1  210.0  210.0  210.0   
595  215.0  214.9  215.0  214.9  215.0  209.9  210.0  209.9  210.0  209.9   

     X_168  X_169  X_170  X_171  X_172  X_173  X_174  X_175  X_176  X_177  \
0    210.0  209.9  210.0  205.0  205.0  204.9  205.0  204.9  205.0  204.9   
2    210.0  209.9  210.0  204.9  205.0  204.9  205.0  204.9  205.0 

In [191]:
x

Processing:   0%|          | 0/73 [00:00<?, ?it/s]

In [192]:
T050304_total_models = []

T050304_model_rf = create_model('rf', fold = 5)
T050304_total_models.append(T050304_model_rf)

T050304_model_gbc = create_model('gbc', fold = 5)
T050304_total_models.append(T050304_model_gbc)

T050304_model_et = create_model('et', fold = 5)
T050304_total_models.append(T050304_model_et)

T050304_model_catboost = create_model('catboost', fold = 5)
T050304_total_models.append(T050304_model_catboost)

T050304_model_xgb = create_model('xgboost', fold = 5)
T050304_total_models.append(T050304_model_xgb)

T050304_model_ada = create_model('ada', fold = 5)
T050304_total_models.append(T050304_model_ada)

T050304_model_lightgbm = create_model('lightgbm', fold = 5)
T050304_total_models.append(T050304_model_lightgbm)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [193]:
T050304_model_rf = tune_model(T050304_model_rf, fold=5, choose_better = True)

T050304_model_gbc = tune_model(T050304_model_gbc, fold=5, choose_better = True)

T050304_model_et = tune_model(T050304_model_et, fold=5, choose_better = True)

T050304_model_catboost = tune_model(T050304_model_catboost, fold=5, choose_better = True)

T050304_model_xgb = tune_model(T050304_model_xgb, fold=5, choose_better = True)

T050304_model_ada = tune_model(T050304_model_ada, fold=5, choose_better = True)

T050304_model_lightgbm = tune_model(T050304_model_lightgbm, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


In [194]:
T050304_tuned_models = [T050304_model_rf, T050304_model_gbc, T050304_model_et, T050304_model_catboost, T050304_model_xgb, T050304_model_ada, T050304_model_lightgbm]
T050304_tuned_models

[RandomForestClassifier(bootstrap=True, ccp_alpha=0.0, class_weight=None,
                        criterion='gini', max_depth=None, max_features='auto',
                        max_leaf_nodes=None, max_samples=None,
                        min_impurity_decrease=0.0, min_samples_leaf=1,
                        min_samples_split=2, min_weight_fraction_leaf=0.0,
                        n_estimators=100, n_jobs=-1, oob_score=False,
                        random_state=414, verbose=0, warm_start=False),
 GradientBoostingClassifier(ccp_alpha=0.0, criterion='friedman_mse', init=None,
                            learning_rate=0.05, loss='deviance', max_depth=7,
                            max_features='log2', max_leaf_nodes=None,
                            min_impurity_decrease=0, min_samples_leaf=1,
                            min_samples_split=10, min_weight_fraction_leaf=0.0,
                            n_estimators=60, n_iter_no_change=None,
                            random_state=414, s

In [195]:
for model in T050304_tuned_models:
    display(predict_model(model))

PRODUCT_CODE    X_128    X_129  X_132  X_133  X_134  X_135  X_136  X_137  \
54             1   7830.0   7830.0   0.19   0.20   0.19    0.2  228.0  228.0   
55             1  16654.0  16654.0   0.20   0.21   0.20    0.2  550.0  550.0   
56             1  25564.0  25564.0   0.20   0.21   0.20    0.2  844.0  844.0   
57             1   1009.0   1009.0   0.20   0.21   0.19    0.2   50.0   50.0   
58             1   6065.0  13248.0   0.19   0.20   0.19    0.2  156.0  156.0   
59             1   7827.0   7827.0   0.19   0.20   0.19    0.2  228.0  228.0   
60             1   2932.0   2932.0   0.20   0.21   0.20    0.2  123.0  123.0   
61             1   7832.0   7832.0   0.19   0.20   0.19    0.2  228.0  228.0   
62             1   9401.0   9401.0   0.19   0.20   0.19    0.2  191.0  191.0   
63             1   7820.0   7820.0   0.19   0.20   0.19    0.2  228.0  228.0   
64             1   7825.0   7825.0   0.19   0.20   0.19    0.2  228.0  228.0   
65             1  26581.0  26581.0   0.20   0.21   0.20    0.2  874.0  874.0   
66             1   8207.0   8207.0   0.19   0.20   0.19    0.2  172.0  172.0   
67             1   9445.0   9445.0   0.19   0.20   0.19    0.2  192.0  192.0   
68             1  14810.0  14810.0   0.19   0.20   0.19    0.2  304.0  304.0   
69             1  13369.0  13369.0   0.20   0.21   0.19    0.2  458.0  458.0   
70             1    837.0    837.0   0.19   0.20   0.19    0.2   32.0   32.0   
71             1   5595.0   5595.0   0.20   0.21   0.20    0.2  200.0  200.0   
72             1   2947.0   2947.0   0.20   0.21   0.19    0.2  123.0  123.0   
73             1  22242.0  22242.0   0.20   0.21   0.20    0.2  717.0  717.0   
74             1  21873.0  21873.0   0.19   0.21   0.19    0.2  705.0  705.0   
75             1   7822.0   7822.0   0.19   0.20   0.19    0.2  228.0  228.0   
76             1  25105.0  25105.0   0.20   0.21   0.20    0.2  827.0  827.0   
77             1   5580.0   5580.0   0.19   0.21   0.19    0.2  200.0  200.0   

    X_138  ...  X_2865     X_2866     X_2867     X_2868     X_2869     X_2870  \
54  225.0  ...   352.0  40.419998  38.330002  40.139999  30.719999  76.519997   
55  550.0  ...   353.0  56.119999  61.099998  50.220001  55.529999  66.860001   
56  845.0  ...   353.0  55.540001  52.660000  59.680000  52.990002  63.160000   
57   50.0  ...   353.0  49.490002  55.590000  40.490002  53.840000  66.470001   
58  156.0  ...   353.0  55.049999  59.299999  54.570000  56.139999  64.830002   
59  225.0  ...   352.0  36.549999  32.320000  54.250000  35.150002  78.860001   
60  123.0  ...   353.0  56.860001  50.459999  40.490002  57.340000  66.370003   
61  225.0  ...   353.0  40.529999  31.700001  49.490002  35.730000  79.750000   
62  191.0  ...   352.0  52.650002  58.950001  41.009998  58.430000  64.459999   
63  225.0  ...   353.0  32.500000  41.419998  38.360001  30.830000  76.930000   
64  225.0  ...   352.0  32.119999  34.740002  54.930000  33.160000  76.300003   
65  874.0  ...   345.0  54.900002  61.299999  54.060001  59.930000  62.610001   
66  172.0  ...   343.0  57.939999  55.840000  53.240002  56.720001  64.169998   
67  192.0  ...   350.0  53.810001  51.840000  59.369999  57.630001  66.250000   
68  304.0  ...   353.0  49.470001  53.070000  50.889999  55.099998  66.489998   
69  458.0  ...   352.0  54.759998  54.930000  59.680000  56.779999  64.680000   
70   32.0  ...   353.0  53.490002  58.759998  42.220001  57.919998  66.180000   
71  200.0  ...   352.0  51.557312  54.230148  48.665222  52.332539  66.685966   
72  123.0  ...   352.0  48.279999  51.250000  55.430000  56.950001  67.440002   
73  717.0  ...   353.0  53.490002  58.060001  33.430000  54.709999  61.930000   
74  705.0  ...   352.0  54.410000  54.779999  40.340000  55.310001  61.669998   
75  225.0  ...   353.0  42.250000  43.169998  55.599998  33.259998  78.500000   
76  828.0  ...   353.0  52.389999  57.230000  36.810001  51.470001  65.139999   
77  200.0  ...   342.0  52.970001  59.150002  42.290001  57

PRODUCT_CODE    X_128    X_129  X_132  X_133  X_134  X_135  X_136  X_137  \
54             1   7830.0   7830.0   0.19   0.20   0.19    0.2  228.0  228.0   
55             1  16654.0  16654.0   0.20   0.21   0.20    0.2  550.0  550.0   
56             1  25564.0  25564.0   0.20   0.21   0.20    0.2  844.0  844.0   
57             1   1009.0   1009.0   0.20   0.21   0.19    0.2   50.0   50.0   
58             1   6065.0  13248.0   0.19   0.20   0.19    0.2  156.0  156.0   
59             1   7827.0   7827.0   0.19   0.20   0.19    0.2  228.0  228.0   
60             1   2932.0   2932.0   0.20   0.21   0.20    0.2  123.0  123.0   
61             1   7832.0   7832.0   0.19   0.20   0.19    0.2  228.0  228.0   
62             1   9401.0   9401.0   0.19   0.20   0.19    0.2  191.0  191.0   
63             1   7820.0   7820.0   0.19   0.20   0.19    0.2  228.0  228.0   
64             1   7825.0   7825.0   0.19   0.20   0.19    0.2  228.0  228.0   
65             1  26581.0  26581.0   0.20   0.21   0.20    0.2  874.0  874.0   
66             1   8207.0   8207.0   0.19   0.20   0.19    0.2  172.0  172.0   
67             1   9445.0   9445.0   0.19   0.20   0.19    0.2  192.0  192.0   
68             1  14810.0  14810.0   0.19   0.20   0.19    0.2  304.0  304.0   
69             1  13369.0  13369.0   0.20   0.21   0.19    0.2  458.0  458.0   
70             1    837.0    837.0   0.19   0.20   0.19    0.2   32.0   32.0   
71             1   5595.0   5595.0   0.20   0.21   0.20    0.2  200.0  200.0   
72             1   2947.0   2947.0   0.20   0.21   0.19    0.2  123.0  123.0   
73             1  22242.0  22242.0   0.20   0.21   0.20    0.2  717.0  717.0   
74             1  21873.0  21873.0   0.19   0.21   0.19    0.2  705.0  705.0   
75             1   7822.0   7822.0   0.19   0.20   0.19    0.2  228.0  228.0   
76             1  25105.0  25105.0   0.20   0.21   0.20    0.2  827.0  827.0   
77             1   5580.0   5580.0   0.19   0.21   0.19    0.2  200.0  200.0   

    X_138  ...  X_2865     X_2866     X_2867     X_2868     X_2869     X_2870  \
54  225.0  ...   352.0  40.419998  38.330002  40.139999  30.719999  76.519997   
55  550.0  ...   353.0  56.119999  61.099998  50.220001  55.529999  66.860001   
56  845.0  ...   353.0  55.540001  52.660000  59.680000  52.990002  63.160000   
57   50.0  ...   353.0  49.490002  55.590000  40.490002  53.840000  66.470001   
58  156.0  ...   353.0  55.049999  59.299999  54.570000  56.139999  64.830002   
59  225.0  ...   352.0  36.549999  32.320000  54.250000  35.150002  78.860001   
60  123.0  ...   353.0  56.860001  50.459999  40.490002  57.340000  66.370003   
61  225.0  ...   353.0  40.529999  31.700001  49.490002  35.730000  79.750000   
62  191.0  ...   352.0  52.650002  58.950001  41.009998  58.430000  64.459999   
63  225.0  ...   353.0  32.500000  41.419998  38.360001  30.830000  76.930000   
64  225.0  ...   352.0  32.119999  34.740002  54.930000  33.160000  76.300003   
65  874.0  ...   345.0  54.900002  61.299999  54.060001  59.930000  62.610001   
66  172.0  ...   343.0  57.939999  55.840000  53.240002  56.720001  64.169998   
67  192.0  ...   350.0  53.810001  51.840000  59.369999  57.630001  66.250000   
68  304.0  ...   353.0  49.470001  53.070000  50.889999  55.099998  66.489998   
69  458.0  ...   352.0  54.759998  54.930000  59.680000  56.779999  64.680000   
70   32.0  ...   353.0  53.490002  58.759998  42.220001  57.919998  66.180000   
71  200.0  ...   352.0  51.557312  54.230148  48.665222  52.332539  66.685966   
72  123.0  ...   352.0  48.279999  51.250000  55.430000  56.950001  67.440002   
73  717.0  ...   353.0  53.490002  58.060001  33.430000  54.709999  61.930000   
74  705.0  ...   352.0  54.410000  54.779999  40.340000  55.310001  61.669998   
75  225.0  ...   353.0  42.250000  43.169998  55.599998  33.259998  78.500000   
76  828.0  ...   353.0  52.389999  57.230000  36.810001  51.470001  65.139999   
77  200.0  ...   342.0  52.970001  59.150002  42.290001  57

PRODUCT_CODE    X_128    X_129  X_132  X_133  X_134  X_135  X_136  X_137  \
54             1   7830.0   7830.0   0.19   0.20   0.19    0.2  228.0  228.0   
55             1  16654.0  16654.0   0.20   0.21   0.20    0.2  550.0  550.0   
56             1  25564.0  25564.0   0.20   0.21   0.20    0.2  844.0  844.0   
57             1   1009.0   1009.0   0.20   0.21   0.19    0.2   50.0   50.0   
58             1   6065.0  13248.0   0.19   0.20   0.19    0.2  156.0  156.0   
59             1   7827.0   7827.0   0.19   0.20   0.19    0.2  228.0  228.0   
60             1   2932.0   2932.0   0.20   0.21   0.20    0.2  123.0  123.0   
61             1   7832.0   7832.0   0.19   0.20   0.19    0.2  228.0  228.0   
62             1   9401.0   9401.0   0.19   0.20   0.19    0.2  191.0  191.0   
63             1   7820.0   7820.0   0.19   0.20   0.19    0.2  228.0  228.0   
64             1   7825.0   7825.0   0.19   0.20   0.19    0.2  228.0  228.0   
65             1  26581.0  26581.0   0.20   0.21   0.20    0.2  874.0  874.0   
66             1   8207.0   8207.0   0.19   0.20   0.19    0.2  172.0  172.0   
67             1   9445.0   9445.0   0.19   0.20   0.19    0.2  192.0  192.0   
68             1  14810.0  14810.0   0.19   0.20   0.19    0.2  304.0  304.0   
69             1  13369.0  13369.0   0.20   0.21   0.19    0.2  458.0  458.0   
70             1    837.0    837.0   0.19   0.20   0.19    0.2   32.0   32.0   
71             1   5595.0   5595.0   0.20   0.21   0.20    0.2  200.0  200.0   
72             1   2947.0   2947.0   0.20   0.21   0.19    0.2  123.0  123.0   
73             1  22242.0  22242.0   0.20   0.21   0.20    0.2  717.0  717.0   
74             1  21873.0  21873.0   0.19   0.21   0.19    0.2  705.0  705.0   
75             1   7822.0   7822.0   0.19   0.20   0.19    0.2  228.0  228.0   
76             1  25105.0  25105.0   0.20   0.21   0.20    0.2  827.0  827.0   
77             1   5580.0   5580.0   0.19   0.21   0.19    0.2  200.0  200.0   

    X_138  ...  X_2865     X_2866     X_2867     X_2868     X_2869     X_2870  \
54  225.0  ...   352.0  40.419998  38.330002  40.139999  30.719999  76.519997   
55  550.0  ...   353.0  56.119999  61.099998  50.220001  55.529999  66.860001   
56  845.0  ...   353.0  55.540001  52.660000  59.680000  52.990002  63.160000   
57   50.0  ...   353.0  49.490002  55.590000  40.490002  53.840000  66.470001   
58  156.0  ...   353.0  55.049999  59.299999  54.570000  56.139999  64.830002   
59  225.0  ...   352.0  36.549999  32.320000  54.250000  35.150002  78.860001   
60  123.0  ...   353.0  56.860001  50.459999  40.490002  57.340000  66.370003   
61  225.0  ...   353.0  40.529999  31.700001  49.490002  35.730000  79.750000   
62  191.0  ...   352.0  52.650002  58.950001  41.009998  58.430000  64.459999   
63  225.0  ...   353.0  32.500000  41.419998  38.360001  30.830000  76.930000   
64  225.0  ...   352.0  32.119999  34.740002  54.930000  33.160000  76.300003   
65  874.0  ...   345.0  54.900002  61.299999  54.060001  59.930000  62.610001   
66  172.0  ...   343.0  57.939999  55.840000  53.240002  56.720001  64.169998   
67  192.0  ...   350.0  53.810001  51.840000  59.369999  57.630001  66.250000   
68  304.0  ...   353.0  49.470001  53.070000  50.889999  55.099998  66.489998   
69  458.0  ...   352.0  54.759998  54.930000  59.680000  56.779999  64.680000   
70   32.0  ...   353.0  53.490002  58.759998  42.220001  57.919998  66.180000   
71  200.0  ...   352.0  51.557312  54.230148  48.665222  52.332539  66.685966   
72  123.0  ...   352.0  48.279999  51.250000  55.430000  56.950001  67.440002   
73  717.0  ...   353.0  53.490002  58.060001  33.430000  54.709999  61.930000   
74  705.0  ...   352.0  54.410000  54.779999  40.340000  55.310001  61.669998   
75  225.0  ...   353.0  42.250000  43.169998  55.599998  33.259998  78.500000   
76  828.0  ...   353.0  52.389999  57.230000  36.810001  51.470001  65.139999   
77  200.0  ...   342.0  52.970001  59.150002  42.290001  57

PRODUCT_CODE    X_128    X_129  X_132  X_133  X_134  X_135  X_136  X_137  \
54             1   7830.0   7830.0   0.19   0.20   0.19    0.2  228.0  228.0   
55             1  16654.0  16654.0   0.20   0.21   0.20    0.2  550.0  550.0   
56             1  25564.0  25564.0   0.20   0.21   0.20    0.2  844.0  844.0   
57             1   1009.0   1009.0   0.20   0.21   0.19    0.2   50.0   50.0   
58             1   6065.0  13248.0   0.19   0.20   0.19    0.2  156.0  156.0   
59             1   7827.0   7827.0   0.19   0.20   0.19    0.2  228.0  228.0   
60             1   2932.0   2932.0   0.20   0.21   0.20    0.2  123.0  123.0   
61             1   7832.0   7832.0   0.19   0.20   0.19    0.2  228.0  228.0   
62             1   9401.0   9401.0   0.19   0.20   0.19    0.2  191.0  191.0   
63             1   7820.0   7820.0   0.19   0.20   0.19    0.2  228.0  228.0   
64             1   7825.0   7825.0   0.19   0.20   0.19    0.2  228.0  228.0   
65             1  26581.0  26581.0   0.20   0.21   0.20    0.2  874.0  874.0   
66             1   8207.0   8207.0   0.19   0.20   0.19    0.2  172.0  172.0   
67             1   9445.0   9445.0   0.19   0.20   0.19    0.2  192.0  192.0   
68             1  14810.0  14810.0   0.19   0.20   0.19    0.2  304.0  304.0   
69             1  13369.0  13369.0   0.20   0.21   0.19    0.2  458.0  458.0   
70             1    837.0    837.0   0.19   0.20   0.19    0.2   32.0   32.0   
71             1   5595.0   5595.0   0.20   0.21   0.20    0.2  200.0  200.0   
72             1   2947.0   2947.0   0.20   0.21   0.19    0.2  123.0  123.0   
73             1  22242.0  22242.0   0.20   0.21   0.20    0.2  717.0  717.0   
74             1  21873.0  21873.0   0.19   0.21   0.19    0.2  705.0  705.0   
75             1   7822.0   7822.0   0.19   0.20   0.19    0.2  228.0  228.0   
76             1  25105.0  25105.0   0.20   0.21   0.20    0.2  827.0  827.0   
77             1   5580.0   5580.0   0.19   0.21   0.19    0.2  200.0  200.0   

    X_138  ...  X_2865     X_2866     X_2867     X_2868     X_2869     X_2870  \
54  225.0  ...   352.0  40.419998  38.330002  40.139999  30.719999  76.519997   
55  550.0  ...   353.0  56.119999  61.099998  50.220001  55.529999  66.860001   
56  845.0  ...   353.0  55.540001  52.660000  59.680000  52.990002  63.160000   
57   50.0  ...   353.0  49.490002  55.590000  40.490002  53.840000  66.470001   
58  156.0  ...   353.0  55.049999  59.299999  54.570000  56.139999  64.830002   
59  225.0  ...   352.0  36.549999  32.320000  54.250000  35.150002  78.860001   
60  123.0  ...   353.0  56.860001  50.459999  40.490002  57.340000  66.370003   
61  225.0  ...   353.0  40.529999  31.700001  49.490002  35.730000  79.750000   
62  191.0  ...   352.0  52.650002  58.950001  41.009998  58.430000  64.459999   
63  225.0  ...   353.0  32.500000  41.419998  38.360001  30.830000  76.930000   
64  225.0  ...   352.0  32.119999  34.740002  54.930000  33.160000  76.300003   
65  874.0  ...   345.0  54.900002  61.299999  54.060001  59.930000  62.610001   
66  172.0  ...   343.0  57.939999  55.840000  53.240002  56.720001  64.169998   
67  192.0  ...   350.0  53.810001  51.840000  59.369999  57.630001  66.250000   
68  304.0  ...   353.0  49.470001  53.070000  50.889999  55.099998  66.489998   
69  458.0  ...   352.0  54.759998  54.930000  59.680000  56.779999  64.680000   
70   32.0  ...   353.0  53.490002  58.759998  42.220001  57.919998  66.180000   
71  200.0  ...   352.0  51.557312  54.230148  48.665222  52.332539  66.685966   
72  123.0  ...   352.0  48.279999  51.250000  55.430000  56.950001  67.440002   
73  717.0  ...   353.0  53.490002  58.060001  33.430000  54.709999  61.930000   
74  705.0  ...   352.0  54.410000  54.779999  40.340000  55.310001  61.669998   
75  225.0  ...   353.0  42.250000  43.169998  55.599998  33.259998  78.500000   
76  828.0  ...   353.0  52.389999  57.230000  36.810001  51.470001  65.139999   
77  200.0  ...   342.0  52.970001  59.150002  42.290001  57

PRODUCT_CODE    X_128    X_129  X_132  X_133  X_134  X_135  X_136  X_137  \
54             1   7830.0   7830.0   0.19   0.20   0.19    0.2  228.0  228.0   
55             1  16654.0  16654.0   0.20   0.21   0.20    0.2  550.0  550.0   
56             1  25564.0  25564.0   0.20   0.21   0.20    0.2  844.0  844.0   
57             1   1009.0   1009.0   0.20   0.21   0.19    0.2   50.0   50.0   
58             1   6065.0  13248.0   0.19   0.20   0.19    0.2  156.0  156.0   
59             1   7827.0   7827.0   0.19   0.20   0.19    0.2  228.0  228.0   
60             1   2932.0   2932.0   0.20   0.21   0.20    0.2  123.0  123.0   
61             1   7832.0   7832.0   0.19   0.20   0.19    0.2  228.0  228.0   
62             1   9401.0   9401.0   0.19   0.20   0.19    0.2  191.0  191.0   
63             1   7820.0   7820.0   0.19   0.20   0.19    0.2  228.0  228.0   
64             1   7825.0   7825.0   0.19   0.20   0.19    0.2  228.0  228.0   
65             1  26581.0  26581.0   0.20   0.21   0.20    0.2  874.0  874.0   
66             1   8207.0   8207.0   0.19   0.20   0.19    0.2  172.0  172.0   
67             1   9445.0   9445.0   0.19   0.20   0.19    0.2  192.0  192.0   
68             1  14810.0  14810.0   0.19   0.20   0.19    0.2  304.0  304.0   
69             1  13369.0  13369.0   0.20   0.21   0.19    0.2  458.0  458.0   
70             1    837.0    837.0   0.19   0.20   0.19    0.2   32.0   32.0   
71             1   5595.0   5595.0   0.20   0.21   0.20    0.2  200.0  200.0   
72             1   2947.0   2947.0   0.20   0.21   0.19    0.2  123.0  123.0   
73             1  22242.0  22242.0   0.20   0.21   0.20    0.2  717.0  717.0   
74             1  21873.0  21873.0   0.19   0.21   0.19    0.2  705.0  705.0   
75             1   7822.0   7822.0   0.19   0.20   0.19    0.2  228.0  228.0   
76             1  25105.0  25105.0   0.20   0.21   0.20    0.2  827.0  827.0   
77             1   5580.0   5580.0   0.19   0.21   0.19    0.2  200.0  200.0   

    X_138  ...  X_2865     X_2866     X_2867     X_2868     X_2869     X_2870  \
54  225.0  ...   352.0  40.419998  38.330002  40.139999  30.719999  76.519997   
55  550.0  ...   353.0  56.119999  61.099998  50.220001  55.529999  66.860001   
56  845.0  ...   353.0  55.540001  52.660000  59.680000  52.990002  63.160000   
57   50.0  ...   353.0  49.490002  55.590000  40.490002  53.840000  66.470001   
58  156.0  ...   353.0  55.049999  59.299999  54.570000  56.139999  64.830002   
59  225.0  ...   352.0  36.549999  32.320000  54.250000  35.150002  78.860001   
60  123.0  ...   353.0  56.860001  50.459999  40.490002  57.340000  66.370003   
61  225.0  ...   353.0  40.529999  31.700001  49.490002  35.730000  79.750000   
62  191.0  ...   352.0  52.650002  58.950001  41.009998  58.430000  64.459999   
63  225.0  ...   353.0  32.500000  41.419998  38.360001  30.830000  76.930000   
64  225.0  ...   352.0  32.119999  34.740002  54.930000  33.160000  76.300003   
65  874.0  ...   345.0  54.900002  61.299999  54.060001  59.930000  62.610001   
66  172.0  ...   343.0  57.939999  55.840000  53.240002  56.720001  64.169998   
67  192.0  ...   350.0  53.810001  51.840000  59.369999  57.630001  66.250000   
68  304.0  ...   353.0  49.470001  53.070000  50.889999  55.099998  66.489998   
69  458.0  ...   352.0  54.759998  54.930000  59.680000  56.779999  64.680000   
70   32.0  ...   353.0  53.490002  58.759998  42.220001  57.919998  66.180000   
71  200.0  ...   352.0  51.557312  54.230148  48.665222  52.332539  66.685966   
72  123.0  ...   352.0  48.279999  51.250000  55.430000  56.950001  67.440002   
73  717.0  ...   353.0  53.490002  58.060001  33.430000  54.709999  61.930000   
74  705.0  ...   352.0  54.410000  54.779999  40.340000  55.310001  61.669998   
75  225.0  ...   353.0  42.250000  43.169998  55.599998  33.259998  78.500000   
76  828.0  ...   353.0  52.389999  57.230000  36.810001  51.470001  65.139999   
77  200.0  ...   342.0  52.970001  59.150002  42.290001  57

PRODUCT_CODE    X_128    X_129  X_132  X_133  X_134  X_135  X_136  X_137  \
54             1   7830.0   7830.0   0.19   0.20   0.19    0.2  228.0  228.0   
55             1  16654.0  16654.0   0.20   0.21   0.20    0.2  550.0  550.0   
56             1  25564.0  25564.0   0.20   0.21   0.20    0.2  844.0  844.0   
57             1   1009.0   1009.0   0.20   0.21   0.19    0.2   50.0   50.0   
58             1   6065.0  13248.0   0.19   0.20   0.19    0.2  156.0  156.0   
59             1   7827.0   7827.0   0.19   0.20   0.19    0.2  228.0  228.0   
60             1   2932.0   2932.0   0.20   0.21   0.20    0.2  123.0  123.0   
61             1   7832.0   7832.0   0.19   0.20   0.19    0.2  228.0  228.0   
62             1   9401.0   9401.0   0.19   0.20   0.19    0.2  191.0  191.0   
63             1   7820.0   7820.0   0.19   0.20   0.19    0.2  228.0  228.0   
64             1   7825.0   7825.0   0.19   0.20   0.19    0.2  228.0  228.0   
65             1  26581.0  26581.0   0.20   0.21   0.20    0.2  874.0  874.0   
66             1   8207.0   8207.0   0.19   0.20   0.19    0.2  172.0  172.0   
67             1   9445.0   9445.0   0.19   0.20   0.19    0.2  192.0  192.0   
68             1  14810.0  14810.0   0.19   0.20   0.19    0.2  304.0  304.0   
69             1  13369.0  13369.0   0.20   0.21   0.19    0.2  458.0  458.0   
70             1    837.0    837.0   0.19   0.20   0.19    0.2   32.0   32.0   
71             1   5595.0   5595.0   0.20   0.21   0.20    0.2  200.0  200.0   
72             1   2947.0   2947.0   0.20   0.21   0.19    0.2  123.0  123.0   
73             1  22242.0  22242.0   0.20   0.21   0.20    0.2  717.0  717.0   
74             1  21873.0  21873.0   0.19   0.21   0.19    0.2  705.0  705.0   
75             1   7822.0   7822.0   0.19   0.20   0.19    0.2  228.0  228.0   
76             1  25105.0  25105.0   0.20   0.21   0.20    0.2  827.0  827.0   
77             1   5580.0   5580.0   0.19   0.21   0.19    0.2  200.0  200.0   

    X_138  ...  X_2865     X_2866     X_2867     X_2868     X_2869     X_2870  \
54  225.0  ...   352.0  40.419998  38.330002  40.139999  30.719999  76.519997   
55  550.0  ...   353.0  56.119999  61.099998  50.220001  55.529999  66.860001   
56  845.0  ...   353.0  55.540001  52.660000  59.680000  52.990002  63.160000   
57   50.0  ...   353.0  49.490002  55.590000  40.490002  53.840000  66.470001   
58  156.0  ...   353.0  55.049999  59.299999  54.570000  56.139999  64.830002   
59  225.0  ...   352.0  36.549999  32.320000  54.250000  35.150002  78.860001   
60  123.0  ...   353.0  56.860001  50.459999  40.490002  57.340000  66.370003   
61  225.0  ...   353.0  40.529999  31.700001  49.490002  35.730000  79.750000   
62  191.0  ...   352.0  52.650002  58.950001  41.009998  58.430000  64.459999   
63  225.0  ...   353.0  32.500000  41.419998  38.360001  30.830000  76.930000   
64  225.0  ...   352.0  32.119999  34.740002  54.930000  33.160000  76.300003   
65  874.0  ...   345.0  54.900002  61.299999  54.060001  59.930000  62.610001   
66  172.0  ...   343.0  57.939999  55.840000  53.240002  56.720001  64.169998   
67  192.0  ...   350.0  53.810001  51.840000  59.369999  57.630001  66.250000   
68  304.0  ...   353.0  49.470001  53.070000  50.889999  55.099998  66.489998   
69  458.0  ...   352.0  54.759998  54.930000  59.680000  56.779999  64.680000   
70   32.0  ...   353.0  53.490002  58.759998  42.220001  57.919998  66.180000   
71  200.0  ...   352.0  51.557312  54.230148  48.665222  52.332539  66.685966   
72  123.0  ...   352.0  48.279999  51.250000  55.430000  56.950001  67.440002   
73  717.0  ...   353.0  53.490002  58.060001  33.430000  54.709999  61.930000   
74  705.0  ...   352.0  54.410000  54.779999  40.340000  55.310001  61.669998   
75  225.0  ...   353.0  42.250000  43.169998  55.599998  33.259998  78.500000   
76  828.0  ...   353.0  52.389999  57.230000  36.810001  51.470001  65.139999   
77  200.0  ...   342.0  52.970001  59.150002  42.290001  57

PRODUCT_CODE    X_128    X_129  X_132  X_133  X_134  X_135  X_136  X_137  \
54             1   7830.0   7830.0   0.19   0.20   0.19    0.2  228.0  228.0   
55             1  16654.0  16654.0   0.20   0.21   0.20    0.2  550.0  550.0   
56             1  25564.0  25564.0   0.20   0.21   0.20    0.2  844.0  844.0   
57             1   1009.0   1009.0   0.20   0.21   0.19    0.2   50.0   50.0   
58             1   6065.0  13248.0   0.19   0.20   0.19    0.2  156.0  156.0   
59             1   7827.0   7827.0   0.19   0.20   0.19    0.2  228.0  228.0   
60             1   2932.0   2932.0   0.20   0.21   0.20    0.2  123.0  123.0   
61             1   7832.0   7832.0   0.19   0.20   0.19    0.2  228.0  228.0   
62             1   9401.0   9401.0   0.19   0.20   0.19    0.2  191.0  191.0   
63             1   7820.0   7820.0   0.19   0.20   0.19    0.2  228.0  228.0   
64             1   7825.0   7825.0   0.19   0.20   0.19    0.2  228.0  228.0   
65             1  26581.0  26581.0   0.20   0.21   0.20    0.2  874.0  874.0   
66             1   8207.0   8207.0   0.19   0.20   0.19    0.2  172.0  172.0   
67             1   9445.0   9445.0   0.19   0.20   0.19    0.2  192.0  192.0   
68             1  14810.0  14810.0   0.19   0.20   0.19    0.2  304.0  304.0   
69             1  13369.0  13369.0   0.20   0.21   0.19    0.2  458.0  458.0   
70             1    837.0    837.0   0.19   0.20   0.19    0.2   32.0   32.0   
71             1   5595.0   5595.0   0.20   0.21   0.20    0.2  200.0  200.0   
72             1   2947.0   2947.0   0.20   0.21   0.19    0.2  123.0  123.0   
73             1  22242.0  22242.0   0.20   0.21   0.20    0.2  717.0  717.0   
74             1  21873.0  21873.0   0.19   0.21   0.19    0.2  705.0  705.0   
75             1   7822.0   7822.0   0.19   0.20   0.19    0.2  228.0  228.0   
76             1  25105.0  25105.0   0.20   0.21   0.20    0.2  827.0  827.0   
77             1   5580.0   5580.0   0.19   0.21   0.19    0.2  200.0  200.0   

    X_138  ...  X_2865     X_2866     X_2867     X_2868     X_2869     X_2870  \
54  225.0  ...   352.0  40.419998  38.330002  40.139999  30.719999  76.519997   
55  550.0  ...   353.0  56.119999  61.099998  50.220001  55.529999  66.860001   
56  845.0  ...   353.0  55.540001  52.660000  59.680000  52.990002  63.160000   
57   50.0  ...   353.0  49.490002  55.590000  40.490002  53.840000  66.470001   
58  156.0  ...   353.0  55.049999  59.299999  54.570000  56.139999  64.830002   
59  225.0  ...   352.0  36.549999  32.320000  54.250000  35.150002  78.860001   
60  123.0  ...   353.0  56.860001  50.459999  40.490002  57.340000  66.370003   
61  225.0  ...   353.0  40.529999  31.700001  49.490002  35.730000  79.750000   
62  191.0  ...   352.0  52.650002  58.950001  41.009998  58.430000  64.459999   
63  225.0  ...   353.0  32.500000  41.419998  38.360001  30.830000  76.930000   
64  225.0  ...   352.0  32.119999  34.740002  54.930000  33.160000  76.300003   
65  874.0  ...   345.0  54.900002  61.299999  54.060001  59.930000  62.610001   
66  172.0  ...   343.0  57.939999  55.840000  53.240002  56.720001  64.169998   
67  192.0  ...   350.0  53.810001  51.840000  59.369999  57.630001  66.250000   
68  304.0  ...   353.0  49.470001  53.070000  50.889999  55.099998  66.489998   
69  458.0  ...   352.0  54.759998  54.930000  59.680000  56.779999  64.680000   
70   32.0  ...   353.0  53.490002  58.759998  42.220001  57.919998  66.180000   
71  200.0  ...   352.0  51.557312  54.230148  48.665222  52.332539  66.685966   
72  123.0  ...   352.0  48.279999  51.250000  55.430000  56.950001  67.440002   
73  717.0  ...   353.0  53.490002  58.060001  33.430000  54.709999  61.930000   
74  705.0  ...   352.0  54.410000  54.779999  40.340000  55.310001  61.669998   
75  225.0  ...   353.0  42.250000  43.169998  55.599998  33.259998  78.500000   
76  828.0  ...   353.0  52.389999  57.230000  36.810001  51.470001  65.139999   
77  200.0  ...   342.0  52.970001  59.150002  42.290001  57

In [196]:
T050304_final_classification_model = finalize_model(T050304_model_et)

In [197]:
T050304_prediction = predict_model(T050304_final_classification_model, data=T050304_data)
#prediction.drop(['Y_Quality'], axis = 1, inplace = True)

In [198]:
T050304_prediction

PRODUCT_CODE    X_128    X_129  X_132  X_133  X_134  X_135  X_136  X_137  \
0              1   7813.0   7813.0   0.19    0.2   0.19    0.2  228.0  228.0   
1              1   7815.0   7815.0   0.19    0.2   0.19    0.2  228.0  228.0   
2              1   7817.0   7817.0   0.19    0.2   0.18    0.2  228.0  228.0   
3              1   7820.0   7820.0   0.19    0.2   0.19    0.2  228.0  228.0   
4              1   7822.0   7822.0   0.19    0.2   0.19    0.2  228.0  228.0   
..           ...      ...      ...    ...    ...    ...    ...    ...    ...   
73             1  11864.0  11864.0   0.19    0.2   0.19    0.2  230.0  230.0   
74             1  11898.0  11898.0   0.18    0.2   0.18    0.2  230.0  230.0   
75             1  11920.0  11920.0   0.19    0.2   0.19    0.2  230.0  230.0   
76             1  14810.0  14810.0   0.19    0.2   0.19    0.2  304.0  304.0   
77             1  14813.0  14813.0   0.19    0.2   0.19    0.2  304.0  304.0   

    X_138  ...      X_2864  X_2865     X_2866     X_2867     X_2868  \
0   225.0  ...  368.296295   353.0  39.340000  40.889999  32.560001   
1   225.0  ...  367.320740   353.0  39.189999  36.650002  42.470001   
2   225.0  ...  367.351837   352.0  38.700001  41.889999  46.930000   
3   225.0  ...  368.425934   353.0  32.500000  41.419998  38.360001   
4   225.0  ...  373.500000   353.0  42.250000  43.169998  55.599998   
..    ...  ...         ...     ...        ...        ...        ...   
73  230.0  ...  367.333344   352.0  51.557312  54.230148  48.665222   
74  230.0  ...  367.037048   352.0  50.880001  53.230000  52.439999   
75  230.0  ...  371.943390   353.0  51.709999  59.639999  54.610001   
76  304.0  ...  369.811310   353.0  49.470001  53.070000  50.889999   
77  304.0  ...  367.018860   352.0  51.557312  54.230148  48.665222   

       X_2869     X_2870  X_2871  prediction_label  prediction_score  
0   34.090000  77.769997     1.0                 1               1.0  
1   36.529999  78.349998     1.0                 1               1.0  
2   33.090000  76.970001     1.0                 1               1.0  
3   30.830000  76.930000     1.0                 1               1.0  
4   33.259998  78.500000     1.0                 1               1.0  
..        ...        ...     ...               ...               ...  
73  52.332539  66.685966     1.0                 0               1.0  
74  56.279999  66.830002     1.0                 0               1.0  
75  57.049999  63.180000     1.0                 0               1.0  
76  55.099998  66.489998     1.0                 0               1.0  
77  52.332539  66.685966     1.0                 0               1.0  

[78 rows x 1971 columns]

# T050307

In [199]:
T050307_class = T050307['Y_Class']
T050307_target = T050307['Y_Quality']
T050307_data = T050307.drop(['Y_Class', 'Y_Quality'], axis = 1)
T050307_data

PRODUCT_CODE    X_130    X_131  X_132  X_133  X_134  X_135  X_136  X_137  \
1               1  19854.0  19854.0   0.20   0.21   0.20    0.2  413.0  414.0   
3               1  19856.0  19856.0   0.20   0.21   0.20    0.2  414.0  414.0   
5               1  19859.0  19859.0   0.20   0.21   0.20    0.2  414.0  414.0   
7               1  19861.0  19861.0   0.20   0.21   0.20    0.2  414.0  414.0   
9               1  19864.0  19864.0   0.20   0.21   0.20    0.2  414.0  414.0   
11              1  19866.0  19866.0   0.20   0.21   0.20    0.2  414.0  414.0   
13              1  19869.0  19869.0   0.20   0.21   0.20    0.2  414.0  414.0   
15              1  19871.0  19871.0   0.20   0.21   0.20    0.2  414.0  414.0   
17              1  19874.0  19874.0   0.20   0.21   0.20    0.2  414.0  414.0   
19              1  19876.0  19876.0   0.20   0.21   0.20    0.2  414.0  414.0   
24              1  22589.0  22589.0   0.20   0.21   0.20    0.2  504.0  499.0   
35              1  26155.0  26155.0   0.20   0.21   0.20    0.2  618.0  612.0   
81              1   6473.0   6473.0   0.20   0.21   0.20    0.2  171.0  171.0   
82              1   6482.0   6482.0   0.20   0.21   0.20    0.2  172.0  172.0   
187             1  19631.0  19631.0   0.20   0.21   0.19    0.2  609.0  609.0   
195             1  20594.0  20594.0   0.20   0.21   0.20    0.2  633.0  633.0   
198             1  21289.0  21289.0   0.20   0.21   0.19    0.2  646.0  646.0   
256             1  25395.0  25395.0   0.20   0.21   0.20    0.2  760.0  760.0   
261             1  26126.0  26126.0   0.19   0.21   0.19    0.2  779.0  779.0   
296             1   1055.0   1055.0   0.20   0.21   0.20    0.2   50.0   52.0   
298             1   1102.0   1102.0   0.19   0.21   0.19    0.2   50.0   52.0   
307             1   1232.0   1232.0   0.20   0.21   0.20    0.2   58.0   59.0   
316             1   1561.0   1561.0   0.20   0.21   0.20    0.2   67.0   69.0   
336             1   2705.0   2705.0   0.20   0.21   0.20    0.2  119.0  121.0   
355             1   3699.0   3699.0   0.20   0.21   0.20    0.2  157.0  159.0   
356             1   3704.0   3704.0   0.20   0.21   0.20    0.2  157.0  159.0   
369             1   4446.0   4446.0   0.20   0.21   0.20    0.2  178.0  180.0   
432             1  10545.0  10545.0   0.20   0.21   0.20    0.2  349.0  351.0   
444             1  11538.0  11538.0   0.20   0.21   0.20    0.2  376.0  378.0   
454             1  11942.0  11942.0   0.20   0.21   0.20    0.2  394.0  396.0   
477             1  13975.0  13975.0   0.20   0.21   0.20    0.2  449.0  451.0   
541             1    806.0    806.0   0.19   0.21   0.19    0.2   58.0   58.0   
542             1    829.0    829.0   0.19   0.20   0.19    0.2   58.0   58.0   
543             1    851.0    851.0   0.19   0.21   0.19    0.2   59.0   59.0   
544             1    874.0    874.0   0.19   0.21   0.19    0.2   59.0   59.0   
545             1    896.0    896.0   0.19   0.21   0.19    0.2   59.0   59.0   
546             1    919.0    919.0   0.19   0.21   0.19    0.2   59.0   59.0   
549             1   2248.0   2248.0   0.19   0.20   0.19    0.2   81.0   81.0   
550             1   2278.0   2278.0   0.19   0.20   0.19    0.2   82.0   82.0   
551             1   2407.0   2407.0   0.19   0.20   0.19    0.2   84.0   84.0   
552             1   2446.0   2446.0   0.19   0.20   0.19    0.2   84.0   84.0   
555             1   2540.0   2540.0   0.19   0.20   0.19    0.2   87.0   87.0   

     X_138  ...  X_2862  X_2863      X_2864  X_2865     X_2866     X_2867  \
1    414.0  ...   185.6   383.0  367.735849   353.0  38.890000  42.820000   
3    414.0  ...   165.8   384.0  369.188679   353.0  37.740000  39.170000   
5    414.0  ...   184.7   384.0  368.622641   352.0  38.160000  51.250000   
7    414.0  ...   173.8   393.0  370.283019   353.0  39.000000  35.950000   
9    414.0  ...   167.2   393.0  372.870370   353.0  34.400000  35.880000   
11   414.0  ...   166.1   394.0  374.425926   352.0  39.160

In [200]:
from pycaret.classification import *
# 분류 패키지의 모든 모듈을 임포트한다.
exp_clf101 = setup(data=T050307_data, 
                   target=T050307_class, 
                   fold=5,
                   session_id=414)
top5 = compare_models(sort='Accuracy', n_select=5)

Processing:   0%|          | 0/73 [00:00<?, ?it/s]

In [201]:
T050307_total_models = []

T050307_model_rf = create_model('rf', fold = 5)
T050307_total_models.append(T050307_model_rf)

T050307_model_gbc = create_model('gbc', fold = 5)
T050307_total_models.append(T050307_model_gbc)

T050307_model_ada = create_model('ada', fold = 5)
T050307_total_models.append(T050307_model_ada)

T050307_model_catboost = create_model('catboost', fold = 5)
T050307_total_models.append(T050307_model_catboost)

T050307_model_xgb = create_model('xgboost', fold = 5)
T050307_total_models.append(T050307_model_xgb)

T050307_model_lightgbm = create_model('lightgbm', fold = 5)
T050307_total_models.append(T050307_model_lightgbm)

T050307_model_et = create_model('et', fold = 5)
T050307_total_models.append(T050307_model_et)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [202]:
T050307_model_rf = tune_model(T050307_model_rf, fold=5, choose_better = True)

T050307_model_gbc = tune_model(T050307_model_gbc, fold=5, choose_better = True)

T050307_model_ada = tune_model(T050307_model_ada, fold=5, choose_better = True)

T050307_model_catboost = tune_model(T050307_model_catboost, fold=5, choose_better = True)

T050307_model_xgb = tune_model(T050307_model_xgb, fold=5, choose_better = True)

T050307_model_lightgbm = tune_model(T050307_model_lightgbm, fold=5, choose_better = True)

T050307_model_et = tune_model(T050307_model_et, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


In [203]:
T050307_tuned_models = [T050307_model_rf, T050307_model_gbc, T050307_model_ada, T050307_model_catboost, T050307_model_xgb, T050307_model_lightgbm, T050307_model_et]
T050307_tuned_models

[RandomForestClassifier(bootstrap=True, ccp_alpha=0.0, class_weight='balanced',
                        criterion='entropy', max_depth=6, max_features=1.0,
                        max_leaf_nodes=None, max_samples=None,
                        min_impurity_decrease=0.02, min_samples_leaf=6,
                        min_samples_split=10, min_weight_fraction_leaf=0.0,
                        n_estimators=140, n_jobs=-1, oob_score=False,
                        random_state=414, verbose=0, warm_start=False),
 GradientBoostingClassifier(ccp_alpha=0.0, criterion='friedman_mse', init=None,
                            learning_rate=0.2, loss='deviance', max_depth=1,
                            max_features='sqrt', max_leaf_nodes=None,
                            min_impurity_decrease=0.002, min_samples_leaf=1,
                            min_samples_split=7, min_weight_fraction_leaf=0.0,
                            n_estimators=110, n_iter_no_change=None,
                            random_stat

In [204]:
for model in T050307_tuned_models:
    display(predict_model(model))

PRODUCT_CODE    X_130    X_131  X_132  X_133  X_134  X_135  X_136  X_137  \
29             1  20594.0  20594.0   0.20   0.21   0.20    0.2  633.0  633.0   
30             1  11942.0  11942.0   0.20   0.21   0.20    0.2  394.0  396.0   
31             1    919.0    919.0   0.19   0.21   0.19    0.2   59.0   59.0   
32             1  26126.0  26126.0   0.19   0.21   0.19    0.2  779.0  779.0   
33             1   2446.0   2446.0   0.19   0.20   0.19    0.2   84.0   84.0   
34             1  19866.0  19866.0   0.20   0.21   0.20    0.2  414.0  414.0   
35             1    806.0    806.0   0.19   0.21   0.19    0.2   58.0   58.0   
36             1  19856.0  19856.0   0.20   0.21   0.20    0.2  414.0  414.0   
37             1   1102.0   1102.0   0.19   0.21   0.19    0.2   50.0   52.0   
38             1   3699.0   3699.0   0.20   0.21   0.20    0.2  157.0  159.0   
39             1  10545.0  10545.0   0.20   0.21   0.20    0.2  349.0  351.0   
40             1  19871.0  19871.0   0.20   0.21   0.20    0.2  414.0  414.0   
41             1  21289.0  21289.0   0.20   0.21   0.19    0.2  646.0  646.0   

    X_138  ...  X_2865     X_2866     X_2867     X_2868     X_2869     X_2870  \
29  633.0  ...   353.0  49.284546  52.343941  51.516666  50.293938  66.576057   
30  396.0  ...   352.0  55.689999  53.029999  53.750000  58.959999  64.010002   
31   59.0  ...   352.0  53.169998  53.220001  50.070000  57.130001  64.269997   
32  779.0  ...   352.0  44.040001  60.240002  59.639999  57.340000  65.860001   
33   84.0  ...   352.0  53.639999  58.900002  49.849998  57.660000  63.139999   
34  414.0  ...   352.0  39.160000  35.490002  52.270000  31.450001  72.459999   
35   58.0  ...   353.0  53.369999  58.320000  49.099998  53.290001  62.480000   
36  414.0  ...   353.0  37.740002  39.169998  52.169998  30.580000  71.779999   
37   52.0  ...   352.0  50.820000  61.500000  56.619999  57.869999  67.220001   
38  159.0  ...   354.0  53.450001  57.770000  41.880001  53.930000  63.400002   
39  351.0  ...   352.0  55.400002  59.570000  42.580002  57.580002  64.900002   
40  414.0  ...   353.0  38.029999  44.529999  41.540001  37.200001  72.459999   
41  646.0  ...   353.0  53.270000  56.009998  59.470001  58.889999  65.269997   

    X_2871  Y_Class  prediction_label  prediction_score  
29     1.0        2                 2            0.6045  
30     1.0        1                 2            0.4173  
31     1.0        0                 0            0.6092  
32     1.0        2                 2            0.6471  
33     1.0        1                 1            0.4471  
34     1.0        2                 2            0.7918  
35     1.0        0                 0            0.6091  
36     1.0        2                 2            0.5926  
37     1.0        0                 0            0.4462  
38     1.0        2                 2            0.6325  
39     1.0        1                 1            0.5300  
40     1.0        2                 2            0.8197  
41     1.0        2                 2            0.5707  

[13 rows x 1979 columns]

PRODUCT_CODE    X_130    X_131  X_132  X_133  X_134  X_135  X_136  X_137  \
29             1  20594.0  20594.0   0.20   0.21   0.20    0.2  633.0  633.0   
30             1  11942.0  11942.0   0.20   0.21   0.20    0.2  394.0  396.0   
31             1    919.0    919.0   0.19   0.21   0.19    0.2   59.0   59.0   
32             1  26126.0  26126.0   0.19   0.21   0.19    0.2  779.0  779.0   
33             1   2446.0   2446.0   0.19   0.20   0.19    0.2   84.0   84.0   
34             1  19866.0  19866.0   0.20   0.21   0.20    0.2  414.0  414.0   
35             1    806.0    806.0   0.19   0.21   0.19    0.2   58.0   58.0   
36             1  19856.0  19856.0   0.20   0.21   0.20    0.2  414.0  414.0   
37             1   1102.0   1102.0   0.19   0.21   0.19    0.2   50.0   52.0   
38             1   3699.0   3699.0   0.20   0.21   0.20    0.2  157.0  159.0   
39             1  10545.0  10545.0   0.20   0.21   0.20    0.2  349.0  351.0   
40             1  19871.0  19871.0   0.20   0.21   0.20    0.2  414.0  414.0   
41             1  21289.0  21289.0   0.20   0.21   0.19    0.2  646.0  646.0   

    X_138  ...  X_2865     X_2866     X_2867     X_2868     X_2869     X_2870  \
29  633.0  ...   353.0  49.284546  52.343941  51.516666  50.293938  66.576057   
30  396.0  ...   352.0  55.689999  53.029999  53.750000  58.959999  64.010002   
31   59.0  ...   352.0  53.169998  53.220001  50.070000  57.130001  64.269997   
32  779.0  ...   352.0  44.040001  60.240002  59.639999  57.340000  65.860001   
33   84.0  ...   352.0  53.639999  58.900002  49.849998  57.660000  63.139999   
34  414.0  ...   352.0  39.160000  35.490002  52.270000  31.450001  72.459999   
35   58.0  ...   353.0  53.369999  58.320000  49.099998  53.290001  62.480000   
36  414.0  ...   353.0  37.740002  39.169998  52.169998  30.580000  71.779999   
37   52.0  ...   352.0  50.820000  61.500000  56.619999  57.869999  67.220001   
38  159.0  ...   354.0  53.450001  57.770000  41.880001  53.930000  63.400002   
39  351.0  ...   352.0  55.400002  59.570000  42.580002  57.580002  64.900002   
40  414.0  ...   353.0  38.029999  44.529999  41.540001  37.200001  72.459999   
41  646.0  ...   353.0  53.270000  56.009998  59.470001  58.889999  65.269997   

    X_2871  Y_Class  prediction_label  prediction_score  
29     1.0        2                 2            0.8277  
30     1.0        1                 2            0.5725  
31     1.0        0                 0            0.9639  
32     1.0        2                 2            0.9842  
33     1.0        1                 1            0.7514  
34     1.0        2                 2            0.9987  
35     1.0        0                 0            0.9614  
36     1.0        2                 2            0.9955  
37     1.0        0                 0            0.9320  
38     1.0        2                 2            0.9847  
39     1.0        1                 1            0.6150  
40     1.0        2                 2            0.9968  
41     1.0        2                 2            0.9590  

[13 rows x 1979 columns]

PRODUCT_CODE    X_130    X_131  X_132  X_133  X_134  X_135  X_136  X_137  \
29             1  20594.0  20594.0   0.20   0.21   0.20    0.2  633.0  633.0   
30             1  11942.0  11942.0   0.20   0.21   0.20    0.2  394.0  396.0   
31             1    919.0    919.0   0.19   0.21   0.19    0.2   59.0   59.0   
32             1  26126.0  26126.0   0.19   0.21   0.19    0.2  779.0  779.0   
33             1   2446.0   2446.0   0.19   0.20   0.19    0.2   84.0   84.0   
34             1  19866.0  19866.0   0.20   0.21   0.20    0.2  414.0  414.0   
35             1    806.0    806.0   0.19   0.21   0.19    0.2   58.0   58.0   
36             1  19856.0  19856.0   0.20   0.21   0.20    0.2  414.0  414.0   
37             1   1102.0   1102.0   0.19   0.21   0.19    0.2   50.0   52.0   
38             1   3699.0   3699.0   0.20   0.21   0.20    0.2  157.0  159.0   
39             1  10545.0  10545.0   0.20   0.21   0.20    0.2  349.0  351.0   
40             1  19871.0  19871.0   0.20   0.21   0.20    0.2  414.0  414.0   
41             1  21289.0  21289.0   0.20   0.21   0.19    0.2  646.0  646.0   

    X_138  ...  X_2865     X_2866     X_2867     X_2868     X_2869     X_2870  \
29  633.0  ...   353.0  49.284546  52.343941  51.516666  50.293938  66.576057   
30  396.0  ...   352.0  55.689999  53.029999  53.750000  58.959999  64.010002   
31   59.0  ...   352.0  53.169998  53.220001  50.070000  57.130001  64.269997   
32  779.0  ...   352.0  44.040001  60.240002  59.639999  57.340000  65.860001   
33   84.0  ...   352.0  53.639999  58.900002  49.849998  57.660000  63.139999   
34  414.0  ...   352.0  39.160000  35.490002  52.270000  31.450001  72.459999   
35   58.0  ...   353.0  53.369999  58.320000  49.099998  53.290001  62.480000   
36  414.0  ...   353.0  37.740002  39.169998  52.169998  30.580000  71.779999   
37   52.0  ...   352.0  50.820000  61.500000  56.619999  57.869999  67.220001   
38  159.0  ...   354.0  53.450001  57.770000  41.880001  53.930000  63.400002   
39  351.0  ...   352.0  55.400002  59.570000  42.580002  57.580002  64.900002   
40  414.0  ...   353.0  38.029999  44.529999  41.540001  37.200001  72.459999   
41  646.0  ...   353.0  53.270000  56.009998  59.470001  58.889999  65.269997   

    X_2871  Y_Class  prediction_label  prediction_score  
29     1.0        2                 2            0.3806  
30     1.0        1                 2            0.3648  
31     1.0        0                 0            0.3919  
32     1.0        2                 2            0.3765  
33     1.0        1                 0            0.3684  
34     1.0        2                 2            0.3900  
35     1.0        0                 0            0.3919  
36     1.0        2                 1            0.3842  
37     1.0        0                 0            0.3792  
38     1.0        2                 2            0.3882  
39     1.0        1                 1            0.3839  
40     1.0        2                 2            0.3900  
41     1.0        2                 2            0.3747  

[13 rows x 1979 columns]

PRODUCT_CODE    X_130    X_131  X_132  X_133  X_134  X_135  X_136  X_137  \
29             1  20594.0  20594.0   0.20   0.21   0.20    0.2  633.0  633.0   
30             1  11942.0  11942.0   0.20   0.21   0.20    0.2  394.0  396.0   
31             1    919.0    919.0   0.19   0.21   0.19    0.2   59.0   59.0   
32             1  26126.0  26126.0   0.19   0.21   0.19    0.2  779.0  779.0   
33             1   2446.0   2446.0   0.19   0.20   0.19    0.2   84.0   84.0   
34             1  19866.0  19866.0   0.20   0.21   0.20    0.2  414.0  414.0   
35             1    806.0    806.0   0.19   0.21   0.19    0.2   58.0   58.0   
36             1  19856.0  19856.0   0.20   0.21   0.20    0.2  414.0  414.0   
37             1   1102.0   1102.0   0.19   0.21   0.19    0.2   50.0   52.0   
38             1   3699.0   3699.0   0.20   0.21   0.20    0.2  157.0  159.0   
39             1  10545.0  10545.0   0.20   0.21   0.20    0.2  349.0  351.0   
40             1  19871.0  19871.0   0.20   0.21   0.20    0.2  414.0  414.0   
41             1  21289.0  21289.0   0.20   0.21   0.19    0.2  646.0  646.0   

    X_138  ...  X_2865     X_2866     X_2867     X_2868     X_2869     X_2870  \
29  633.0  ...   353.0  49.284546  52.343941  51.516666  50.293938  66.576057   
30  396.0  ...   352.0  55.689999  53.029999  53.750000  58.959999  64.010002   
31   59.0  ...   352.0  53.169998  53.220001  50.070000  57.130001  64.269997   
32  779.0  ...   352.0  44.040001  60.240002  59.639999  57.340000  65.860001   
33   84.0  ...   352.0  53.639999  58.900002  49.849998  57.660000  63.139999   
34  414.0  ...   352.0  39.160000  35.490002  52.270000  31.450001  72.459999   
35   58.0  ...   353.0  53.369999  58.320000  49.099998  53.290001  62.480000   
36  414.0  ...   353.0  37.740002  39.169998  52.169998  30.580000  71.779999   
37   52.0  ...   352.0  50.820000  61.500000  56.619999  57.869999  67.220001   
38  159.0  ...   354.0  53.450001  57.770000  41.880001  53.930000  63.400002   
39  351.0  ...   352.0  55.400002  59.570000  42.580002  57.580002  64.900002   
40  414.0  ...   353.0  38.029999  44.529999  41.540001  37.200001  72.459999   
41  646.0  ...   353.0  53.270000  56.009998  59.470001  58.889999  65.269997   

    X_2871  Y_Class  prediction_label  prediction_score  
29     1.0        2                 2            0.6334  
30     1.0        1                 2            0.4923  
31     1.0        0                 0            0.7345  
32     1.0        2                 2            0.6227  
33     1.0        1                 1            0.4699  
34     1.0        2                 2            0.8333  
35     1.0        0                 0            0.7155  
36     1.0        2                 2            0.5746  
37     1.0        0                 0            0.4299  
38     1.0        2                 2            0.7691  
39     1.0        1                 1            0.4963  
40     1.0        2                 2            0.8467  
41     1.0        2                 2            0.6200  

[13 rows x 1979 columns]

PRODUCT_CODE    X_130    X_131  X_132  X_133  X_134  X_135  X_136  X_137  \
29             1  20594.0  20594.0   0.20   0.21   0.20    0.2  633.0  633.0   
30             1  11942.0  11942.0   0.20   0.21   0.20    0.2  394.0  396.0   
31             1    919.0    919.0   0.19   0.21   0.19    0.2   59.0   59.0   
32             1  26126.0  26126.0   0.19   0.21   0.19    0.2  779.0  779.0   
33             1   2446.0   2446.0   0.19   0.20   0.19    0.2   84.0   84.0   
34             1  19866.0  19866.0   0.20   0.21   0.20    0.2  414.0  414.0   
35             1    806.0    806.0   0.19   0.21   0.19    0.2   58.0   58.0   
36             1  19856.0  19856.0   0.20   0.21   0.20    0.2  414.0  414.0   
37             1   1102.0   1102.0   0.19   0.21   0.19    0.2   50.0   52.0   
38             1   3699.0   3699.0   0.20   0.21   0.20    0.2  157.0  159.0   
39             1  10545.0  10545.0   0.20   0.21   0.20    0.2  349.0  351.0   
40             1  19871.0  19871.0   0.20   0.21   0.20    0.2  414.0  414.0   
41             1  21289.0  21289.0   0.20   0.21   0.19    0.2  646.0  646.0   

    X_138  ...  X_2865     X_2866     X_2867     X_2868     X_2869     X_2870  \
29  633.0  ...   353.0  49.284546  52.343941  51.516666  50.293938  66.576057   
30  396.0  ...   352.0  55.689999  53.029999  53.750000  58.959999  64.010002   
31   59.0  ...   352.0  53.169998  53.220001  50.070000  57.130001  64.269997   
32  779.0  ...   352.0  44.040001  60.240002  59.639999  57.340000  65.860001   
33   84.0  ...   352.0  53.639999  58.900002  49.849998  57.660000  63.139999   
34  414.0  ...   352.0  39.160000  35.490002  52.270000  31.450001  72.459999   
35   58.0  ...   353.0  53.369999  58.320000  49.099998  53.290001  62.480000   
36  414.0  ...   353.0  37.740002  39.169998  52.169998  30.580000  71.779999   
37   52.0  ...   352.0  50.820000  61.500000  56.619999  57.869999  67.220001   
38  159.0  ...   354.0  53.450001  57.770000  41.880001  53.930000  63.400002   
39  351.0  ...   352.0  55.400002  59.570000  42.580002  57.580002  64.900002   
40  414.0  ...   353.0  38.029999  44.529999  41.540001  37.200001  72.459999   
41  646.0  ...   353.0  53.270000  56.009998  59.470001  58.889999  65.269997   

    X_2871  Y_Class  prediction_label  prediction_score  
29     1.0        2                 2            0.8167  
30     1.0        1                 1            0.3674  
31     1.0        0                 0            0.9681  
32     1.0        2                 2            0.9212  
33     1.0        1                 1            0.4226  
34     1.0        2                 2            0.9799  
35     1.0        0                 0            0.9474  
36     1.0        2                 2            0.7076  
37     1.0        0                 0            0.8885  
38     1.0        2                 2            0.9510  
39     1.0        1                 1            0.5424  
40     1.0        2                 2            0.9658  
41     1.0        2                 2            0.8988  

[13 rows x 1979 columns]

PRODUCT_CODE    X_130    X_131  X_132  X_133  X_134  X_135  X_136  X_137  \
29             1  20594.0  20594.0   0.20   0.21   0.20    0.2  633.0  633.0   
30             1  11942.0  11942.0   0.20   0.21   0.20    0.2  394.0  396.0   
31             1    919.0    919.0   0.19   0.21   0.19    0.2   59.0   59.0   
32             1  26126.0  26126.0   0.19   0.21   0.19    0.2  779.0  779.0   
33             1   2446.0   2446.0   0.19   0.20   0.19    0.2   84.0   84.0   
34             1  19866.0  19866.0   0.20   0.21   0.20    0.2  414.0  414.0   
35             1    806.0    806.0   0.19   0.21   0.19    0.2   58.0   58.0   
36             1  19856.0  19856.0   0.20   0.21   0.20    0.2  414.0  414.0   
37             1   1102.0   1102.0   0.19   0.21   0.19    0.2   50.0   52.0   
38             1   3699.0   3699.0   0.20   0.21   0.20    0.2  157.0  159.0   
39             1  10545.0  10545.0   0.20   0.21   0.20    0.2  349.0  351.0   
40             1  19871.0  19871.0   0.20   0.21   0.20    0.2  414.0  414.0   
41             1  21289.0  21289.0   0.20   0.21   0.19    0.2  646.0  646.0   

    X_138  ...  X_2865     X_2866     X_2867     X_2868     X_2869     X_2870  \
29  633.0  ...   353.0  49.284546  52.343941  51.516666  50.293938  66.576057   
30  396.0  ...   352.0  55.689999  53.029999  53.750000  58.959999  64.010002   
31   59.0  ...   352.0  53.169998  53.220001  50.070000  57.130001  64.269997   
32  779.0  ...   352.0  44.040001  60.240002  59.639999  57.340000  65.860001   
33   84.0  ...   352.0  53.639999  58.900002  49.849998  57.660000  63.139999   
34  414.0  ...   352.0  39.160000  35.490002  52.270000  31.450001  72.459999   
35   58.0  ...   353.0  53.369999  58.320000  49.099998  53.290001  62.480000   
36  414.0  ...   353.0  37.740002  39.169998  52.169998  30.580000  71.779999   
37   52.0  ...   352.0  50.820000  61.500000  56.619999  57.869999  67.220001   
38  159.0  ...   354.0  53.450001  57.770000  41.880001  53.930000  63.400002   
39  351.0  ...   352.0  55.400002  59.570000  42.580002  57.580002  64.900002   
40  414.0  ...   353.0  38.029999  44.529999  41.540001  37.200001  72.459999   
41  646.0  ...   353.0  53.270000  56.009998  59.470001  58.889999  65.269997   

    X_2871  Y_Class  prediction_label  prediction_score  
29     1.0        2                 2            0.5172  
30     1.0        1                 2            0.5172  
31     1.0        0                 2            0.5172  
32     1.0        2                 2            0.5172  
33     1.0        1                 2            0.5172  
34     1.0        2                 2            0.5172  
35     1.0        0                 2            0.5172  
36     1.0        2                 2            0.5172  
37     1.0        0                 2            0.5172  
38     1.0        2                 2            0.5172  
39     1.0        1                 2            0.5172  
40     1.0        2                 2            0.5172  
41     1.0        2                 2            0.5172  

[13 rows x 1979 columns]

PRODUCT_CODE    X_130    X_131  X_132  X_133  X_134  X_135  X_136  X_137  \
29             1  20594.0  20594.0   0.20   0.21   0.20    0.2  633.0  633.0   
30             1  11942.0  11942.0   0.20   0.21   0.20    0.2  394.0  396.0   
31             1    919.0    919.0   0.19   0.21   0.19    0.2   59.0   59.0   
32             1  26126.0  26126.0   0.19   0.21   0.19    0.2  779.0  779.0   
33             1   2446.0   2446.0   0.19   0.20   0.19    0.2   84.0   84.0   
34             1  19866.0  19866.0   0.20   0.21   0.20    0.2  414.0  414.0   
35             1    806.0    806.0   0.19   0.21   0.19    0.2   58.0   58.0   
36             1  19856.0  19856.0   0.20   0.21   0.20    0.2  414.0  414.0   
37             1   1102.0   1102.0   0.19   0.21   0.19    0.2   50.0   52.0   
38             1   3699.0   3699.0   0.20   0.21   0.20    0.2  157.0  159.0   
39             1  10545.0  10545.0   0.20   0.21   0.20    0.2  349.0  351.0   
40             1  19871.0  19871.0   0.20   0.21   0.20    0.2  414.0  414.0   
41             1  21289.0  21289.0   0.20   0.21   0.19    0.2  646.0  646.0   

    X_138  ...  X_2865     X_2866     X_2867     X_2868     X_2869     X_2870  \
29  633.0  ...   353.0  49.284546  52.343941  51.516666  50.293938  66.576057   
30  396.0  ...   352.0  55.689999  53.029999  53.750000  58.959999  64.010002   
31   59.0  ...   352.0  53.169998  53.220001  50.070000  57.130001  64.269997   
32  779.0  ...   352.0  44.040001  60.240002  59.639999  57.340000  65.860001   
33   84.0  ...   352.0  53.639999  58.900002  49.849998  57.660000  63.139999   
34  414.0  ...   352.0  39.160000  35.490002  52.270000  31.450001  72.459999   
35   58.0  ...   353.0  53.369999  58.320000  49.099998  53.290001  62.480000   
36  414.0  ...   353.0  37.740002  39.169998  52.169998  30.580000  71.779999   
37   52.0  ...   352.0  50.820000  61.500000  56.619999  57.869999  67.220001   
38  159.0  ...   354.0  53.450001  57.770000  41.880001  53.930000  63.400002   
39  351.0  ...   352.0  55.400002  59.570000  42.580002  57.580002  64.900002   
40  414.0  ...   353.0  38.029999  44.529999  41.540001  37.200001  72.459999   
41  646.0  ...   353.0  53.270000  56.009998  59.470001  58.889999  65.269997   

    X_2871  Y_Class  prediction_label  prediction_score  
29     1.0        2                 2            0.4375  
30     1.0        1                 2            0.3736  
31     1.0        0                 0            0.5733  
32     1.0        2                 2            0.5510  
33     1.0        1                 1            0.5108  
34     1.0        2                 2            0.7991  
35     1.0        0                 0            0.5633  
36     1.0        2                 2            0.6170  
37     1.0        0                 0            0.4122  
38     1.0        2                 2            0.5956  
39     1.0        1                 0            0.4730  
40     1.0        2                 2            0.7978  
41     1.0        2                 2            0.4216  

[13 rows x 1979 columns]

In [205]:
T050307_final_classification_model = finalize_model(T050307_model_xgb)

In [206]:
#최종 예측
#29
T050307_prediction = predict_model(T050307_final_classification_model, data=T050307_data)
#prediction.drop(['Y_Quality'], axis = 1, inplace = True)

# T010305

In [207]:
T010305_class = T010305['Y_Class']
T010305_target = T010305['Y_Quality']
T010305_data = T010305.drop(['Y_Class', 'Y_Quality'], axis = 1)
T010305_data

PRODUCT_CODE  X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  \
28              1    1.0   89.0    0.0   45.0   11.0   90.0   45.0   11.0   
33              1    1.0   95.0    0.0   45.0   11.0   98.0   45.0   11.0   
39              1    1.0   95.0    0.0   45.0   11.0  102.0   45.0   12.0   
40              1    1.0   95.0    0.0   45.0   11.0  105.0   45.0   11.0   
41              1    1.0   87.0    0.0   45.0   11.0  105.0   45.0   11.0   
48              1    1.0   91.0    0.0   45.0   11.0  111.0   45.0   11.0   
52              1    2.0   87.0    0.0   45.0   11.0  114.0   45.0   11.0   
57              1    2.0   87.0    0.0   45.0   11.0  119.0   45.0   11.0   
58              1    1.0   88.0    0.0   45.0   11.0  119.0   45.0   11.0   
59              1    2.0   88.0    0.0   45.0   11.0  120.0   45.0   11.0   
64              1    1.0   90.0    0.0   45.0   11.0  125.0   45.0   11.0   
65              1    2.0   87.0    0.0   45.0   11.0  126.0   45.0   11.0   
66              1    2.0   88.0    0.0   45.0   11.0  127.0   45.0   11.0   
69              1    2.0   91.0    0.0   45.0   11.0  129.0   45.0   11.0   
71              1    1.0   89.0    0.0   45.0   11.0  129.0   45.0   11.0   
75              1    2.0   89.0    0.0   45.0   11.0  135.0   45.0   11.0   
77              1    1.0   95.0    0.0   45.0   11.0  148.0   45.0   11.0   
84              1    1.0   95.0    0.0   45.0   11.0  155.0   45.0   11.0   
90              1    2.0   89.0    0.0   45.0   11.0  163.0   45.0   11.0   
94              1    1.0   88.0    0.0   45.0   11.0  167.0   45.0   11.0   
95              1    2.0   90.0    0.0   45.0   11.0  168.0   45.0   11.0   
116             1    1.0   95.0    0.0   45.0   11.0    2.0   45.0   11.0   
118             1    1.0   91.0    0.0   45.0   11.0    2.0   45.0   12.0   
123             1    2.0   93.0    0.0   45.0   11.0    8.0   45.0   11.0   
129             1    1.0   89.0    0.0   45.0   11.0   13.0   45.0   12.0   
179             1    1.0   87.0    0.0   45.0   11.0   11.0   45.0   11.0   
190             1    1.0   95.0    0.0   45.0   11.0   22.0   45.0   11.0   
208             1    1.0   95.0    0.0   45.0   11.0   28.0   45.0   11.0   
220             1    2.0   93.0    0.0   45.0   11.0   34.0   45.0   11.0   
230             1    2.0   91.0    0.0   45.0   11.0   38.0   45.0   11.0   
235             1    2.0   88.0    0.0   45.0   11.0   42.0   45.0   11.0   
239             1    2.0   88.0    0.0   45.0   11.0   44.0   45.0   11.0   
244             1    1.0   90.0    0.0   45.0   11.0   46.0   45.0   11.0   
281             1    2.0   88.0    0.0   45.0   11.0   85.0   45.0   11.0   
283             1    1.0   89.0    0.0   45.0   11.0   85.0   45.0   12.0   
287             1    1.0   90.0    0.0   45.0   11.0   87.0   45.0   11.0   
291             1    1.0   90.0    0.0   45.0   11.0   89.0   45.0   11.0   
292             1    1.0   89.0    0.0   45.0   11.0   89.0   45.0   11.0   
295             1    1.0   89.0    0.0   45.0   11.0   91.0   45.0   11.0   
299             1    1.0   96.0    0.0   45.0   11.0   93.0   45.0   11.0   
300             1    1.0   87.0    0.0   45.0   11.0   93.0   45.0   11.0   
312             1    1.0   88.0    0.0   45.0   11.0   96.0   45.0   11.0   
332             1    1.0   90.0    0.0   45.0   11.0  111.0   45.0   11.0   
334             1    2.0   88.0    0.0   45.0   11.0  111.0   45.0   11.0   
404             1    1.0   90.0    0.0   45.0   11.0   14.0   45.0   11.0   
410             1    1.0   88.0    0.0   45.0   11.0   19.0   45.0   11.0   
436             1    1.0   90.0    0.0   45.0   11.0   35.0   45.0   11.0   
449             1   11.0   90.0    0.0   45.0   11.0   43.0   45.0   11.0   
455             1    1.0   89.0    0.0   45.0   11.0   45.0   45.0   11.0   
456             1    1.0   91.0    0.0   45.0   11.0   45.0   45.0   11.0   
480             1    1.0   88.0    0.0   45.0   11.0   61.0   45.0   11.0   
4

In [208]:
from pycaret.classification import *
# 분류 패키지의 모든 모듈을 임포트한다.
exp_clf101 = setup(data=T010305_data, 
                   target=T010305_class, 
                   fold=5,
                   session_id=414)
top5 = compare_models(sort='Accuracy', n_select=5)

Processing:   0%|          | 0/73 [00:00<?, ?it/s]

In [209]:
T010305_total_models = []

T010305_model_lda = create_model('lda', fold = 5)
T010305_total_models.append(T010305_model_lda)

T010305_model_lr = create_model('lr', fold = 5)
T010305_total_models.append(T010305_model_lr)

T010305_model_gbc = create_model('gbc', fold = 5)
T010305_total_models.append(T010305_model_gbc)

T010305_model_et = create_model('et', fold = 5)
T010305_total_models.append(T010305_model_et)

T010305_model_catboost = create_model('catboost', fold = 5)
T010305_total_models.append(T010305_model_catboost)

T010305_model_xgb = create_model('xgboost', fold = 5)
T010305_total_models.append(T010305_model_xgb)

T010305_model_ada = create_model('ada', fold = 5)
T010305_total_models.append(T010305_model_ada)

T010305_model_rf = create_model('rf', fold = 5)
T010305_total_models.append(T010305_model_rf)

T010305_model_lightgbm = create_model('lightgbm', fold = 5)
T010305_total_models.append(T010305_model_lightgbm)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [210]:
T010305_model_lda = tune_model(T010305_model_lda, fold=5, choose_better = True)

T010305_model_lr = tune_model(T010305_model_lr, fold=5, choose_better = True)

T010305_model_rf = tune_model(T010305_model_rf, fold=5, choose_better = True)

T010305_model_gbc = tune_model(T010305_model_gbc, fold=5, choose_better = True)

T010305_model_ada = tune_model(T010305_model_ada, fold=5, choose_better = True)

T010305_model_catboost = tune_model(T010305_model_catboost, fold=5, choose_better = True)

T010305_model_xgb = tune_model(T010305_model_xgb, fold=5, choose_better = True)

T010305_model_lightgbm = tune_model(T010305_model_lightgbm, fold=5, choose_better = True)

T010305_model_et = tune_model(T010305_model_et, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


In [211]:
T010305_tuned_models = [T010305_model_lda, T010305_model_lr, T010305_model_rf, T010305_model_gbc, T010305_model_ada, T010305_model_catboost, T010305_model_xgb, T010305_model_lightgbm, T010305_model_et]
T010305_tuned_models

[LinearDiscriminantAnalysis(covariance_estimator=None, n_components=None,
                            priors=None, shrinkage=None, solver='svd',
                            store_covariance=False, tol=0.0001),
 LogisticRegression(C=1.0, class_weight=None, dual=False, fit_intercept=True,
                    intercept_scaling=1, l1_ratio=None, max_iter=1000,
                    multi_class='auto', n_jobs=None, penalty='l2',
                    random_state=414, solver='lbfgs', tol=0.0001, verbose=0,
                    warm_start=False),
 RandomForestClassifier(bootstrap=True, ccp_alpha=0.0, class_weight='balanced',
                        criterion='gini', max_depth=4, max_features='log2',
                        max_leaf_nodes=None, max_samples=None,
                        min_impurity_decrease=0.4, min_samples_leaf=4,
                        min_samples_split=7, min_weight_fraction_leaf=0.0,
                        n_estimators=230, n_jobs=-1, oob_score=False,
                       

In [212]:
for model in T010305_tuned_models:
    display(predict_model(model))

PRODUCT_CODE  X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  \
41             1    2.0   90.0    0.0   45.0   11.0  122.0   45.0   11.0   
42             1    1.0   88.0    0.0   45.0   11.0   96.0   45.0   11.0   
43             1    1.0   90.0    0.0   45.0   11.0   89.0   45.0   11.0   
44             1    1.0   90.0    0.0   45.0   11.0  125.0   45.0   11.0   
45             1    2.0   93.0    0.0   45.0   11.0    8.0   45.0   11.0   
46             1    1.0   90.0    0.0   45.0   11.0   35.0   45.0   11.0   
47             1    2.0   87.0    0.0   45.0   11.0  126.0   45.0   11.0   
48             1    1.0   95.0    0.0   45.0   11.0  148.0   45.0   11.0   
49             1    2.0   87.0    0.0   45.0   11.0  119.0   45.0   11.0   
50             1    1.0   89.0    0.0   45.0   11.0   45.0   45.0   11.0   
51             1    1.0   95.0    0.0   45.0   11.0   22.0   45.0   11.0   
52             1    2.0   88.0    0.0   45.0   11.0  127.0   45.0   11.0   
53             1    1.0   88.0    0.0   45.0   11.0  167.0   45.0   11.0   
54             1    1.0   91.0    0.0   45.0   11.0  111.0   45.0   11.0   
55             1    1.0   88.0    0.0   45.0   11.0   61.0   45.0   11.0   
56             1    2.0   87.0    0.0   45.0   11.0   78.0   45.0   11.0   
57             1    2.0   88.0    0.0   45.0   11.0   42.0   45.0   11.0   
58             1    1.0   87.0    0.0   45.0   11.0  105.0   45.0   11.0   

    X_254  ...      X_2859      X_2860      X_2861      X_2862  X_2863  \
41   42.0  ...  195.699997  201.199997  191.286209  181.699997   466.0   
42   42.0  ...  178.100006  170.899994  159.134476  149.199997   465.0   
43   42.0  ...  187.000000  181.600006  169.371429  156.100006   465.0   
44   42.0  ...  184.500000  196.199997  188.800003  175.699997   465.0   
45   42.0  ...  163.100006  177.800003  167.967850  158.399994   466.0   
46   42.0  ...  191.100006  174.500000  167.992859  161.800003   466.0   
47   42.0  ...  192.100006  192.000000  186.341385  175.100006   463.0   
48   42.0  ...  169.100006  198.899994  188.513794  181.000000   456.0   
49   42.0  ...  183.199997  197.500000  189.206894  181.800003   437.0   
50   42.0  ...  188.199997  179.899994  168.828568  156.300003   456.0   
51   42.0  ...  161.100006  185.100006  167.035721  157.300003   466.0   
52   42.0  ...  189.899994  190.399994  184.720688  180.000000   466.0   
53   42.0  ...  163.100006  156.199997  153.746429  150.899994   466.0   
54   42.0  ...  175.100006  183.100006  174.758621  160.600006   446.0   
55   42.0  ...  167.600006  179.399994  170.572418  157.600006   456.0   
56   42.0  ...  172.699997  192.399994  171.437927  154.100006   465.0   
57   42.0  ...  185.300003  173.100006  162.460709  154.000000   456.0   
58   42.0  ...  146.899994  182.399994  170.379303  162.899994   446.0   

        X_2864  X_2865  Y_Class  prediction_label  prediction_score  
41  444.924530   424.0        0                 1            0.7868  
42  447.245270   423.0        0                 1            0.8072  
43  445.634613   423.0        2                 1            0.8986  
44  441.396240   423.0        1                 1            0.8980  
45  447.750000   432.0        0                 1            0.6120  
46  443.923065   423.0        1                 1            0.8306  
47  440.867920   423.0        1                 1            0.6671  
48  439.415100   422.0        1                 1            0.8855  
49  418.660370   396.0        2                 2            0.9389  
50  438.596161   422.0        1                 1            0.7415  
51  448.442322   433.0        1                 1            0.6560  
52  449.962250   434.0        0                 1            0.6055  
53  449.326935   432.0        2                 1            0.8793  
54  428.000000   413.0        1                 1            0.6024  
55  440.075470   422.0        1                 1            0.6459  
56  448.075470   423.0        1 

PRODUCT_CODE  X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  \
41             1    2.0   90.0    0.0   45.0   11.0  122.0   45.0   11.0   
42             1    1.0   88.0    0.0   45.0   11.0   96.0   45.0   11.0   
43             1    1.0   90.0    0.0   45.0   11.0   89.0   45.0   11.0   
44             1    1.0   90.0    0.0   45.0   11.0  125.0   45.0   11.0   
45             1    2.0   93.0    0.0   45.0   11.0    8.0   45.0   11.0   
46             1    1.0   90.0    0.0   45.0   11.0   35.0   45.0   11.0   
47             1    2.0   87.0    0.0   45.0   11.0  126.0   45.0   11.0   
48             1    1.0   95.0    0.0   45.0   11.0  148.0   45.0   11.0   
49             1    2.0   87.0    0.0   45.0   11.0  119.0   45.0   11.0   
50             1    1.0   89.0    0.0   45.0   11.0   45.0   45.0   11.0   
51             1    1.0   95.0    0.0   45.0   11.0   22.0   45.0   11.0   
52             1    2.0   88.0    0.0   45.0   11.0  127.0   45.0   11.0   
53             1    1.0   88.0    0.0   45.0   11.0  167.0   45.0   11.0   
54             1    1.0   91.0    0.0   45.0   11.0  111.0   45.0   11.0   
55             1    1.0   88.0    0.0   45.0   11.0   61.0   45.0   11.0   
56             1    2.0   87.0    0.0   45.0   11.0   78.0   45.0   11.0   
57             1    2.0   88.0    0.0   45.0   11.0   42.0   45.0   11.0   
58             1    1.0   87.0    0.0   45.0   11.0  105.0   45.0   11.0   

    X_254  ...      X_2859      X_2860      X_2861      X_2862  X_2863  \
41   42.0  ...  195.699997  201.199997  191.286209  181.699997   466.0   
42   42.0  ...  178.100006  170.899994  159.134476  149.199997   465.0   
43   42.0  ...  187.000000  181.600006  169.371429  156.100006   465.0   
44   42.0  ...  184.500000  196.199997  188.800003  175.699997   465.0   
45   42.0  ...  163.100006  177.800003  167.967850  158.399994   466.0   
46   42.0  ...  191.100006  174.500000  167.992859  161.800003   466.0   
47   42.0  ...  192.100006  192.000000  186.341385  175.100006   463.0   
48   42.0  ...  169.100006  198.899994  188.513794  181.000000   456.0   
49   42.0  ...  183.199997  197.500000  189.206894  181.800003   437.0   
50   42.0  ...  188.199997  179.899994  168.828568  156.300003   456.0   
51   42.0  ...  161.100006  185.100006  167.035721  157.300003   466.0   
52   42.0  ...  189.899994  190.399994  184.720688  180.000000   466.0   
53   42.0  ...  163.100006  156.199997  153.746429  150.899994   466.0   
54   42.0  ...  175.100006  183.100006  174.758621  160.600006   446.0   
55   42.0  ...  167.600006  179.399994  170.572418  157.600006   456.0   
56   42.0  ...  172.699997  192.399994  171.437927  154.100006   465.0   
57   42.0  ...  185.300003  173.100006  162.460709  154.000000   456.0   
58   42.0  ...  146.899994  182.399994  170.379303  162.899994   446.0   

        X_2864  X_2865  Y_Class  prediction_label  prediction_score  
41  444.924530   424.0        0                 1            0.9395  
42  447.245270   423.0        0                 2            0.8460  
43  445.634613   423.0        2                 1            0.8842  
44  441.396240   423.0        1                 0            1.0000  
45  447.750000   432.0        0                 1            0.9643  
46  443.923065   423.0        1                 1            1.0000  
47  440.867920   423.0        1                 0            1.0000  
48  439.415100   422.0        1                 1            1.0000  
49  418.660370   396.0        2                 2            0.9937  
50  438.596161   422.0        1                 1            0.9906  
51  448.442322   433.0        1                 1            0.9992  
52  449.962250   434.0        0                 0            1.0000  
53  449.326935   432.0        2                 2            0.9888  
54  428.000000   413.0        1                 1            1.0000  
55  440.075470   422.0        1                 1            0.9989  
56  448.075470   423.0        1 

PRODUCT_CODE  X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  \
41             1    2.0   90.0    0.0   45.0   11.0  122.0   45.0   11.0   
42             1    1.0   88.0    0.0   45.0   11.0   96.0   45.0   11.0   
43             1    1.0   90.0    0.0   45.0   11.0   89.0   45.0   11.0   
44             1    1.0   90.0    0.0   45.0   11.0  125.0   45.0   11.0   
45             1    2.0   93.0    0.0   45.0   11.0    8.0   45.0   11.0   
46             1    1.0   90.0    0.0   45.0   11.0   35.0   45.0   11.0   
47             1    2.0   87.0    0.0   45.0   11.0  126.0   45.0   11.0   
48             1    1.0   95.0    0.0   45.0   11.0  148.0   45.0   11.0   
49             1    2.0   87.0    0.0   45.0   11.0  119.0   45.0   11.0   
50             1    1.0   89.0    0.0   45.0   11.0   45.0   45.0   11.0   
51             1    1.0   95.0    0.0   45.0   11.0   22.0   45.0   11.0   
52             1    2.0   88.0    0.0   45.0   11.0  127.0   45.0   11.0   
53             1    1.0   88.0    0.0   45.0   11.0  167.0   45.0   11.0   
54             1    1.0   91.0    0.0   45.0   11.0  111.0   45.0   11.0   
55             1    1.0   88.0    0.0   45.0   11.0   61.0   45.0   11.0   
56             1    2.0   87.0    0.0   45.0   11.0   78.0   45.0   11.0   
57             1    2.0   88.0    0.0   45.0   11.0   42.0   45.0   11.0   
58             1    1.0   87.0    0.0   45.0   11.0  105.0   45.0   11.0   

    X_254  ...      X_2859      X_2860      X_2861      X_2862  X_2863  \
41   42.0  ...  195.699997  201.199997  191.286209  181.699997   466.0   
42   42.0  ...  178.100006  170.899994  159.134476  149.199997   465.0   
43   42.0  ...  187.000000  181.600006  169.371429  156.100006   465.0   
44   42.0  ...  184.500000  196.199997  188.800003  175.699997   465.0   
45   42.0  ...  163.100006  177.800003  167.967850  158.399994   466.0   
46   42.0  ...  191.100006  174.500000  167.992859  161.800003   466.0   
47   42.0  ...  192.100006  192.000000  186.341385  175.100006   463.0   
48   42.0  ...  169.100006  198.899994  188.513794  181.000000   456.0   
49   42.0  ...  183.199997  197.500000  189.206894  181.800003   437.0   
50   42.0  ...  188.199997  179.899994  168.828568  156.300003   456.0   
51   42.0  ...  161.100006  185.100006  167.035721  157.300003   466.0   
52   42.0  ...  189.899994  190.399994  184.720688  180.000000   466.0   
53   42.0  ...  163.100006  156.199997  153.746429  150.899994   466.0   
54   42.0  ...  175.100006  183.100006  174.758621  160.600006   446.0   
55   42.0  ...  167.600006  179.399994  170.572418  157.600006   456.0   
56   42.0  ...  172.699997  192.399994  171.437927  154.100006   465.0   
57   42.0  ...  185.300003  173.100006  162.460709  154.000000   456.0   
58   42.0  ...  146.899994  182.399994  170.379303  162.899994   446.0   

        X_2864  X_2865  Y_Class  prediction_label  prediction_score  
41  444.924530   424.0        0                 2            0.3412  
42  447.245270   423.0        0                 2            0.3412  
43  445.634613   423.0        2                 2            0.3412  
44  441.396240   423.0        1                 2            0.3412  
45  447.750000   432.0        0                 2            0.3412  
46  443.923065   423.0        1                 2            0.3412  
47  440.867920   423.0        1                 2            0.3412  
48  439.415100   422.0        1                 2            0.3412  
49  418.660370   396.0        2                 2            0.3412  
50  438.596161   422.0        1                 2            0.3412  
51  448.442322   433.0        1                 2            0.3412  
52  449.962250   434.0        0                 2            0.3412  
53  449.326935   432.0        2                 2            0.3412  
54  428.000000   413.0        1                 2            0.3412  
55  440.075470   422.0        1                 2            0.3412  
56  448.075470   423.0        1 

PRODUCT_CODE  X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  \
41             1    2.0   90.0    0.0   45.0   11.0  122.0   45.0   11.0   
42             1    1.0   88.0    0.0   45.0   11.0   96.0   45.0   11.0   
43             1    1.0   90.0    0.0   45.0   11.0   89.0   45.0   11.0   
44             1    1.0   90.0    0.0   45.0   11.0  125.0   45.0   11.0   
45             1    2.0   93.0    0.0   45.0   11.0    8.0   45.0   11.0   
46             1    1.0   90.0    0.0   45.0   11.0   35.0   45.0   11.0   
47             1    2.0   87.0    0.0   45.0   11.0  126.0   45.0   11.0   
48             1    1.0   95.0    0.0   45.0   11.0  148.0   45.0   11.0   
49             1    2.0   87.0    0.0   45.0   11.0  119.0   45.0   11.0   
50             1    1.0   89.0    0.0   45.0   11.0   45.0   45.0   11.0   
51             1    1.0   95.0    0.0   45.0   11.0   22.0   45.0   11.0   
52             1    2.0   88.0    0.0   45.0   11.0  127.0   45.0   11.0   
53             1    1.0   88.0    0.0   45.0   11.0  167.0   45.0   11.0   
54             1    1.0   91.0    0.0   45.0   11.0  111.0   45.0   11.0   
55             1    1.0   88.0    0.0   45.0   11.0   61.0   45.0   11.0   
56             1    2.0   87.0    0.0   45.0   11.0   78.0   45.0   11.0   
57             1    2.0   88.0    0.0   45.0   11.0   42.0   45.0   11.0   
58             1    1.0   87.0    0.0   45.0   11.0  105.0   45.0   11.0   

    X_254  ...      X_2859      X_2860      X_2861      X_2862  X_2863  \
41   42.0  ...  195.699997  201.199997  191.286209  181.699997   466.0   
42   42.0  ...  178.100006  170.899994  159.134476  149.199997   465.0   
43   42.0  ...  187.000000  181.600006  169.371429  156.100006   465.0   
44   42.0  ...  184.500000  196.199997  188.800003  175.699997   465.0   
45   42.0  ...  163.100006  177.800003  167.967850  158.399994   466.0   
46   42.0  ...  191.100006  174.500000  167.992859  161.800003   466.0   
47   42.0  ...  192.100006  192.000000  186.341385  175.100006   463.0   
48   42.0  ...  169.100006  198.899994  188.513794  181.000000   456.0   
49   42.0  ...  183.199997  197.500000  189.206894  181.800003   437.0   
50   42.0  ...  188.199997  179.899994  168.828568  156.300003   456.0   
51   42.0  ...  161.100006  185.100006  167.035721  157.300003   466.0   
52   42.0  ...  189.899994  190.399994  184.720688  180.000000   466.0   
53   42.0  ...  163.100006  156.199997  153.746429  150.899994   466.0   
54   42.0  ...  175.100006  183.100006  174.758621  160.600006   446.0   
55   42.0  ...  167.600006  179.399994  170.572418  157.600006   456.0   
56   42.0  ...  172.699997  192.399994  171.437927  154.100006   465.0   
57   42.0  ...  185.300003  173.100006  162.460709  154.000000   456.0   
58   42.0  ...  146.899994  182.399994  170.379303  162.899994   446.0   

        X_2864  X_2865  Y_Class  prediction_label  prediction_score  
41  444.924530   424.0        0                 1            0.9341  
42  447.245270   423.0        0                 1            0.9897  
43  445.634613   423.0        2                 1            0.9466  
44  441.396240   423.0        1                 1            0.9033  
45  447.750000   432.0        0                 1            0.8259  
46  443.923065   423.0        1                 1            0.8346  
47  440.867920   423.0        1                 1            0.9740  
48  439.415100   422.0        1                 1            0.9346  
49  418.660370   396.0        2                 2            0.9046  
50  438.596161   422.0        1                 1            0.9988  
51  448.442322   433.0        1                 1            0.9873  
52  449.962250   434.0        0                 2            0.5714  
53  449.326935   432.0        2                 1            0.9719  
54  428.000000   413.0        1                 1            0.9132  
55  440.075470   422.0        1                 1            0.9848  
56  448.075470   423.0        1 

PRODUCT_CODE  X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  \
41             1    2.0   90.0    0.0   45.0   11.0  122.0   45.0   11.0   
42             1    1.0   88.0    0.0   45.0   11.0   96.0   45.0   11.0   
43             1    1.0   90.0    0.0   45.0   11.0   89.0   45.0   11.0   
44             1    1.0   90.0    0.0   45.0   11.0  125.0   45.0   11.0   
45             1    2.0   93.0    0.0   45.0   11.0    8.0   45.0   11.0   
46             1    1.0   90.0    0.0   45.0   11.0   35.0   45.0   11.0   
47             1    2.0   87.0    0.0   45.0   11.0  126.0   45.0   11.0   
48             1    1.0   95.0    0.0   45.0   11.0  148.0   45.0   11.0   
49             1    2.0   87.0    0.0   45.0   11.0  119.0   45.0   11.0   
50             1    1.0   89.0    0.0   45.0   11.0   45.0   45.0   11.0   
51             1    1.0   95.0    0.0   45.0   11.0   22.0   45.0   11.0   
52             1    2.0   88.0    0.0   45.0   11.0  127.0   45.0   11.0   
53             1    1.0   88.0    0.0   45.0   11.0  167.0   45.0   11.0   
54             1    1.0   91.0    0.0   45.0   11.0  111.0   45.0   11.0   
55             1    1.0   88.0    0.0   45.0   11.0   61.0   45.0   11.0   
56             1    2.0   87.0    0.0   45.0   11.0   78.0   45.0   11.0   
57             1    2.0   88.0    0.0   45.0   11.0   42.0   45.0   11.0   
58             1    1.0   87.0    0.0   45.0   11.0  105.0   45.0   11.0   

    X_254  ...      X_2859      X_2860      X_2861      X_2862  X_2863  \
41   42.0  ...  195.699997  201.199997  191.286209  181.699997   466.0   
42   42.0  ...  178.100006  170.899994  159.134476  149.199997   465.0   
43   42.0  ...  187.000000  181.600006  169.371429  156.100006   465.0   
44   42.0  ...  184.500000  196.199997  188.800003  175.699997   465.0   
45   42.0  ...  163.100006  177.800003  167.967850  158.399994   466.0   
46   42.0  ...  191.100006  174.500000  167.992859  161.800003   466.0   
47   42.0  ...  192.100006  192.000000  186.341385  175.100006   463.0   
48   42.0  ...  169.100006  198.899994  188.513794  181.000000   456.0   
49   42.0  ...  183.199997  197.500000  189.206894  181.800003   437.0   
50   42.0  ...  188.199997  179.899994  168.828568  156.300003   456.0   
51   42.0  ...  161.100006  185.100006  167.035721  157.300003   466.0   
52   42.0  ...  189.899994  190.399994  184.720688  180.000000   466.0   
53   42.0  ...  163.100006  156.199997  153.746429  150.899994   466.0   
54   42.0  ...  175.100006  183.100006  174.758621  160.600006   446.0   
55   42.0  ...  167.600006  179.399994  170.572418  157.600006   456.0   
56   42.0  ...  172.699997  192.399994  171.437927  154.100006   465.0   
57   42.0  ...  185.300003  173.100006  162.460709  154.000000   456.0   
58   42.0  ...  146.899994  182.399994  170.379303  162.899994   446.0   

        X_2864  X_2865  Y_Class  prediction_label  prediction_score  
41  444.924530   424.0        0                 1            0.9931  
42  447.245270   423.0        0                 1            0.8054  
43  445.634613   423.0        2                 1            0.8661  
44  441.396240   423.0        1                 1            0.9965  
45  447.750000   432.0        0                 1            0.8046  
46  443.923065   423.0        1                 1            0.7292  
47  440.867920   423.0        1                 1            0.9001  
48  439.415100   422.0        1                 1            0.9870  
49  418.660370   396.0        2                 2            0.7000  
50  438.596161   422.0        1                 1            0.6730  
51  448.442322   433.0        1                 1            0.8072  
52  449.962250   434.0        0                 1            0.9154  
53  449.326935   432.0        2                 1            0.9614  
54  428.000000   413.0        1                 1            0.9907  
55  440.075470   422.0        1                 1            0.6551  
56  448.075470   423.0        1 

PRODUCT_CODE  X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  \
41             1    2.0   90.0    0.0   45.0   11.0  122.0   45.0   11.0   
42             1    1.0   88.0    0.0   45.0   11.0   96.0   45.0   11.0   
43             1    1.0   90.0    0.0   45.0   11.0   89.0   45.0   11.0   
44             1    1.0   90.0    0.0   45.0   11.0  125.0   45.0   11.0   
45             1    2.0   93.0    0.0   45.0   11.0    8.0   45.0   11.0   
46             1    1.0   90.0    0.0   45.0   11.0   35.0   45.0   11.0   
47             1    2.0   87.0    0.0   45.0   11.0  126.0   45.0   11.0   
48             1    1.0   95.0    0.0   45.0   11.0  148.0   45.0   11.0   
49             1    2.0   87.0    0.0   45.0   11.0  119.0   45.0   11.0   
50             1    1.0   89.0    0.0   45.0   11.0   45.0   45.0   11.0   
51             1    1.0   95.0    0.0   45.0   11.0   22.0   45.0   11.0   
52             1    2.0   88.0    0.0   45.0   11.0  127.0   45.0   11.0   
53             1    1.0   88.0    0.0   45.0   11.0  167.0   45.0   11.0   
54             1    1.0   91.0    0.0   45.0   11.0  111.0   45.0   11.0   
55             1    1.0   88.0    0.0   45.0   11.0   61.0   45.0   11.0   
56             1    2.0   87.0    0.0   45.0   11.0   78.0   45.0   11.0   
57             1    2.0   88.0    0.0   45.0   11.0   42.0   45.0   11.0   
58             1    1.0   87.0    0.0   45.0   11.0  105.0   45.0   11.0   

    X_254  ...      X_2859      X_2860      X_2861      X_2862  X_2863  \
41   42.0  ...  195.699997  201.199997  191.286209  181.699997   466.0   
42   42.0  ...  178.100006  170.899994  159.134476  149.199997   465.0   
43   42.0  ...  187.000000  181.600006  169.371429  156.100006   465.0   
44   42.0  ...  184.500000  196.199997  188.800003  175.699997   465.0   
45   42.0  ...  163.100006  177.800003  167.967850  158.399994   466.0   
46   42.0  ...  191.100006  174.500000  167.992859  161.800003   466.0   
47   42.0  ...  192.100006  192.000000  186.341385  175.100006   463.0   
48   42.0  ...  169.100006  198.899994  188.513794  181.000000   456.0   
49   42.0  ...  183.199997  197.500000  189.206894  181.800003   437.0   
50   42.0  ...  188.199997  179.899994  168.828568  156.300003   456.0   
51   42.0  ...  161.100006  185.100006  167.035721  157.300003   466.0   
52   42.0  ...  189.899994  190.399994  184.720688  180.000000   466.0   
53   42.0  ...  163.100006  156.199997  153.746429  150.899994   466.0   
54   42.0  ...  175.100006  183.100006  174.758621  160.600006   446.0   
55   42.0  ...  167.600006  179.399994  170.572418  157.600006   456.0   
56   42.0  ...  172.699997  192.399994  171.437927  154.100006   465.0   
57   42.0  ...  185.300003  173.100006  162.460709  154.000000   456.0   
58   42.0  ...  146.899994  182.399994  170.379303  162.899994   446.0   

        X_2864  X_2865  Y_Class  prediction_label  prediction_score  
41  444.924530   424.0        0                 1            0.8413  
42  447.245270   423.0        0                 1            0.6733  
43  445.634613   423.0        2                 1            0.8696  
44  441.396240   423.0        1                 1            0.9306  
45  447.750000   432.0        0                 1            0.5848  
46  443.923065   423.0        1                 1            0.7573  
47  440.867920   423.0        1                 1            0.9266  
48  439.415100   422.0        1                 1            0.9504  
49  418.660370   396.0        2                 1            0.5236  
50  438.596161   422.0        1                 1            0.9441  
51  448.442322   433.0        1                 1            0.7969  
52  449.962250   434.0        0                 1            0.7283  
53  449.326935   432.0        2                 1            0.8155  
54  428.000000   413.0        1                 1            0.8910  
55  440.075470   422.0        1                 1            0.6051  
56  448.075470   423.0        1 

PRODUCT_CODE  X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  \
41             1    2.0   90.0    0.0   45.0   11.0  122.0   45.0   11.0   
42             1    1.0   88.0    0.0   45.0   11.0   96.0   45.0   11.0   
43             1    1.0   90.0    0.0   45.0   11.0   89.0   45.0   11.0   
44             1    1.0   90.0    0.0   45.0   11.0  125.0   45.0   11.0   
45             1    2.0   93.0    0.0   45.0   11.0    8.0   45.0   11.0   
46             1    1.0   90.0    0.0   45.0   11.0   35.0   45.0   11.0   
47             1    2.0   87.0    0.0   45.0   11.0  126.0   45.0   11.0   
48             1    1.0   95.0    0.0   45.0   11.0  148.0   45.0   11.0   
49             1    2.0   87.0    0.0   45.0   11.0  119.0   45.0   11.0   
50             1    1.0   89.0    0.0   45.0   11.0   45.0   45.0   11.0   
51             1    1.0   95.0    0.0   45.0   11.0   22.0   45.0   11.0   
52             1    2.0   88.0    0.0   45.0   11.0  127.0   45.0   11.0   
53             1    1.0   88.0    0.0   45.0   11.0  167.0   45.0   11.0   
54             1    1.0   91.0    0.0   45.0   11.0  111.0   45.0   11.0   
55             1    1.0   88.0    0.0   45.0   11.0   61.0   45.0   11.0   
56             1    2.0   87.0    0.0   45.0   11.0   78.0   45.0   11.0   
57             1    2.0   88.0    0.0   45.0   11.0   42.0   45.0   11.0   
58             1    1.0   87.0    0.0   45.0   11.0  105.0   45.0   11.0   

    X_254  ...      X_2859      X_2860      X_2861      X_2862  X_2863  \
41   42.0  ...  195.699997  201.199997  191.286209  181.699997   466.0   
42   42.0  ...  178.100006  170.899994  159.134476  149.199997   465.0   
43   42.0  ...  187.000000  181.600006  169.371429  156.100006   465.0   
44   42.0  ...  184.500000  196.199997  188.800003  175.699997   465.0   
45   42.0  ...  163.100006  177.800003  167.967850  158.399994   466.0   
46   42.0  ...  191.100006  174.500000  167.992859  161.800003   466.0   
47   42.0  ...  192.100006  192.000000  186.341385  175.100006   463.0   
48   42.0  ...  169.100006  198.899994  188.513794  181.000000   456.0   
49   42.0  ...  183.199997  197.500000  189.206894  181.800003   437.0   
50   42.0  ...  188.199997  179.899994  168.828568  156.300003   456.0   
51   42.0  ...  161.100006  185.100006  167.035721  157.300003   466.0   
52   42.0  ...  189.899994  190.399994  184.720688  180.000000   466.0   
53   42.0  ...  163.100006  156.199997  153.746429  150.899994   466.0   
54   42.0  ...  175.100006  183.100006  174.758621  160.600006   446.0   
55   42.0  ...  167.600006  179.399994  170.572418  157.600006   456.0   
56   42.0  ...  172.699997  192.399994  171.437927  154.100006   465.0   
57   42.0  ...  185.300003  173.100006  162.460709  154.000000   456.0   
58   42.0  ...  146.899994  182.399994  170.379303  162.899994   446.0   

        X_2864  X_2865  Y_Class  prediction_label  prediction_score  
41  444.924530   424.0        0                 1            0.4069  
42  447.245270   423.0        0                 1            0.4051  
43  445.634613   423.0        2                 1            0.4138  
44  441.396240   423.0        1                 1            0.4010  
45  447.750000   432.0        0                 1            0.4010  
46  443.923065   423.0        1                 1            0.4000  
47  440.867920   423.0        1                 1            0.3966  
48  439.415100   422.0        1                 1            0.3904  
49  418.660370   396.0        2                 1            0.3941  
50  438.596161   422.0        1                 1            0.3916  
51  448.442322   433.0        1                 1            0.3990  
52  449.962250   434.0        0                 1            0.4101  
53  449.326935   432.0        2                 1            0.4232  
54  428.000000   413.0        1                 1            0.4233  
55  440.075470   422.0        1                 1            0.4025  
56  448.075470   423.0        1 

PRODUCT_CODE  X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  \
41             1    2.0   90.0    0.0   45.0   11.0  122.0   45.0   11.0   
42             1    1.0   88.0    0.0   45.0   11.0   96.0   45.0   11.0   
43             1    1.0   90.0    0.0   45.0   11.0   89.0   45.0   11.0   
44             1    1.0   90.0    0.0   45.0   11.0  125.0   45.0   11.0   
45             1    2.0   93.0    0.0   45.0   11.0    8.0   45.0   11.0   
46             1    1.0   90.0    0.0   45.0   11.0   35.0   45.0   11.0   
47             1    2.0   87.0    0.0   45.0   11.0  126.0   45.0   11.0   
48             1    1.0   95.0    0.0   45.0   11.0  148.0   45.0   11.0   
49             1    2.0   87.0    0.0   45.0   11.0  119.0   45.0   11.0   
50             1    1.0   89.0    0.0   45.0   11.0   45.0   45.0   11.0   
51             1    1.0   95.0    0.0   45.0   11.0   22.0   45.0   11.0   
52             1    2.0   88.0    0.0   45.0   11.0  127.0   45.0   11.0   
53             1    1.0   88.0    0.0   45.0   11.0  167.0   45.0   11.0   
54             1    1.0   91.0    0.0   45.0   11.0  111.0   45.0   11.0   
55             1    1.0   88.0    0.0   45.0   11.0   61.0   45.0   11.0   
56             1    2.0   87.0    0.0   45.0   11.0   78.0   45.0   11.0   
57             1    2.0   88.0    0.0   45.0   11.0   42.0   45.0   11.0   
58             1    1.0   87.0    0.0   45.0   11.0  105.0   45.0   11.0   

    X_254  ...      X_2859      X_2860      X_2861      X_2862  X_2863  \
41   42.0  ...  195.699997  201.199997  191.286209  181.699997   466.0   
42   42.0  ...  178.100006  170.899994  159.134476  149.199997   465.0   
43   42.0  ...  187.000000  181.600006  169.371429  156.100006   465.0   
44   42.0  ...  184.500000  196.199997  188.800003  175.699997   465.0   
45   42.0  ...  163.100006  177.800003  167.967850  158.399994   466.0   
46   42.0  ...  191.100006  174.500000  167.992859  161.800003   466.0   
47   42.0  ...  192.100006  192.000000  186.341385  175.100006   463.0   
48   42.0  ...  169.100006  198.899994  188.513794  181.000000   456.0   
49   42.0  ...  183.199997  197.500000  189.206894  181.800003   437.0   
50   42.0  ...  188.199997  179.899994  168.828568  156.300003   456.0   
51   42.0  ...  161.100006  185.100006  167.035721  157.300003   466.0   
52   42.0  ...  189.899994  190.399994  184.720688  180.000000   466.0   
53   42.0  ...  163.100006  156.199997  153.746429  150.899994   466.0   
54   42.0  ...  175.100006  183.100006  174.758621  160.600006   446.0   
55   42.0  ...  167.600006  179.399994  170.572418  157.600006   456.0   
56   42.0  ...  172.699997  192.399994  171.437927  154.100006   465.0   
57   42.0  ...  185.300003  173.100006  162.460709  154.000000   456.0   
58   42.0  ...  146.899994  182.399994  170.379303  162.899994   446.0   

        X_2864  X_2865  Y_Class  prediction_label  prediction_score  
41  444.924530   424.0        0                 1            0.8072  
42  447.245270   423.0        0                 1            0.9134  
43  445.634613   423.0        2                 1            0.6645  
44  441.396240   423.0        1                 1            0.9074  
45  447.750000   432.0        0                 1            0.7223  
46  443.923065   423.0        1                 0            0.5029  
47  440.867920   423.0        1                 1            0.7344  
48  439.415100   422.0        1                 1            0.7231  
49  418.660370   396.0        2                 2            0.6273  
50  438.596161   422.0        1                 1            0.9471  
51  448.442322   433.0        1                 0            0.8584  
52  449.962250   434.0        0                 1            0.9060  
53  449.326935   432.0        2                 1            0.8752  
54  428.000000   413.0        1                 1            0.7581  
55  440.075470   422.0        1                 0            0.5922  
56  448.075470   423.0        1 

PRODUCT_CODE  X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  \
41             1    2.0   90.0    0.0   45.0   11.0  122.0   45.0   11.0   
42             1    1.0   88.0    0.0   45.0   11.0   96.0   45.0   11.0   
43             1    1.0   90.0    0.0   45.0   11.0   89.0   45.0   11.0   
44             1    1.0   90.0    0.0   45.0   11.0  125.0   45.0   11.0   
45             1    2.0   93.0    0.0   45.0   11.0    8.0   45.0   11.0   
46             1    1.0   90.0    0.0   45.0   11.0   35.0   45.0   11.0   
47             1    2.0   87.0    0.0   45.0   11.0  126.0   45.0   11.0   
48             1    1.0   95.0    0.0   45.0   11.0  148.0   45.0   11.0   
49             1    2.0   87.0    0.0   45.0   11.0  119.0   45.0   11.0   
50             1    1.0   89.0    0.0   45.0   11.0   45.0   45.0   11.0   
51             1    1.0   95.0    0.0   45.0   11.0   22.0   45.0   11.0   
52             1    2.0   88.0    0.0   45.0   11.0  127.0   45.0   11.0   
53             1    1.0   88.0    0.0   45.0   11.0  167.0   45.0   11.0   
54             1    1.0   91.0    0.0   45.0   11.0  111.0   45.0   11.0   
55             1    1.0   88.0    0.0   45.0   11.0   61.0   45.0   11.0   
56             1    2.0   87.0    0.0   45.0   11.0   78.0   45.0   11.0   
57             1    2.0   88.0    0.0   45.0   11.0   42.0   45.0   11.0   
58             1    1.0   87.0    0.0   45.0   11.0  105.0   45.0   11.0   

    X_254  ...      X_2859      X_2860      X_2861      X_2862  X_2863  \
41   42.0  ...  195.699997  201.199997  191.286209  181.699997   466.0   
42   42.0  ...  178.100006  170.899994  159.134476  149.199997   465.0   
43   42.0  ...  187.000000  181.600006  169.371429  156.100006   465.0   
44   42.0  ...  184.500000  196.199997  188.800003  175.699997   465.0   
45   42.0  ...  163.100006  177.800003  167.967850  158.399994   466.0   
46   42.0  ...  191.100006  174.500000  167.992859  161.800003   466.0   
47   42.0  ...  192.100006  192.000000  186.341385  175.100006   463.0   
48   42.0  ...  169.100006  198.899994  188.513794  181.000000   456.0   
49   42.0  ...  183.199997  197.500000  189.206894  181.800003   437.0   
50   42.0  ...  188.199997  179.899994  168.828568  156.300003   456.0   
51   42.0  ...  161.100006  185.100006  167.035721  157.300003   466.0   
52   42.0  ...  189.899994  190.399994  184.720688  180.000000   466.0   
53   42.0  ...  163.100006  156.199997  153.746429  150.899994   466.0   
54   42.0  ...  175.100006  183.100006  174.758621  160.600006   446.0   
55   42.0  ...  167.600006  179.399994  170.572418  157.600006   456.0   
56   42.0  ...  172.699997  192.399994  171.437927  154.100006   465.0   
57   42.0  ...  185.300003  173.100006  162.460709  154.000000   456.0   
58   42.0  ...  146.899994  182.399994  170.379303  162.899994   446.0   

        X_2864  X_2865  Y_Class  prediction_label  prediction_score  
41  444.924530   424.0        0                 1              0.75  
42  447.245270   423.0        0                 1              0.57  
43  445.634613   423.0        2                 1              0.56  
44  441.396240   423.0        1                 1              0.59  
45  447.750000   432.0        0                 0              0.56  
46  443.923065   423.0        1                 1              0.60  
47  440.867920   423.0        1                 1              0.55  
48  439.415100   422.0        1                 1              0.64  
49  418.660370   396.0        2                 2              0.84  
50  438.596161   422.0        1                 1              0.77  
51  448.442322   433.0        1                 1              0.70  
52  449.962250   434.0        0                 2              0.55  
53  449.326935   432.0        2                 1              0.64  
54  428.000000   413.0        1                 1              0.76  
55  440.075470   422.0        1                 1              0.70  
56  448.075470   423.0        1 

In [213]:
T010305_final_classification_model = finalize_model(T010305_model_et)

In [214]:
#최종 예측
#29
T010305_prediction = predict_model(T010305_final_classification_model, data=T010305_data)
#prediction.drop(['Y_Quality'], axis = 1, inplace = True)

# T010306

In [215]:
T010306_class = T010306['Y_Class']
T010306_target = T010306['Y_Quality']
T010306_data = T010306.drop(['Y_Class', 'Y_Quality'], axis = 1)
T010306_data

PRODUCT_CODE  X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  \
27              1    1.0   87.0  144.0   45.0   12.0    0.0   45.0   12.0   
31              1    4.0   93.0  150.0   45.0   12.0    0.0   45.0   12.0   
32              1    1.0   89.0  152.0   45.0   12.0    0.0   45.0   12.0   
38              1    2.0   91.0  158.0   45.0   11.0    0.0   45.0   12.0   
47              1    1.0   95.0  166.0   45.0   11.0    0.0   45.0   12.0   
..            ...    ...    ...    ...    ...    ...    ...    ...    ...   
479             1    1.0   93.0  107.0   45.0   11.0    0.0   45.0   12.0   
501             1    2.0   95.0  124.0   45.0   11.0    0.0   45.0   12.0   
523             1    1.0   89.0  136.0   45.0   12.0    0.0   45.0   12.0   
531             1    1.0   90.0  142.0   45.0   11.0    0.0   45.0   12.0   
585             1    1.0   93.0   63.0   45.0   12.0    0.0   45.0   12.0   

     X_254  ...  X_2856  X_2857      X_2858  X_2859  X_2860      X_2861  \
27    51.0  ...   177.1   186.2  169.907143   156.5   188.4  175.225000   
31    51.0  ...   170.8   207.8  191.775862   166.0   195.1  188.696552   
32    51.0  ...   174.5   190.7  181.686207   172.7   180.0  168.775862   
38    51.0  ...   167.9   200.3  187.339286   180.1   184.3  177.528571   
47    51.0  ...   173.1   203.7  188.434483   165.3   185.9  173.596552   
..     ...  ...     ...     ...         ...     ...     ...         ...   
479   51.0  ...   199.7   222.6  193.278571   177.5   183.3  169.553571   
501   51.0  ...   196.1   211.1  197.392857   173.1   187.6  182.142857   
523   51.0  ...   203.2   205.1  194.860714   183.9   189.2  181.700000   
531   51.0  ...   189.0   201.3  190.407143   181.1   192.6  185.207143   
585   51.0  ...   204.1   216.0  205.079310   196.1   192.2  187.396552   

     X_2862  X_2863      X_2864  X_2865  
27    159.9   446.0  430.442308   413.0  
31    181.7   446.0  429.245283   413.0  
32    154.1   446.0  429.981132   415.0  
38    166.6   446.0  426.250000   404.0  
47    157.2   447.0  429.905660   413.0  
..      ...     ...         ...     ...  
479   154.2   456.0  438.132075   413.0  
501   175.1   466.0  445.307692   425.0  
523   172.7   466.0  444.615385   423.0  
531   173.2   466.0  446.038461   427.0  
585   176.7   472.0  450.339623   432.0  

[70 rows x 887 columns]

In [216]:
from pycaret.classification import *
# 분류 패키지의 모든 모듈을 임포트한다.
exp_clf101 = setup(data=T010306_data, 
                   target=T010306_class, 
                   fold=5,
                   session_id=414)
top5 = compare_models(sort='Accuracy', n_select=5)

Processing:   0%|          | 0/73 [00:00<?, ?it/s]

In [217]:
T010306_total_models = []

T010306_model_ada = create_model('ada', fold = 5)
T010306_total_models.append(T010306_model_ada)

T010306_model_gbc = create_model('gbc', fold = 5)
T010306_total_models.append(T010306_model_gbc)

T010306_model_et = create_model('et', fold = 5)
T010306_total_models.append(T010306_model_et)

T010306_model_catboost = create_model('catboost', fold = 5)
T010306_total_models.append(T010306_model_catboost)

T010306_model_xgb = create_model('xgboost', fold = 5)
T010306_total_models.append(T010306_model_xgb)

T010306_model_rf = create_model('rf', fold = 5)
T010306_total_models.append(T010306_model_rf)

T010306_model_lightgbm = create_model('lightgbm', fold = 5)
T010306_total_models.append(T010306_model_lightgbm)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [218]:
T010306_model_ada = tune_model(T010306_model_ada, fold=5, choose_better = True)

T010306_model_gbc = tune_model(T010306_model_gbc, fold=5, choose_better = True)

T010306_model_et = tune_model(T010306_model_et, fold=5, choose_better = True)

T010306_model_catboost = tune_model(T010306_model_catboost, fold=5, choose_better = True)

T010306_model_xgb = tune_model(T010306_model_xgb, fold=5, choose_better = True)

T010306_model_rf = tune_model(T010306_model_rf, fold=5, choose_better = True)

T010306_model_lightgbm = tune_model(T010306_model_lightgbm, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


In [219]:
T010306_tuned_models = [T010306_model_ada, T010306_model_gbc, T010306_model_et, T010306_model_catboost, T010306_model_xgb, T010306_model_rf, T010306_model_lightgbm]
T010306_tuned_models

[AdaBoostClassifier(algorithm='SAMME', base_estimator=None, learning_rate=0.15,
                    n_estimators=40, random_state=414),
 GradientBoostingClassifier(ccp_alpha=0.0, criterion='friedman_mse', init=None,
                            learning_rate=0.2, loss='deviance', max_depth=1,
                            max_features='sqrt', max_leaf_nodes=None,
                            min_impurity_decrease=0.002, min_samples_leaf=1,
                            min_samples_split=7, min_weight_fraction_leaf=0.0,
                            n_estimators=110, n_iter_no_change=None,
                            random_state=414, subsample=0.45, tol=0.0001,
                            validation_fraction=0.1, verbose=0,
                            warm_start=False),
 ExtraTreesClassifier(bootstrap=False, ccp_alpha=0.0, class_weight=None,
                      criterion='gini', max_depth=None, max_features='auto',
                      max_leaf_nodes=None, max_samples=None,
                

In [220]:
for model in T010306_tuned_models:
    display(predict_model(model))

PRODUCT_CODE  X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  \
49             1    1.0   90.0   84.0   45.0   11.0    0.0   45.0   12.0   
50             1    1.0   91.0    1.0   45.0   12.0    0.0   45.0   12.0   
51             1    1.0   95.0  145.0   45.0   11.0    0.0   45.0   12.0   
52             1    1.0   95.0  142.0   45.0   12.0    0.0   45.0   12.0   
53             1    2.0   91.0  170.0   45.0   11.0    0.0   45.0   12.0   
54             1    1.0   88.0   25.0   45.0   12.0    0.0   45.0   12.0   
55             1    1.0   93.0  138.0   45.0   11.0    0.0   45.0   12.0   
56             1    2.0   95.0    7.0   45.0   12.0    0.0   45.0   12.0   
57             1    1.0   93.0  107.0   45.0   11.0    0.0   45.0   12.0   
58             1    2.0   88.0   77.0   45.0   12.0    0.0   45.0   12.0   
59             1    2.0   91.0  158.0   45.0   11.0    0.0   45.0   12.0   
60             1    2.0   89.0  149.0   45.0   11.0    0.0   45.0   12.0   
61             1    2.0   95.0  170.0   45.0   12.0    0.0   45.0   12.0   
62             1    1.0   88.0   92.0   45.0   12.0    0.0   45.0   12.0   
63             1    1.0   91.0  138.0   45.0   12.0    0.0   45.0   12.0   
64             1    1.0   88.0   54.0   45.0   11.0    0.0   45.0   12.0   
65             1    1.0   93.0   63.0   45.0   12.0    0.0   45.0   12.0   
66             1    1.0   87.0  144.0   45.0   12.0    0.0   45.0   12.0   
67             1    1.0   93.0  129.0   45.0   11.0    0.0   45.0   12.0   
68             1    2.0   89.0   67.0   45.0   11.0    0.0   45.0   12.0   
69             1    2.0   91.0   81.0   45.0   12.0    0.0   45.0   12.0   

    X_254  ...      X_2859      X_2860      X_2861      X_2862  X_2863  \
49   51.0  ...  165.699997  198.600006  185.696426  169.000000   465.0   
50   51.0  ...  167.399994  185.000000  179.503571  172.600006   466.0   
51   51.0  ...  186.100006  181.199997  167.639282  158.000000   456.0   
52   51.0  ...  185.300003  171.199997  164.860718  157.500000   456.0   
53   51.0  ...  160.500000  194.100006  180.189285  165.500000   446.0   
54   51.0  ...  184.100006  180.399994  169.782150  161.500000   466.0   
55   51.0  ...  187.500000  185.899994  172.920685  151.100006   466.0   
56   51.0  ...  161.100006  152.000000  143.085709  132.000000   473.0   
57   51.0  ...  177.500000  183.300003  169.553574  154.199997   456.0   
58   51.0  ...  189.100006  184.800003  178.096558  166.300003   456.0   
59   51.0  ...  180.100006  184.300003  177.528564  166.600006   446.0   
60   51.0  ...  172.000000  183.600006  171.437927  163.899994   447.0   
61   51.0  ...  178.699997  189.800003  177.810715  159.699997   447.0   
62   51.0  ...  188.399994  188.300003  177.379303  166.600006   456.0   
63   51.0  ...  165.199997  175.300003  166.265518  153.899994   466.0   
64   51.0  ...  188.800003  191.199997  181.581482  168.199997   463.0   
65   51.0  ...  196.100006  192.199997  187.396545  176.699997   472.0   
66   51.0  ...  156.500000  188.399994  175.225006  159.899994   446.0   
67   51.0  ...  177.399994  170.500000  153.157150  143.899994   456.0   
68   51.0  ...  190.300003  176.399994  168.962967  157.000000   465.0   
69   51.0  ...  160.100006  176.000000  161.782150  147.199997   466.0   

        X_2864  X_2865  Y_Class  prediction_label  prediction_score  
49  449.442322   432.0        2                 2            0.3654  
50  447.769226   422.0        0                 1            0.3765  
51  439.961548   422.0        1                 2            0.3649  
52  440.288452   423.0        1                 1            0.3576  
53  430.942322   413.0        2                 2            0.3643  
54  446.557678   423.0        1                 1            0.3809  
55  446.169800   424.0        2                 2            0.3835  
56  450.692322   432.0        1                 1            0.3537  
57  438.132080   413.0        1                 1            0.3696  
58

PRODUCT_CODE  X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  \
49             1    1.0   90.0   84.0   45.0   11.0    0.0   45.0   12.0   
50             1    1.0   91.0    1.0   45.0   12.0    0.0   45.0   12.0   
51             1    1.0   95.0  145.0   45.0   11.0    0.0   45.0   12.0   
52             1    1.0   95.0  142.0   45.0   12.0    0.0   45.0   12.0   
53             1    2.0   91.0  170.0   45.0   11.0    0.0   45.0   12.0   
54             1    1.0   88.0   25.0   45.0   12.0    0.0   45.0   12.0   
55             1    1.0   93.0  138.0   45.0   11.0    0.0   45.0   12.0   
56             1    2.0   95.0    7.0   45.0   12.0    0.0   45.0   12.0   
57             1    1.0   93.0  107.0   45.0   11.0    0.0   45.0   12.0   
58             1    2.0   88.0   77.0   45.0   12.0    0.0   45.0   12.0   
59             1    2.0   91.0  158.0   45.0   11.0    0.0   45.0   12.0   
60             1    2.0   89.0  149.0   45.0   11.0    0.0   45.0   12.0   
61             1    2.0   95.0  170.0   45.0   12.0    0.0   45.0   12.0   
62             1    1.0   88.0   92.0   45.0   12.0    0.0   45.0   12.0   
63             1    1.0   91.0  138.0   45.0   12.0    0.0   45.0   12.0   
64             1    1.0   88.0   54.0   45.0   11.0    0.0   45.0   12.0   
65             1    1.0   93.0   63.0   45.0   12.0    0.0   45.0   12.0   
66             1    1.0   87.0  144.0   45.0   12.0    0.0   45.0   12.0   
67             1    1.0   93.0  129.0   45.0   11.0    0.0   45.0   12.0   
68             1    2.0   89.0   67.0   45.0   11.0    0.0   45.0   12.0   
69             1    2.0   91.0   81.0   45.0   12.0    0.0   45.0   12.0   

    X_254  ...      X_2859      X_2860      X_2861      X_2862  X_2863  \
49   51.0  ...  165.699997  198.600006  185.696426  169.000000   465.0   
50   51.0  ...  167.399994  185.000000  179.503571  172.600006   466.0   
51   51.0  ...  186.100006  181.199997  167.639282  158.000000   456.0   
52   51.0  ...  185.300003  171.199997  164.860718  157.500000   456.0   
53   51.0  ...  160.500000  194.100006  180.189285  165.500000   446.0   
54   51.0  ...  184.100006  180.399994  169.782150  161.500000   466.0   
55   51.0  ...  187.500000  185.899994  172.920685  151.100006   466.0   
56   51.0  ...  161.100006  152.000000  143.085709  132.000000   473.0   
57   51.0  ...  177.500000  183.300003  169.553574  154.199997   456.0   
58   51.0  ...  189.100006  184.800003  178.096558  166.300003   456.0   
59   51.0  ...  180.100006  184.300003  177.528564  166.600006   446.0   
60   51.0  ...  172.000000  183.600006  171.437927  163.899994   447.0   
61   51.0  ...  178.699997  189.800003  177.810715  159.699997   447.0   
62   51.0  ...  188.399994  188.300003  177.379303  166.600006   456.0   
63   51.0  ...  165.199997  175.300003  166.265518  153.899994   466.0   
64   51.0  ...  188.800003  191.199997  181.581482  168.199997   463.0   
65   51.0  ...  196.100006  192.199997  187.396545  176.699997   472.0   
66   51.0  ...  156.500000  188.399994  175.225006  159.899994   446.0   
67   51.0  ...  177.399994  170.500000  153.157150  143.899994   456.0   
68   51.0  ...  190.300003  176.399994  168.962967  157.000000   465.0   
69   51.0  ...  160.100006  176.000000  161.782150  147.199997   466.0   

        X_2864  X_2865  Y_Class  prediction_label  prediction_score  
49  449.442322   432.0        2                 2            0.6893  
50  447.769226   422.0        0                 1            0.4986  
51  439.961548   422.0        1                 2            0.7601  
52  440.288452   423.0        1                 1            0.4990  
53  430.942322   413.0        2                 2            0.9664  
54  446.557678   423.0        1                 1            0.9305  
55  446.169800   424.0        2                 2            0.9792  
56  450.692322   432.0        1                 2            0.8092  
57  438.132080   413.0        1                 1            0.8627  
58

PRODUCT_CODE  X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  \
49             1    1.0   90.0   84.0   45.0   11.0    0.0   45.0   12.0   
50             1    1.0   91.0    1.0   45.0   12.0    0.0   45.0   12.0   
51             1    1.0   95.0  145.0   45.0   11.0    0.0   45.0   12.0   
52             1    1.0   95.0  142.0   45.0   12.0    0.0   45.0   12.0   
53             1    2.0   91.0  170.0   45.0   11.0    0.0   45.0   12.0   
54             1    1.0   88.0   25.0   45.0   12.0    0.0   45.0   12.0   
55             1    1.0   93.0  138.0   45.0   11.0    0.0   45.0   12.0   
56             1    2.0   95.0    7.0   45.0   12.0    0.0   45.0   12.0   
57             1    1.0   93.0  107.0   45.0   11.0    0.0   45.0   12.0   
58             1    2.0   88.0   77.0   45.0   12.0    0.0   45.0   12.0   
59             1    2.0   91.0  158.0   45.0   11.0    0.0   45.0   12.0   
60             1    2.0   89.0  149.0   45.0   11.0    0.0   45.0   12.0   
61             1    2.0   95.0  170.0   45.0   12.0    0.0   45.0   12.0   
62             1    1.0   88.0   92.0   45.0   12.0    0.0   45.0   12.0   
63             1    1.0   91.0  138.0   45.0   12.0    0.0   45.0   12.0   
64             1    1.0   88.0   54.0   45.0   11.0    0.0   45.0   12.0   
65             1    1.0   93.0   63.0   45.0   12.0    0.0   45.0   12.0   
66             1    1.0   87.0  144.0   45.0   12.0    0.0   45.0   12.0   
67             1    1.0   93.0  129.0   45.0   11.0    0.0   45.0   12.0   
68             1    2.0   89.0   67.0   45.0   11.0    0.0   45.0   12.0   
69             1    2.0   91.0   81.0   45.0   12.0    0.0   45.0   12.0   

    X_254  ...      X_2859      X_2860      X_2861      X_2862  X_2863  \
49   51.0  ...  165.699997  198.600006  185.696426  169.000000   465.0   
50   51.0  ...  167.399994  185.000000  179.503571  172.600006   466.0   
51   51.0  ...  186.100006  181.199997  167.639282  158.000000   456.0   
52   51.0  ...  185.300003  171.199997  164.860718  157.500000   456.0   
53   51.0  ...  160.500000  194.100006  180.189285  165.500000   446.0   
54   51.0  ...  184.100006  180.399994  169.782150  161.500000   466.0   
55   51.0  ...  187.500000  185.899994  172.920685  151.100006   466.0   
56   51.0  ...  161.100006  152.000000  143.085709  132.000000   473.0   
57   51.0  ...  177.500000  183.300003  169.553574  154.199997   456.0   
58   51.0  ...  189.100006  184.800003  178.096558  166.300003   456.0   
59   51.0  ...  180.100006  184.300003  177.528564  166.600006   446.0   
60   51.0  ...  172.000000  183.600006  171.437927  163.899994   447.0   
61   51.0  ...  178.699997  189.800003  177.810715  159.699997   447.0   
62   51.0  ...  188.399994  188.300003  177.379303  166.600006   456.0   
63   51.0  ...  165.199997  175.300003  166.265518  153.899994   466.0   
64   51.0  ...  188.800003  191.199997  181.581482  168.199997   463.0   
65   51.0  ...  196.100006  192.199997  187.396545  176.699997   472.0   
66   51.0  ...  156.500000  188.399994  175.225006  159.899994   446.0   
67   51.0  ...  177.399994  170.500000  153.157150  143.899994   456.0   
68   51.0  ...  190.300003  176.399994  168.962967  157.000000   465.0   
69   51.0  ...  160.100006  176.000000  161.782150  147.199997   466.0   

        X_2864  X_2865  Y_Class  prediction_label  prediction_score  
49  449.442322   432.0        2                 1              0.50  
50  447.769226   422.0        0                 1              0.34  
51  439.961548   422.0        1                 2              0.59  
52  440.288452   423.0        1                 1              0.60  
53  430.942322   413.0        2                 2              0.75  
54  446.557678   423.0        1                 1              0.72  
55  446.169800   424.0        2                 2              0.73  
56  450.692322   432.0        1                 1              0.48  
57  438.132080   413.0        1                 1              0.57  
58

PRODUCT_CODE  X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  \
49             1    1.0   90.0   84.0   45.0   11.0    0.0   45.0   12.0   
50             1    1.0   91.0    1.0   45.0   12.0    0.0   45.0   12.0   
51             1    1.0   95.0  145.0   45.0   11.0    0.0   45.0   12.0   
52             1    1.0   95.0  142.0   45.0   12.0    0.0   45.0   12.0   
53             1    2.0   91.0  170.0   45.0   11.0    0.0   45.0   12.0   
54             1    1.0   88.0   25.0   45.0   12.0    0.0   45.0   12.0   
55             1    1.0   93.0  138.0   45.0   11.0    0.0   45.0   12.0   
56             1    2.0   95.0    7.0   45.0   12.0    0.0   45.0   12.0   
57             1    1.0   93.0  107.0   45.0   11.0    0.0   45.0   12.0   
58             1    2.0   88.0   77.0   45.0   12.0    0.0   45.0   12.0   
59             1    2.0   91.0  158.0   45.0   11.0    0.0   45.0   12.0   
60             1    2.0   89.0  149.0   45.0   11.0    0.0   45.0   12.0   
61             1    2.0   95.0  170.0   45.0   12.0    0.0   45.0   12.0   
62             1    1.0   88.0   92.0   45.0   12.0    0.0   45.0   12.0   
63             1    1.0   91.0  138.0   45.0   12.0    0.0   45.0   12.0   
64             1    1.0   88.0   54.0   45.0   11.0    0.0   45.0   12.0   
65             1    1.0   93.0   63.0   45.0   12.0    0.0   45.0   12.0   
66             1    1.0   87.0  144.0   45.0   12.0    0.0   45.0   12.0   
67             1    1.0   93.0  129.0   45.0   11.0    0.0   45.0   12.0   
68             1    2.0   89.0   67.0   45.0   11.0    0.0   45.0   12.0   
69             1    2.0   91.0   81.0   45.0   12.0    0.0   45.0   12.0   

    X_254  ...      X_2859      X_2860      X_2861      X_2862  X_2863  \
49   51.0  ...  165.699997  198.600006  185.696426  169.000000   465.0   
50   51.0  ...  167.399994  185.000000  179.503571  172.600006   466.0   
51   51.0  ...  186.100006  181.199997  167.639282  158.000000   456.0   
52   51.0  ...  185.300003  171.199997  164.860718  157.500000   456.0   
53   51.0  ...  160.500000  194.100006  180.189285  165.500000   446.0   
54   51.0  ...  184.100006  180.399994  169.782150  161.500000   466.0   
55   51.0  ...  187.500000  185.899994  172.920685  151.100006   466.0   
56   51.0  ...  161.100006  152.000000  143.085709  132.000000   473.0   
57   51.0  ...  177.500000  183.300003  169.553574  154.199997   456.0   
58   51.0  ...  189.100006  184.800003  178.096558  166.300003   456.0   
59   51.0  ...  180.100006  184.300003  177.528564  166.600006   446.0   
60   51.0  ...  172.000000  183.600006  171.437927  163.899994   447.0   
61   51.0  ...  178.699997  189.800003  177.810715  159.699997   447.0   
62   51.0  ...  188.399994  188.300003  177.379303  166.600006   456.0   
63   51.0  ...  165.199997  175.300003  166.265518  153.899994   466.0   
64   51.0  ...  188.800003  191.199997  181.581482  168.199997   463.0   
65   51.0  ...  196.100006  192.199997  187.396545  176.699997   472.0   
66   51.0  ...  156.500000  188.399994  175.225006  159.899994   446.0   
67   51.0  ...  177.399994  170.500000  153.157150  143.899994   456.0   
68   51.0  ...  190.300003  176.399994  168.962967  157.000000   465.0   
69   51.0  ...  160.100006  176.000000  161.782150  147.199997   466.0   

        X_2864  X_2865  Y_Class  prediction_label  prediction_score  
49  449.442322   432.0        2                 2            0.5555  
50  447.769226   422.0        0                 1            0.6845  
51  439.961548   422.0        1                 2            0.6968  
52  440.288452   423.0        1                 1            0.8519  
53  430.942322   413.0        2                 2            0.8629  
54  446.557678   423.0        1                 1            0.8253  
55  446.169800   424.0        2                 2            0.8514  
56  450.692322   432.0        1                 1            0.6905  
57  438.132080   413.0        1                 1            0.7052  
58

PRODUCT_CODE  X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  \
49             1    1.0   90.0   84.0   45.0   11.0    0.0   45.0   12.0   
50             1    1.0   91.0    1.0   45.0   12.0    0.0   45.0   12.0   
51             1    1.0   95.0  145.0   45.0   11.0    0.0   45.0   12.0   
52             1    1.0   95.0  142.0   45.0   12.0    0.0   45.0   12.0   
53             1    2.0   91.0  170.0   45.0   11.0    0.0   45.0   12.0   
54             1    1.0   88.0   25.0   45.0   12.0    0.0   45.0   12.0   
55             1    1.0   93.0  138.0   45.0   11.0    0.0   45.0   12.0   
56             1    2.0   95.0    7.0   45.0   12.0    0.0   45.0   12.0   
57             1    1.0   93.0  107.0   45.0   11.0    0.0   45.0   12.0   
58             1    2.0   88.0   77.0   45.0   12.0    0.0   45.0   12.0   
59             1    2.0   91.0  158.0   45.0   11.0    0.0   45.0   12.0   
60             1    2.0   89.0  149.0   45.0   11.0    0.0   45.0   12.0   
61             1    2.0   95.0  170.0   45.0   12.0    0.0   45.0   12.0   
62             1    1.0   88.0   92.0   45.0   12.0    0.0   45.0   12.0   
63             1    1.0   91.0  138.0   45.0   12.0    0.0   45.0   12.0   
64             1    1.0   88.0   54.0   45.0   11.0    0.0   45.0   12.0   
65             1    1.0   93.0   63.0   45.0   12.0    0.0   45.0   12.0   
66             1    1.0   87.0  144.0   45.0   12.0    0.0   45.0   12.0   
67             1    1.0   93.0  129.0   45.0   11.0    0.0   45.0   12.0   
68             1    2.0   89.0   67.0   45.0   11.0    0.0   45.0   12.0   
69             1    2.0   91.0   81.0   45.0   12.0    0.0   45.0   12.0   

    X_254  ...      X_2859      X_2860      X_2861      X_2862  X_2863  \
49   51.0  ...  165.699997  198.600006  185.696426  169.000000   465.0   
50   51.0  ...  167.399994  185.000000  179.503571  172.600006   466.0   
51   51.0  ...  186.100006  181.199997  167.639282  158.000000   456.0   
52   51.0  ...  185.300003  171.199997  164.860718  157.500000   456.0   
53   51.0  ...  160.500000  194.100006  180.189285  165.500000   446.0   
54   51.0  ...  184.100006  180.399994  169.782150  161.500000   466.0   
55   51.0  ...  187.500000  185.899994  172.920685  151.100006   466.0   
56   51.0  ...  161.100006  152.000000  143.085709  132.000000   473.0   
57   51.0  ...  177.500000  183.300003  169.553574  154.199997   456.0   
58   51.0  ...  189.100006  184.800003  178.096558  166.300003   456.0   
59   51.0  ...  180.100006  184.300003  177.528564  166.600006   446.0   
60   51.0  ...  172.000000  183.600006  171.437927  163.899994   447.0   
61   51.0  ...  178.699997  189.800003  177.810715  159.699997   447.0   
62   51.0  ...  188.399994  188.300003  177.379303  166.600006   456.0   
63   51.0  ...  165.199997  175.300003  166.265518  153.899994   466.0   
64   51.0  ...  188.800003  191.199997  181.581482  168.199997   463.0   
65   51.0  ...  196.100006  192.199997  187.396545  176.699997   472.0   
66   51.0  ...  156.500000  188.399994  175.225006  159.899994   446.0   
67   51.0  ...  177.399994  170.500000  153.157150  143.899994   456.0   
68   51.0  ...  190.300003  176.399994  168.962967  157.000000   465.0   
69   51.0  ...  160.100006  176.000000  161.782150  147.199997   466.0   

        X_2864  X_2865  Y_Class  prediction_label  prediction_score  
49  449.442322   432.0        2                 2            0.9663  
50  447.769226   422.0        0                 1            0.7202  
51  439.961548   422.0        1                 2            0.7805  
52  440.288452   423.0        1                 1            0.7007  
53  430.942322   413.0        2                 2            0.8919  
54  446.557678   423.0        1                 1            0.9136  
55  446.169800   424.0        2                 2            0.9603  
56  450.692322   432.0        1                 0            0.7923  
57  438.132080   413.0        1                 1            0.7745  
58

PRODUCT_CODE  X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  \
49             1    1.0   90.0   84.0   45.0   11.0    0.0   45.0   12.0   
50             1    1.0   91.0    1.0   45.0   12.0    0.0   45.0   12.0   
51             1    1.0   95.0  145.0   45.0   11.0    0.0   45.0   12.0   
52             1    1.0   95.0  142.0   45.0   12.0    0.0   45.0   12.0   
53             1    2.0   91.0  170.0   45.0   11.0    0.0   45.0   12.0   
54             1    1.0   88.0   25.0   45.0   12.0    0.0   45.0   12.0   
55             1    1.0   93.0  138.0   45.0   11.0    0.0   45.0   12.0   
56             1    2.0   95.0    7.0   45.0   12.0    0.0   45.0   12.0   
57             1    1.0   93.0  107.0   45.0   11.0    0.0   45.0   12.0   
58             1    2.0   88.0   77.0   45.0   12.0    0.0   45.0   12.0   
59             1    2.0   91.0  158.0   45.0   11.0    0.0   45.0   12.0   
60             1    2.0   89.0  149.0   45.0   11.0    0.0   45.0   12.0   
61             1    2.0   95.0  170.0   45.0   12.0    0.0   45.0   12.0   
62             1    1.0   88.0   92.0   45.0   12.0    0.0   45.0   12.0   
63             1    1.0   91.0  138.0   45.0   12.0    0.0   45.0   12.0   
64             1    1.0   88.0   54.0   45.0   11.0    0.0   45.0   12.0   
65             1    1.0   93.0   63.0   45.0   12.0    0.0   45.0   12.0   
66             1    1.0   87.0  144.0   45.0   12.0    0.0   45.0   12.0   
67             1    1.0   93.0  129.0   45.0   11.0    0.0   45.0   12.0   
68             1    2.0   89.0   67.0   45.0   11.0    0.0   45.0   12.0   
69             1    2.0   91.0   81.0   45.0   12.0    0.0   45.0   12.0   

    X_254  ...      X_2859      X_2860      X_2861      X_2862  X_2863  \
49   51.0  ...  165.699997  198.600006  185.696426  169.000000   465.0   
50   51.0  ...  167.399994  185.000000  179.503571  172.600006   466.0   
51   51.0  ...  186.100006  181.199997  167.639282  158.000000   456.0   
52   51.0  ...  185.300003  171.199997  164.860718  157.500000   456.0   
53   51.0  ...  160.500000  194.100006  180.189285  165.500000   446.0   
54   51.0  ...  184.100006  180.399994  169.782150  161.500000   466.0   
55   51.0  ...  187.500000  185.899994  172.920685  151.100006   466.0   
56   51.0  ...  161.100006  152.000000  143.085709  132.000000   473.0   
57   51.0  ...  177.500000  183.300003  169.553574  154.199997   456.0   
58   51.0  ...  189.100006  184.800003  178.096558  166.300003   456.0   
59   51.0  ...  180.100006  184.300003  177.528564  166.600006   446.0   
60   51.0  ...  172.000000  183.600006  171.437927  163.899994   447.0   
61   51.0  ...  178.699997  189.800003  177.810715  159.699997   447.0   
62   51.0  ...  188.399994  188.300003  177.379303  166.600006   456.0   
63   51.0  ...  165.199997  175.300003  166.265518  153.899994   466.0   
64   51.0  ...  188.800003  191.199997  181.581482  168.199997   463.0   
65   51.0  ...  196.100006  192.199997  187.396545  176.699997   472.0   
66   51.0  ...  156.500000  188.399994  175.225006  159.899994   446.0   
67   51.0  ...  177.399994  170.500000  153.157150  143.899994   456.0   
68   51.0  ...  190.300003  176.399994  168.962967  157.000000   465.0   
69   51.0  ...  160.100006  176.000000  161.782150  147.199997   466.0   

        X_2864  X_2865  Y_Class  prediction_label  prediction_score  
49  449.442322   432.0        2                 1              0.50  
50  447.769226   422.0        0                 1              0.53  
51  439.961548   422.0        1                 2              0.50  
52  440.288452   423.0        1                 1              0.55  
53  430.942322   413.0        2                 2              0.62  
54  446.557678   423.0        1                 1              0.72  
55  446.169800   424.0        2                 2              0.70  
56  450.692322   432.0        1                 1              0.60  
57  438.132080   413.0        1                 1              0.49  
58

PRODUCT_CODE  X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  \
49             1    1.0   90.0   84.0   45.0   11.0    0.0   45.0   12.0   
50             1    1.0   91.0    1.0   45.0   12.0    0.0   45.0   12.0   
51             1    1.0   95.0  145.0   45.0   11.0    0.0   45.0   12.0   
52             1    1.0   95.0  142.0   45.0   12.0    0.0   45.0   12.0   
53             1    2.0   91.0  170.0   45.0   11.0    0.0   45.0   12.0   
54             1    1.0   88.0   25.0   45.0   12.0    0.0   45.0   12.0   
55             1    1.0   93.0  138.0   45.0   11.0    0.0   45.0   12.0   
56             1    2.0   95.0    7.0   45.0   12.0    0.0   45.0   12.0   
57             1    1.0   93.0  107.0   45.0   11.0    0.0   45.0   12.0   
58             1    2.0   88.0   77.0   45.0   12.0    0.0   45.0   12.0   
59             1    2.0   91.0  158.0   45.0   11.0    0.0   45.0   12.0   
60             1    2.0   89.0  149.0   45.0   11.0    0.0   45.0   12.0   
61             1    2.0   95.0  170.0   45.0   12.0    0.0   45.0   12.0   
62             1    1.0   88.0   92.0   45.0   12.0    0.0   45.0   12.0   
63             1    1.0   91.0  138.0   45.0   12.0    0.0   45.0   12.0   
64             1    1.0   88.0   54.0   45.0   11.0    0.0   45.0   12.0   
65             1    1.0   93.0   63.0   45.0   12.0    0.0   45.0   12.0   
66             1    1.0   87.0  144.0   45.0   12.0    0.0   45.0   12.0   
67             1    1.0   93.0  129.0   45.0   11.0    0.0   45.0   12.0   
68             1    2.0   89.0   67.0   45.0   11.0    0.0   45.0   12.0   
69             1    2.0   91.0   81.0   45.0   12.0    0.0   45.0   12.0   

    X_254  ...      X_2859      X_2860      X_2861      X_2862  X_2863  \
49   51.0  ...  165.699997  198.600006  185.696426  169.000000   465.0   
50   51.0  ...  167.399994  185.000000  179.503571  172.600006   466.0   
51   51.0  ...  186.100006  181.199997  167.639282  158.000000   456.0   
52   51.0  ...  185.300003  171.199997  164.860718  157.500000   456.0   
53   51.0  ...  160.500000  194.100006  180.189285  165.500000   446.0   
54   51.0  ...  184.100006  180.399994  169.782150  161.500000   466.0   
55   51.0  ...  187.500000  185.899994  172.920685  151.100006   466.0   
56   51.0  ...  161.100006  152.000000  143.085709  132.000000   473.0   
57   51.0  ...  177.500000  183.300003  169.553574  154.199997   456.0   
58   51.0  ...  189.100006  184.800003  178.096558  166.300003   456.0   
59   51.0  ...  180.100006  184.300003  177.528564  166.600006   446.0   
60   51.0  ...  172.000000  183.600006  171.437927  163.899994   447.0   
61   51.0  ...  178.699997  189.800003  177.810715  159.699997   447.0   
62   51.0  ...  188.399994  188.300003  177.379303  166.600006   456.0   
63   51.0  ...  165.199997  175.300003  166.265518  153.899994   466.0   
64   51.0  ...  188.800003  191.199997  181.581482  168.199997   463.0   
65   51.0  ...  196.100006  192.199997  187.396545  176.699997   472.0   
66   51.0  ...  156.500000  188.399994  175.225006  159.899994   446.0   
67   51.0  ...  177.399994  170.500000  153.157150  143.899994   456.0   
68   51.0  ...  190.300003  176.399994  168.962967  157.000000   465.0   
69   51.0  ...  160.100006  176.000000  161.782150  147.199997   466.0   

        X_2864  X_2865  Y_Class  prediction_label  prediction_score  
49  449.442322   432.0        2                 1            0.4787  
50  447.769226   422.0        0                 1            0.5101  
51  439.961548   422.0        1                 1            0.4971  
52  440.288452   423.0        1                 1            0.5101  
53  430.942322   413.0        2                 1            0.5106  
54  446.557678   423.0        1                 1            0.6371  
55  446.169800   424.0        2                 2            0.5268  
56  450.692322   432.0        1                 1            0.5574  
57  438.132080   413.0        1                 1            0.4795  
58

In [221]:
T010306_final_classification_model = finalize_model(T010306_model_xgb)

In [222]:
#최종 예측
#29
T010306_prediction = predict_model(T010306_final_classification_model, data=T010306_data)
#prediction.drop(['Y_Quality'], axis = 1, inplace = True)

# T100304

In [223]:
T100304_class = T100304['Y_Class']
T100304_target = T100304['Y_Quality']
T100304_data = T100304.drop(['Y_Class', 'Y_Quality'], axis = 1)
T100304_data

PRODUCT_CODE   X_1    X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  ...  \
22              2   2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
23              2   2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
25              2   2.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
29              2   2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
37              2   2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
..            ...   ...    ...  ...   ...   ...  ...   ...   ...   ...  ...   
561             2   2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
569             3   4.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
571             3   4.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
592             2   2.0   98.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
596             3  40.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   

          X_924      X_925       X_926       X_927       X_928       X_929  \
22   172.500000  162.80000  157.235484  150.900000  326.000000  309.290909   
23   173.127586  160.68908  154.304640  147.601724  322.954023  306.723357   
25   177.800000  157.10000  154.074194  150.900000  327.000000  310.854546   
29   177.900000  161.30000  156.038710  149.100000  327.000000  312.109091   
37   182.800000  162.90000  155.829032  148.400000  327.000000  312.254546   
..          ...        ...         ...         ...         ...         ...   
561  164.100000  162.60000  156.932258  151.100000  317.000000  303.527273   
569  181.700000  160.00000  155.541935  149.800000  327.000000  312.018182   
571  175.400000  165.70000  159.864516  148.700000  326.000000  311.763636   
592  171.500000  156.60000  152.535484  147.600000  326.000000  312.472727   
596  189.200000  179.50000  173.190323  168.600000  321.000000  303.036364   

          X_930      X_931      X_932      X_933  
22   290.000000  13.700000  13.443333  13.200000  
23   291.126437  13.644253  13.412875  13.213218  
25   298.000000  13.700000  13.454839  13.200000  
29   298.000000  13.700000  13.422581  13.200000  
37   298.000000  13.700000  13.456667  13.300000  
..          ...        ...        ...        ...  
561  289.000000  13.700000  13.470000  13.300000  
569  298.000000  13.600000  13.458065  13.300000  
571  298.000000  13.700000  13.425806  13.200000  
592  298.000000  13.600000  13.361290  13.200000  
596  289.000000  13.600000  13.406667  13.200000  

[175 rows x 672 columns]

In [224]:
from pycaret.classification import *
# 분류 패키지의 모든 모듈을 임포트한다.
exp_clf101 = setup(data=T100304_data, 
                   target=T100304_class, 
                   fold=5,
                   session_id=414)
top5 = compare_models(sort='Accuracy', n_select=5)

Processing:   0%|          | 0/73 [00:00<?, ?it/s]

In [225]:
T100304_total_models = []

T100304_model_gbc = create_model('gbc', fold = 5)
T100304_total_models.append(T100304_model_gbc)

T100304_model_et = create_model('et', fold = 5)
T100304_total_models.append(T100304_model_et)

T100304_model_catboost = create_model('catboost', fold = 5)
T100304_total_models.append(T100304_model_catboost)

T100304_model_xgb = create_model('xgboost', fold = 5)
T100304_total_models.append(T100304_model_xgb)

T100304_model_ada = create_model('ada', fold = 5)
T100304_total_models.append(T100304_model_ada)

T100304_model_rf = create_model('rf', fold = 5)
T100304_total_models.append(T100304_model_rf)

T100304_model_lightgbm = create_model('lightgbm', fold = 5)
T100304_total_models.append(T100304_model_lightgbm)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [226]:
T100304_model_lightgbm = tune_model(T100304_model_lightgbm, fold=5, choose_better = True)

T100304_model_gbc = tune_model(T100304_model_gbc, fold=5, choose_better = True)

T100304_model_et = tune_model(T100304_model_et, fold=5, choose_better = True)

T100304_model_catboost = tune_model(T100304_model_catboost, fold=5, choose_better = True)

T100304_model_xgb = tune_model(T100304_model_xgb, fold=5, choose_better = True)

T100304_model_rf = tune_model(T100304_model_rf, fold=5, choose_better = True)

T100304_model_ada = tune_model(T100304_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


In [227]:
T100304_tuned_models = [T100304_model_gbc, T100304_model_et, T100304_model_catboost, T100304_model_xgb, T100304_model_ada, T100304_model_rf, T100304_model_lightgbm]
T100304_tuned_models

[GradientBoostingClassifier(ccp_alpha=0.0, criterion='friedman_mse', init=None,
                            learning_rate=0.0001, loss='deviance', max_depth=1,
                            max_features='sqrt', max_leaf_nodes=None,
                            min_impurity_decrease=0.0005, min_samples_leaf=4,
                            min_samples_split=9, min_weight_fraction_leaf=0.0,
                            n_estimators=270, n_iter_no_change=None,
                            random_state=414, subsample=0.55, tol=0.0001,
                            validation_fraction=0.1, verbose=0,
                            warm_start=False),
 ExtraTreesClassifier(bootstrap=False, ccp_alpha=0.0, class_weight=None,
                      criterion='gini', max_depth=None, max_features='auto',
                      max_leaf_nodes=None, max_samples=None,
                      min_impurity_decrease=0.0, min_samples_leaf=1,
                      min_samples_split=2, min_weight_fraction_leaf=0.0,
      

In [228]:
for model in T100304_tuned_models:
    display(predict_model(model))

PRODUCT_CODE    X_1    X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  ...  \
122             2    2.0   98.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
123             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
124             2    1.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
125             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
126             2    2.0  101.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
127             2    2.0  100.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
128             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
129             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
130             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
131             2    1.0   93.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
132             2    1.0   98.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
133             2    1.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
134             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
135             2    2.0  100.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
136             2    2.0   97.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
137             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
138             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
139             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
140             2    1.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
141             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
142             2    2.0   97.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
143             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
144             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
145             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
146             2  103.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
147             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
148             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
149             2    2.0  100.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
150             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
151             2    1.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
152             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
153             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
154             2    2.0   96.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
155             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
156             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
157             2    2.0   99.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
158             2    1.0   94.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
159             2    2.0   93.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
160             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
161             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
162             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
163             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
164             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
165             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
166             2    2.0   93.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
167             2    2.0  101.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
168             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
169             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
170             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
171  

PRODUCT_CODE    X_1    X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  ...  \
122             2    2.0   98.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
123             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
124             2    1.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
125             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
126             2    2.0  101.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
127             2    2.0  100.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
128             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
129             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
130             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
131             2    1.0   93.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
132             2    1.0   98.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
133             2    1.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
134             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
135             2    2.0  100.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
136             2    2.0   97.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
137             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
138             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
139             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
140             2    1.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
141             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
142             2    2.0   97.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
143             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
144             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
145             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
146             2  103.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
147             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
148             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
149             2    2.0  100.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
150             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
151             2    1.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
152             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
153             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
154             2    2.0   96.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
155             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
156             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
157             2    2.0   99.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
158             2    1.0   94.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
159             2    2.0   93.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
160             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
161             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
162             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
163             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
164             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
165             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
166             2    2.0   93.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
167             2    2.0  101.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
168             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
169             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
170             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
171  

PRODUCT_CODE    X_1    X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  ...  \
122             2    2.0   98.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
123             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
124             2    1.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
125             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
126             2    2.0  101.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
127             2    2.0  100.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
128             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
129             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
130             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
131             2    1.0   93.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
132             2    1.0   98.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
133             2    1.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
134             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
135             2    2.0  100.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
136             2    2.0   97.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
137             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
138             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
139             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
140             2    1.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
141             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
142             2    2.0   97.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
143             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
144             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
145             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
146             2  103.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
147             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
148             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
149             2    2.0  100.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
150             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
151             2    1.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
152             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
153             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
154             2    2.0   96.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
155             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
156             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
157             2    2.0   99.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
158             2    1.0   94.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
159             2    2.0   93.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
160             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
161             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
162             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
163             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
164             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
165             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
166             2    2.0   93.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
167             2    2.0  101.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
168             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
169             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
170             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
171  

PRODUCT_CODE    X_1    X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  ...  \
122             2    2.0   98.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
123             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
124             2    1.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
125             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
126             2    2.0  101.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
127             2    2.0  100.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
128             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
129             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
130             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
131             2    1.0   93.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
132             2    1.0   98.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
133             2    1.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
134             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
135             2    2.0  100.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
136             2    2.0   97.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
137             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
138             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
139             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
140             2    1.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
141             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
142             2    2.0   97.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
143             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
144             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
145             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
146             2  103.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
147             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
148             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
149             2    2.0  100.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
150             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
151             2    1.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
152             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
153             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
154             2    2.0   96.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
155             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
156             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
157             2    2.0   99.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
158             2    1.0   94.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
159             2    2.0   93.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
160             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
161             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
162             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
163             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
164             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
165             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
166             2    2.0   93.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
167             2    2.0  101.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
168             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
169             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
170             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
171  

PRODUCT_CODE    X_1    X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  ...  \
122             2    2.0   98.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
123             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
124             2    1.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
125             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
126             2    2.0  101.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
127             2    2.0  100.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
128             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
129             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
130             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
131             2    1.0   93.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
132             2    1.0   98.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
133             2    1.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
134             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
135             2    2.0  100.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
136             2    2.0   97.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
137             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
138             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
139             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
140             2    1.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
141             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
142             2    2.0   97.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
143             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
144             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
145             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
146             2  103.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
147             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
148             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
149             2    2.0  100.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
150             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
151             2    1.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
152             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
153             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
154             2    2.0   96.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
155             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
156             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
157             2    2.0   99.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
158             2    1.0   94.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
159             2    2.0   93.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
160             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
161             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
162             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
163             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
164             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
165             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
166             2    2.0   93.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
167             2    2.0  101.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
168             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
169             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
170             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
171  

PRODUCT_CODE    X_1    X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  ...  \
122             2    2.0   98.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
123             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
124             2    1.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
125             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
126             2    2.0  101.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
127             2    2.0  100.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
128             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
129             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
130             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
131             2    1.0   93.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
132             2    1.0   98.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
133             2    1.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
134             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
135             2    2.0  100.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
136             2    2.0   97.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
137             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
138             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
139             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
140             2    1.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
141             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
142             2    2.0   97.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
143             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
144             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
145             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
146             2  103.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
147             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
148             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
149             2    2.0  100.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
150             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
151             2    1.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
152             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
153             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
154             2    2.0   96.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
155             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
156             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
157             2    2.0   99.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
158             2    1.0   94.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
159             2    2.0   93.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
160             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
161             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
162             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
163             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
164             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
165             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
166             2    2.0   93.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
167             2    2.0  101.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
168             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
169             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
170             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
171  

PRODUCT_CODE    X_1    X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  ...  \
122             2    2.0   98.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
123             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
124             2    1.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
125             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
126             2    2.0  101.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
127             2    2.0  100.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
128             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
129             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
130             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
131             2    1.0   93.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
132             2    1.0   98.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
133             2    1.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
134             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
135             2    2.0  100.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
136             2    2.0   97.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
137             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
138             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
139             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
140             2    1.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
141             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
142             2    2.0   97.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
143             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
144             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
145             2    2.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
146             2  103.0   96.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
147             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
148             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
149             2    2.0  100.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
150             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
151             2    1.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
152             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
153             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
154             2    2.0   96.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
155             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
156             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
157             2    2.0   99.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
158             2    1.0   94.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
159             2    2.0   93.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
160             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
161             2    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
162             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
163             2    2.0  101.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
164             2    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
165             2    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
166             2    2.0   93.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
167             2    2.0  101.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
168             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
169             2    2.0   98.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
170             2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
171  

In [230]:
T100304_final_classification_model = finalize_model(T100304_model_lightgbm)

In [231]:
#최종 예측
#29
T100304_prediction = predict_model(T100304_final_classification_model, data=T100304_data)
#prediction.drop(['Y_Quality'], axis = 1, inplace = True)

# T100306

In [232]:
T100306_class = T100306['Y_Class']
T100306_target = T100306['Y_Quality']
T100306_data = T100306.drop(['Y_Class', 'Y_Quality'], axis = 1)
T100306_data

PRODUCT_CODE   X_1   X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  ...  \
26              2   2.0  95.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
30              2   2.0  88.0  0.0  45.0  10.0  0.0  51.0  11.0  52.0  ...   
36              2   2.0  91.0  0.0  45.0  10.0  0.0  60.0  11.0  52.0  ...   
42              2   2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
43              2   2.0  95.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
..            ...   ...   ...  ...   ...   ...  ...   ...   ...   ...  ...   
589             2   1.0  94.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
590             2   1.0  89.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
591             2   1.0  87.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
593             2   2.0  95.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
597             3  21.0  87.0  0.0  45.0  10.0  0.0  61.0  10.0  52.0  ...   

     X_924  X_925       X_926  X_927  X_928       X_929  X_930  X_931  \
26   166.9  158.5  151.096774  146.5  327.0  313.618182  299.0   13.7   
30   174.5  161.1  153.574194  147.6  327.0  313.109091  297.0   13.7   
36   179.3  157.7  151.890323  146.1  327.0  309.636364  292.0   13.7   
42   176.0  160.3  155.129032  151.0  327.0  312.553571  298.0   13.7   
43   183.1  165.1  159.100000  155.0  326.0  305.370370  288.0   13.7   
..     ...    ...         ...    ...    ...         ...    ...    ...   
589  170.1  159.9  154.309677  149.1  326.0  311.272727  298.0   13.7   
590  176.2  158.1  154.812903  150.0  327.0  313.400000  299.0   13.6   
591  177.0  159.6  154.777419  147.7  326.0  313.472727  298.0   13.6   
593  172.8  161.2  155.438710  149.0  327.0  313.363636  298.0   13.6   
597  188.2  172.9  167.087097  161.1  326.0  304.818182  289.0   13.6   

         X_932  X_933  
26   13.461290   13.3  
30   13.376667   13.2  
36   13.454839   13.3  
42   13.503333   13.3  
43   13.446667   13.2  
..         ...    ...  
589  13.483871   13.3  
590  13.393548   13.2  
591  13.400000   13.2  
593  13.351613   13.2  
597  13.380000   13.2  

[174 rows x 672 columns]

In [233]:
from pycaret.classification import *
# 분류 패키지의 모든 모듈을 임포트한다.
exp_clf101 = setup(data=T100306_data, 
                   target=T100306_class, 
                   fold=5,
                   session_id=414)
top5 = compare_models(sort='Accuracy', n_select=5)

Processing:   0%|          | 0/73 [00:00<?, ?it/s]

In [234]:
T100306_total_models = []

T100306_model_rf = create_model('rf', fold = 5)
T100306_total_models.append(T100306_model_rf)

T100306_model_gbc = create_model('gbc', fold = 5)
T100306_total_models.append(T100306_model_gbc)

T100306_model_et = create_model('et', fold = 5)
T100306_total_models.append(T100306_model_et)

T100306_model_catboost = create_model('catboost', fold = 5)
T100306_total_models.append(T100306_model_catboost)

T100306_model_xgb = create_model('xgboost', fold = 5)
T100306_total_models.append(T100306_model_xgb)

T100306_model_ada = create_model('ada', fold = 5)
T100306_total_models.append(T100306_model_ada)

T100306_model_lightgbm = create_model('lightgbm', fold = 5)
T100306_total_models.append(T100306_model_lightgbm)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [235]:
T100306_model_lightgbm = tune_model(T100306_model_rf, fold=5, choose_better = True)

T100306_model_gbc = tune_model(T100306_model_gbc, fold=5, choose_better = True)

T100306_model_et = tune_model(T100306_model_et, fold=5, choose_better = True)

T100306_model_catboost = tune_model(T100306_model_catboost, fold=5, choose_better = True)

T100306_model_xgb = tune_model(T100306_model_xgb, fold=5, choose_better = True)

T100306_model_ada = tune_model(T100306_model_ada, fold=5, choose_better = True)

T100306_model_lightgbm = tune_model(T100306_model_lightgbm, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


In [236]:
T100306_tuned_models = [T100306_model_rf, T100306_model_gbc, T100306_model_et, T100306_model_catboost, T100306_model_xgb, T100306_model_ada, T100306_model_lightgbm]
T100306_tuned_models

[RandomForestClassifier(bootstrap=True, ccp_alpha=0.0, class_weight=None,
                        criterion='gini', max_depth=None, max_features='auto',
                        max_leaf_nodes=None, max_samples=None,
                        min_impurity_decrease=0.0, min_samples_leaf=1,
                        min_samples_split=2, min_weight_fraction_leaf=0.0,
                        n_estimators=100, n_jobs=-1, oob_score=False,
                        random_state=414, verbose=0, warm_start=False),
 GradientBoostingClassifier(ccp_alpha=0.0, criterion='friedman_mse', init=None,
                            learning_rate=0.1, loss='deviance', max_depth=3,
                            max_features=None, max_leaf_nodes=None,
                            min_impurity_decrease=0.0, min_samples_leaf=1,
                            min_samples_split=2, min_weight_fraction_leaf=0.0,
                            n_estimators=100, n_iter_no_change=None,
                            random_state=414, su

In [237]:
for model in T100306_tuned_models:
    display(predict_model(model))

PRODUCT_CODE   X_1   X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  ...  \
121             2   4.0  96.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
122             2   1.0  89.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
123             2   2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
124             2   2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
125             2   2.0  93.0  0.0  45.0  10.0  0.0  60.0  10.0  52.0  ...   
126             2   2.0  95.0  0.0  45.0  10.0  0.0  60.0  10.0  52.0  ...   
127             2   1.0  95.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
128             2   2.0  89.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
129             2   1.0  95.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
130             2   2.0  87.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
131             2   3.0  88.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
132             2   2.0  96.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
133             2   1.0  88.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
134             2   2.0  89.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
135             2   2.0  93.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
136             2   2.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
137             2   2.0  95.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
138             2   1.0  87.0  0.0  45.0  10.0  0.0  54.0  11.0  52.0  ...   
139             2   2.0  87.0  0.0  45.0  10.0  0.0  57.0  11.0  52.0  ...   
140             2   2.0  90.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
141             2   2.0  90.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
142             2   2.0  96.0  0.0  45.0  10.0  0.0  60.0  11.0  52.0  ...   
143             2   2.0  93.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
144             2   2.0  89.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
145             2   1.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
146             2   2.0  89.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
147             2   2.0  96.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
148             2   2.0  87.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
149             2   2.0  95.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
150             2   2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
151             2   2.0  95.0  0.0  45.0  10.0  0.0  62.0  10.0  52.0  ...   
152             2   2.0  88.0  0.0  45.0  10.0  0.0  54.0  11.0  52.0  ...   
153             2   1.0  87.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
154             2   2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
155             2   2.0  89.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
156             2   2.0  88.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
157             2   2.0  95.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
158             2   2.0  96.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
159             2   2.0  96.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
160             2   2.0  93.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
161             2   2.0  93.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
162             2   2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
163             3   6.0  90.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
164             2   1.0  89.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
165             2   2.0  95.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
166             2   2.0  94.0  0.0  45.0  10.0  0.0  53.0  11.0  52.0  ...   
167             2   2.0  93.0  0.0  45.0  10.0  0.0  58.0  11.0  52.0  ...   
168             2   2.0  90.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
169             3  21.0  87.0  0.0  45.0  10.0  0.0  61.0  10.0  52.0  ...   
170             2   2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
171             2   2.0  91

PRODUCT_CODE   X_1   X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  ...  \
121             2   4.0  96.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
122             2   1.0  89.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
123             2   2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
124             2   2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
125             2   2.0  93.0  0.0  45.0  10.0  0.0  60.0  10.0  52.0  ...   
126             2   2.0  95.0  0.0  45.0  10.0  0.0  60.0  10.0  52.0  ...   
127             2   1.0  95.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
128             2   2.0  89.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
129             2   1.0  95.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
130             2   2.0  87.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
131             2   3.0  88.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
132             2   2.0  96.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
133             2   1.0  88.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
134             2   2.0  89.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
135             2   2.0  93.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
136             2   2.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
137             2   2.0  95.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
138             2   1.0  87.0  0.0  45.0  10.0  0.0  54.0  11.0  52.0  ...   
139             2   2.0  87.0  0.0  45.0  10.0  0.0  57.0  11.0  52.0  ...   
140             2   2.0  90.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
141             2   2.0  90.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
142             2   2.0  96.0  0.0  45.0  10.0  0.0  60.0  11.0  52.0  ...   
143             2   2.0  93.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
144             2   2.0  89.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
145             2   1.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
146             2   2.0  89.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
147             2   2.0  96.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
148             2   2.0  87.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
149             2   2.0  95.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
150             2   2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
151             2   2.0  95.0  0.0  45.0  10.0  0.0  62.0  10.0  52.0  ...   
152             2   2.0  88.0  0.0  45.0  10.0  0.0  54.0  11.0  52.0  ...   
153             2   1.0  87.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
154             2   2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
155             2   2.0  89.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
156             2   2.0  88.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
157             2   2.0  95.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
158             2   2.0  96.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
159             2   2.0  96.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
160             2   2.0  93.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
161             2   2.0  93.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
162             2   2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
163             3   6.0  90.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
164             2   1.0  89.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
165             2   2.0  95.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
166             2   2.0  94.0  0.0  45.0  10.0  0.0  53.0  11.0  52.0  ...   
167             2   2.0  93.0  0.0  45.0  10.0  0.0  58.0  11.0  52.0  ...   
168             2   2.0  90.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
169             3  21.0  87.0  0.0  45.0  10.0  0.0  61.0  10.0  52.0  ...   
170             2   2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
171             2   2.0  91

PRODUCT_CODE   X_1   X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  ...  \
121             2   4.0  96.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
122             2   1.0  89.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
123             2   2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
124             2   2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
125             2   2.0  93.0  0.0  45.0  10.0  0.0  60.0  10.0  52.0  ...   
126             2   2.0  95.0  0.0  45.0  10.0  0.0  60.0  10.0  52.0  ...   
127             2   1.0  95.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
128             2   2.0  89.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
129             2   1.0  95.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
130             2   2.0  87.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
131             2   3.0  88.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
132             2   2.0  96.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
133             2   1.0  88.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
134             2   2.0  89.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
135             2   2.0  93.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
136             2   2.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
137             2   2.0  95.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
138             2   1.0  87.0  0.0  45.0  10.0  0.0  54.0  11.0  52.0  ...   
139             2   2.0  87.0  0.0  45.0  10.0  0.0  57.0  11.0  52.0  ...   
140             2   2.0  90.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
141             2   2.0  90.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
142             2   2.0  96.0  0.0  45.0  10.0  0.0  60.0  11.0  52.0  ...   
143             2   2.0  93.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
144             2   2.0  89.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
145             2   1.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
146             2   2.0  89.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
147             2   2.0  96.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
148             2   2.0  87.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
149             2   2.0  95.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
150             2   2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
151             2   2.0  95.0  0.0  45.0  10.0  0.0  62.0  10.0  52.0  ...   
152             2   2.0  88.0  0.0  45.0  10.0  0.0  54.0  11.0  52.0  ...   
153             2   1.0  87.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
154             2   2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
155             2   2.0  89.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
156             2   2.0  88.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
157             2   2.0  95.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
158             2   2.0  96.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
159             2   2.0  96.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
160             2   2.0  93.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
161             2   2.0  93.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
162             2   2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
163             3   6.0  90.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
164             2   1.0  89.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
165             2   2.0  95.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
166             2   2.0  94.0  0.0  45.0  10.0  0.0  53.0  11.0  52.0  ...   
167             2   2.0  93.0  0.0  45.0  10.0  0.0  58.0  11.0  52.0  ...   
168             2   2.0  90.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
169             3  21.0  87.0  0.0  45.0  10.0  0.0  61.0  10.0  52.0  ...   
170             2   2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
171             2   2.0  91

PRODUCT_CODE   X_1   X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  ...  \
121             2   4.0  96.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
122             2   1.0  89.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
123             2   2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
124             2   2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
125             2   2.0  93.0  0.0  45.0  10.0  0.0  60.0  10.0  52.0  ...   
126             2   2.0  95.0  0.0  45.0  10.0  0.0  60.0  10.0  52.0  ...   
127             2   1.0  95.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
128             2   2.0  89.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
129             2   1.0  95.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
130             2   2.0  87.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
131             2   3.0  88.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
132             2   2.0  96.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
133             2   1.0  88.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
134             2   2.0  89.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
135             2   2.0  93.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
136             2   2.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
137             2   2.0  95.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
138             2   1.0  87.0  0.0  45.0  10.0  0.0  54.0  11.0  52.0  ...   
139             2   2.0  87.0  0.0  45.0  10.0  0.0  57.0  11.0  52.0  ...   
140             2   2.0  90.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
141             2   2.0  90.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
142             2   2.0  96.0  0.0  45.0  10.0  0.0  60.0  11.0  52.0  ...   
143             2   2.0  93.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
144             2   2.0  89.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
145             2   1.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
146             2   2.0  89.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
147             2   2.0  96.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
148             2   2.0  87.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
149             2   2.0  95.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
150             2   2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
151             2   2.0  95.0  0.0  45.0  10.0  0.0  62.0  10.0  52.0  ...   
152             2   2.0  88.0  0.0  45.0  10.0  0.0  54.0  11.0  52.0  ...   
153             2   1.0  87.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
154             2   2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
155             2   2.0  89.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
156             2   2.0  88.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
157             2   2.0  95.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
158             2   2.0  96.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
159             2   2.0  96.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
160             2   2.0  93.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
161             2   2.0  93.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
162             2   2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
163             3   6.0  90.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
164             2   1.0  89.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
165             2   2.0  95.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
166             2   2.0  94.0  0.0  45.0  10.0  0.0  53.0  11.0  52.0  ...   
167             2   2.0  93.0  0.0  45.0  10.0  0.0  58.0  11.0  52.0  ...   
168             2   2.0  90.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
169             3  21.0  87.0  0.0  45.0  10.0  0.0  61.0  10.0  52.0  ...   
170             2   2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
171             2   2.0  91

PRODUCT_CODE   X_1   X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  ...  \
121             2   4.0  96.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
122             2   1.0  89.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
123             2   2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
124             2   2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
125             2   2.0  93.0  0.0  45.0  10.0  0.0  60.0  10.0  52.0  ...   
126             2   2.0  95.0  0.0  45.0  10.0  0.0  60.0  10.0  52.0  ...   
127             2   1.0  95.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
128             2   2.0  89.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
129             2   1.0  95.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
130             2   2.0  87.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
131             2   3.0  88.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
132             2   2.0  96.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
133             2   1.0  88.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
134             2   2.0  89.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
135             2   2.0  93.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
136             2   2.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
137             2   2.0  95.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
138             2   1.0  87.0  0.0  45.0  10.0  0.0  54.0  11.0  52.0  ...   
139             2   2.0  87.0  0.0  45.0  10.0  0.0  57.0  11.0  52.0  ...   
140             2   2.0  90.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
141             2   2.0  90.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
142             2   2.0  96.0  0.0  45.0  10.0  0.0  60.0  11.0  52.0  ...   
143             2   2.0  93.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
144             2   2.0  89.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
145             2   1.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
146             2   2.0  89.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
147             2   2.0  96.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
148             2   2.0  87.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
149             2   2.0  95.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
150             2   2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
151             2   2.0  95.0  0.0  45.0  10.0  0.0  62.0  10.0  52.0  ...   
152             2   2.0  88.0  0.0  45.0  10.0  0.0  54.0  11.0  52.0  ...   
153             2   1.0  87.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
154             2   2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
155             2   2.0  89.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
156             2   2.0  88.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
157             2   2.0  95.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
158             2   2.0  96.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
159             2   2.0  96.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
160             2   2.0  93.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
161             2   2.0  93.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
162             2   2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
163             3   6.0  90.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
164             2   1.0  89.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
165             2   2.0  95.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
166             2   2.0  94.0  0.0  45.0  10.0  0.0  53.0  11.0  52.0  ...   
167             2   2.0  93.0  0.0  45.0  10.0  0.0  58.0  11.0  52.0  ...   
168             2   2.0  90.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
169             3  21.0  87.0  0.0  45.0  10.0  0.0  61.0  10.0  52.0  ...   
170             2   2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
171             2   2.0  91

PRODUCT_CODE   X_1   X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  ...  \
121             2   4.0  96.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
122             2   1.0  89.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
123             2   2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
124             2   2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
125             2   2.0  93.0  0.0  45.0  10.0  0.0  60.0  10.0  52.0  ...   
126             2   2.0  95.0  0.0  45.0  10.0  0.0  60.0  10.0  52.0  ...   
127             2   1.0  95.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
128             2   2.0  89.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
129             2   1.0  95.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
130             2   2.0  87.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
131             2   3.0  88.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
132             2   2.0  96.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
133             2   1.0  88.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
134             2   2.0  89.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
135             2   2.0  93.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
136             2   2.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
137             2   2.0  95.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
138             2   1.0  87.0  0.0  45.0  10.0  0.0  54.0  11.0  52.0  ...   
139             2   2.0  87.0  0.0  45.0  10.0  0.0  57.0  11.0  52.0  ...   
140             2   2.0  90.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
141             2   2.0  90.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
142             2   2.0  96.0  0.0  45.0  10.0  0.0  60.0  11.0  52.0  ...   
143             2   2.0  93.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
144             2   2.0  89.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
145             2   1.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
146             2   2.0  89.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
147             2   2.0  96.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
148             2   2.0  87.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
149             2   2.0  95.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
150             2   2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
151             2   2.0  95.0  0.0  45.0  10.0  0.0  62.0  10.0  52.0  ...   
152             2   2.0  88.0  0.0  45.0  10.0  0.0  54.0  11.0  52.0  ...   
153             2   1.0  87.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
154             2   2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
155             2   2.0  89.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
156             2   2.0  88.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
157             2   2.0  95.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
158             2   2.0  96.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
159             2   2.0  96.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
160             2   2.0  93.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
161             2   2.0  93.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
162             2   2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
163             3   6.0  90.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
164             2   1.0  89.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
165             2   2.0  95.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
166             2   2.0  94.0  0.0  45.0  10.0  0.0  53.0  11.0  52.0  ...   
167             2   2.0  93.0  0.0  45.0  10.0  0.0  58.0  11.0  52.0  ...   
168             2   2.0  90.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
169             3  21.0  87.0  0.0  45.0  10.0  0.0  61.0  10.0  52.0  ...   
170             2   2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
171             2   2.0  91

PRODUCT_CODE   X_1   X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  ...  \
121             2   4.0  96.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
122             2   1.0  89.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
123             2   2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
124             2   2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
125             2   2.0  93.0  0.0  45.0  10.0  0.0  60.0  10.0  52.0  ...   
126             2   2.0  95.0  0.0  45.0  10.0  0.0  60.0  10.0  52.0  ...   
127             2   1.0  95.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
128             2   2.0  89.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
129             2   1.0  95.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
130             2   2.0  87.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
131             2   3.0  88.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
132             2   2.0  96.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
133             2   1.0  88.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
134             2   2.0  89.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
135             2   2.0  93.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
136             2   2.0  93.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
137             2   2.0  95.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
138             2   1.0  87.0  0.0  45.0  10.0  0.0  54.0  11.0  52.0  ...   
139             2   2.0  87.0  0.0  45.0  10.0  0.0  57.0  11.0  52.0  ...   
140             2   2.0  90.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
141             2   2.0  90.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
142             2   2.0  96.0  0.0  45.0  10.0  0.0  60.0  11.0  52.0  ...   
143             2   2.0  93.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
144             2   2.0  89.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
145             2   1.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
146             2   2.0  89.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
147             2   2.0  96.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
148             2   2.0  87.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
149             2   2.0  95.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
150             2   2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
151             2   2.0  95.0  0.0  45.0  10.0  0.0  62.0  10.0  52.0  ...   
152             2   2.0  88.0  0.0  45.0  10.0  0.0  54.0  11.0  52.0  ...   
153             2   1.0  87.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
154             2   2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
155             2   2.0  89.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
156             2   2.0  88.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
157             2   2.0  95.0  0.0  45.0  10.0  0.0  57.0  10.0  52.0  ...   
158             2   2.0  96.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
159             2   2.0  96.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
160             2   2.0  93.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
161             2   2.0  93.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
162             2   2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
163             3   6.0  90.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
164             2   1.0  89.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
165             2   2.0  95.0  0.0  45.0  10.0  0.0  53.0  10.0  52.0  ...   
166             2   2.0  94.0  0.0  45.0  10.0  0.0  53.0  11.0  52.0  ...   
167             2   2.0  93.0  0.0  45.0  10.0  0.0  58.0  11.0  52.0  ...   
168             2   2.0  90.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
169             3  21.0  87.0  0.0  45.0  10.0  0.0  61.0  10.0  52.0  ...   
170             2   2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0  ...   
171             2   2.0  91

In [238]:
T100306_final_classification_model = finalize_model(T100306_model_xgb)

In [239]:
#최종 예측
#29
T100306_prediction = predict_model(T100306_final_classification_model, data=T100306_data)
#prediction.drop(['Y_Quality'], axis = 1, inplace = True)

# Test

In [240]:
#44
test_data = pd.read_csv("./test.csv")
test_data

PRODUCT_ID         TIMESTAMP     LINE PRODUCT_CODE  X_1   X_2  X_3   X_4  \
0     TEST_000   2022-09-09 2:01  T100306         T_31  2.0  94.0  0.0  45.0   
1     TEST_001   2022-09-09 2:09  T100304         T_31  2.0  93.0  0.0  45.0   
2     TEST_002   2022-09-09 8:42  T100304         T_31  2.0  95.0  0.0  45.0   
3     TEST_003  2022-09-09 10:56  T010305         A_31  NaN   NaN  NaN   NaN   
4     TEST_004  2022-09-09 11:04  T010306         A_31  NaN   NaN  NaN   NaN   
..         ...               ...      ...          ...  ...   ...  ...   ...   
305   TEST_305  2022-11-05 11:18  T100306         T_31  2.0  91.0  0.0  45.0   
306   TEST_306  2022-11-05 16:39  T100304         T_31  2.0  96.0  0.0  45.0   
307   TEST_307  2022-11-05 16:47  T100306         T_31  2.0  91.0  0.0  45.0   
308   TEST_308  2022-11-05 20:53  T100306         T_31  2.0  95.0  0.0  45.0   
309   TEST_309  2022-11-05 21:01  T100306         T_31  2.0  87.0  0.0  45.0   

      X_5  X_6  ...  X_2866  X_2867  X_2868  X_2869  X_2870  X_2871  X_2872  \
0    10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
1    11.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
2    11.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
3     NaN  NaN  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
4     NaN  NaN  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
..    ...  ...  ...     ...     ...     ...     ...     ...     ...     ...   
305  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
306  11.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
307  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
308  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
309  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   

     X_2873  X_2874  X_2875  
0       NaN     NaN     NaN  
1       NaN     NaN     NaN  
2       NaN     NaN     NaN  
3       NaN     NaN     NaN  
4       NaN     NaN     NaN  
..      ...     ...     ...  
305     NaN     NaN     NaN  
306     NaN     NaN     NaN  
307     NaN     NaN     NaN  
308     NaN     NaN     NaN  
309     NaN     NaN     NaN  

[310 rows x 2879 columns]

In [241]:
test_data.drop(colls, inplace = True, axis = 1)

In [242]:
#train_data.loc[train_data.DAY_OF_WEEK == 'Monday','DAY_OF_WEEK'] = 1
#train_data.loc[train_data.DAY_OF_WEEK == 'Tuesday','DAY_OF_WEEK'] = 2
#train_data.loc[train_data.DAY_OF_WEEK == 'Wednesday','DAY_OF_WEEK'] = 3
#train_data.loc[train_data.DAY_OF_WEEK == 'Thursday','DAY_OF_WEEK'] = 4
#train_data.loc[train_data.DAY_OF_WEEK == 'Friday','DAY_OF_WEEK'] = 5
#train_data.loc[train_data.DAY_OF_WEEK == 'Saturday','DAY_OF_WEEK'] = 6
#train_data.loc[train_data.DAY_OF_WEEK == 'Sunday','DAY_OF_WEEK'] = 7

test_data.loc[test_data.PRODUCT_CODE == 'A_31','PRODUCT_CODE'] = 1
test_data.loc[test_data.PRODUCT_CODE == 'T_31','PRODUCT_CODE'] = 2
test_data.loc[test_data.PRODUCT_CODE == 'O_31','PRODUCT_CODE'] = 3

test_data.drop(['PRODUCT_ID', 'TIMESTAMP'], axis = 1, inplace = True)
test_data

LINE PRODUCT_CODE  X_1   X_2  X_3   X_4   X_5  X_6   X_7   X_8  ...  \
0    T100306            2  2.0  94.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   
1    T100304            2  2.0  93.0  0.0  45.0  11.0  0.0  45.0  10.0  ...   
2    T100304            2  2.0  95.0  0.0  45.0  11.0  0.0  45.0  10.0  ...   
3    T010305            1  NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN  ...   
4    T010306            1  NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN  ...   
..       ...          ...  ...   ...  ...   ...   ...  ...   ...   ...  ...   
305  T100306            2  2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   
306  T100304            2  2.0  96.0  0.0  45.0  11.0  0.0  45.0  10.0  ...   
307  T100306            2  2.0  91.0  0.0  45.0  10.0  0.0  50.0  10.0  ...   
308  T100306            2  2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   
309  T100306            2  2.0  87.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   

     X_2862  X_2863      X_2864  X_2865  X_2866  X_2867  X_2868  X_2869  \
0       NaN     NaN         NaN     NaN     NaN     NaN     NaN     NaN   
1       NaN     NaN         NaN     NaN     NaN     NaN     NaN     NaN   
2       NaN     NaN         NaN     NaN     NaN     NaN     NaN     NaN   
3     183.8   467.0  444.192308   423.0     NaN     NaN     NaN     NaN   
4     179.7   465.0  443.211539   423.0     NaN     NaN     NaN     NaN   
..      ...     ...         ...     ...     ...     ...     ...     ...   
305     NaN     NaN         NaN     NaN     NaN     NaN     NaN     NaN   
306     NaN     NaN         NaN     NaN     NaN     NaN     NaN     NaN   
307     NaN     NaN         NaN     NaN     NaN     NaN     NaN     NaN   
308     NaN     NaN         NaN     NaN     NaN     NaN     NaN     NaN   
309     NaN     NaN         NaN     NaN     NaN     NaN     NaN     NaN   

     X_2870  X_2871  
0       NaN     NaN  
1       NaN     NaN  
2       NaN     NaN  
3       NaN     NaN  
4       NaN     NaN  
..      ...     ...  
305     NaN     NaN  
306     NaN     NaN  
307     NaN     NaN  
308     NaN     NaN  
309     NaN     NaN  

[310 rows x 2795 columns]

In [243]:
TT050304 = test_data[test_data['LINE'] == 'T050304']
TT050307 = test_data[test_data['LINE'] == 'T050307']
TT010305 = test_data[test_data['LINE'] == 'T010305']
TT010306 = test_data[test_data['LINE'] == 'T010306']
TT100304 = test_data[test_data['LINE'] == 'T100304']
TT100306 = test_data[test_data['LINE'] == 'T100306']
TT050304

LINE PRODUCT_CODE  X_1  X_2  X_3  X_4  X_5  X_6  X_7  X_8  ...  X_2862  \
7   T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   168.3   
8   T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   169.8   
14  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   139.5   
35  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   103.5   
41  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   165.6   
42  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   171.8   
52  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   161.0   
53  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   175.1   
54  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   175.1   
61  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   115.9   
64  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   147.1   
65  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   118.9   
66  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   177.0   

    X_2863      X_2864  X_2865  X_2866  X_2867  X_2868  X_2869  X_2870  X_2871  
7    384.0  369.462963   354.0   57.74   52.51   54.45   57.99   63.16     1.0  
8    384.0  370.259259   353.0   53.18   56.02   41.79   47.94   60.72     1.0  
14   384.0  369.377359   353.0   49.77   54.93   49.85   48.62   63.18     1.0  
35   384.0  369.660377   352.0   55.22   58.14   48.93   56.16   64.25     1.0  
41   383.0  368.018519   352.0   49.67   45.00   49.81   55.19   67.17     1.0  
42   384.0  368.452830   353.0   51.30   47.66   60.00   53.75   62.58     1.0  
52   384.0  368.320755   353.0   54.06   51.18   52.17   57.75   63.94     1.0  
53   384.0  361.226415   342.0   54.04   51.25   54.98   57.22   63.33     1.0  
54   384.0  367.849057   352.0   55.72   57.57   42.08   55.19   66.06     1.0  
61   384.0  370.000000   354.0     NaN     NaN     NaN     NaN     NaN     1.0  
64   384.0  367.943396   352.0     NaN     NaN     NaN     NaN     NaN     1.0  
65   383.0  368.056604   352.0   51.55   55.55   39.85   47.82   61.59     1.0  
66   384.0  369.111111   353.0   51.37   55.70   52.49   48.34   62.12     1.0  

[13 rows x 2795 columns]

In [244]:
TT050304.drop(['LINE'], axis = 1, inplace = True)
TT050307.drop(['LINE'], axis = 1, inplace = True)
TT010305.drop(['LINE'], axis = 1, inplace = True)
TT010306.drop(['LINE'], axis = 1, inplace = True)
TT100304.drop(['LINE'], axis = 1, inplace = True)
TT100306.drop(['LINE'], axis = 1, inplace = True)

In [245]:
TT050304.drop(T050304_col, inplace = True, axis = 1)
TT050307.drop(T050307_col, inplace = True, axis = 1)
TT010305.drop(T010305_col, inplace = True, axis = 1)
TT010306.drop(T010306_col, inplace = True, axis = 1)
TT100304.drop(T100304_col, inplace = True, axis = 1)
TT100306.drop(T100306_col, inplace = True, axis = 1)
TT050304

PRODUCT_CODE    X_128    X_129  X_132  X_133  X_134  X_135  X_136  X_137  \
7             1  18031.0  18031.0   0.19   0.20   0.19    0.2  354.0  354.0   
8             1  18064.0  18064.0   0.19   0.20   0.19    0.2  355.0  354.0   
14            1    295.0    295.0   0.19   0.21   0.19    0.2   60.0   60.0   
35            1   8632.0   8632.0   0.20   0.21   0.20    0.2  249.0  249.0   
41            1  10712.0  10712.0   0.20   0.21   0.20    0.2  293.0  293.0   
42            1  10729.0  10729.0   0.20   0.21   0.19    0.2  293.0  293.0   
52            1  12261.0  12261.0   0.19   0.21   0.19    0.2  330.0  330.0   
53            1  12283.0  12283.0   0.20   0.21   0.20    0.2  330.0  330.0   
54            1  12305.0  12305.0   0.19   0.21   0.19    0.2  330.0  330.0   
61            1  17990.0  17990.0   0.20   0.21   0.20    0.2  436.0  436.0   
64            1  18026.0  18026.0   0.20   0.21   0.20    0.2  437.0  437.0   
65            1  18220.0  18220.0   0.20   0.21   0.20    0.2  441.0  441.0   
66            1  18514.0  18514.0   0.20   0.21   0.20    0.2  446.0  446.0   

    X_138  ...  X_2862  X_2863      X_2864  X_2865  X_2866  X_2867  X_2868  \
7   354.0  ...   168.3   384.0  369.462963   354.0   57.74   52.51   54.45   
8   355.0  ...   169.8   384.0  370.259259   353.0   53.18   56.02   41.79   
14   60.0  ...   139.5   384.0  369.377359   353.0   49.77   54.93   49.85   
35  249.0  ...   103.5   384.0  369.660377   352.0   55.22   58.14   48.93   
41  293.0  ...   165.6   383.0  368.018519   352.0   49.67   45.00   49.81   
42  293.0  ...   171.8   384.0  368.452830   353.0   51.30   47.66   60.00   
52  330.0  ...   161.0   384.0  368.320755   353.0   54.06   51.18   52.17   
53  330.0  ...   175.1   384.0  361.226415   342.0   54.04   51.25   54.98   
54  330.0  ...   175.1   384.0  367.849057   352.0   55.72   57.57   42.08   
61  436.0  ...   115.9   384.0  370.000000   354.0     NaN     NaN     NaN   
64  437.0  ...   147.1   384.0  367.943396   352.0     NaN     NaN     NaN   
65  441.0  ...   118.9   383.0  368.056604   352.0   51.55   55.55   39.85   
66  446.0  ...   177.0   384.0  369.111111   353.0   51.37   55.70   52.49   

    X_2869  X_2870  X_2871  
7    57.99   63.16     1.0  
8    47.94   60.72     1.0  
14   48.62   63.18     1.0  
35   56.16   64.25     1.0  
41   55.19   67.17     1.0  
42   53.75   62.58     1.0  
52   57.75   63.94     1.0  
53   57.22   63.33     1.0  
54   55.19   66.06     1.0  
61     NaN     NaN     1.0  
64     NaN     NaN     1.0  
65   47.82   61.59     1.0  
66   48.34   62.12     1.0  

[13 rows x 1969 columns]

In [159]:
TT050304 = TT050304.fillna(0)
TT050307 = TT050307.fillna(0)
TT010305 = TT010305.fillna(0)
TT010306 = TT010306.fillna(0)
TT100304 = TT100304.fillna(0)
TT100306 = TT100306.fillna(0)
TT050304

PRODUCT_CODE    X_128    X_129  X_132  X_133  X_134  X_135  X_136  X_137  \
7              1  18031.0  18031.0   0.19   0.20   0.19    0.2  354.0  354.0   
8              1  18064.0  18064.0   0.19   0.20   0.19    0.2  355.0  354.0   
14             1    295.0    295.0   0.19   0.21   0.19    0.2   60.0   60.0   
35             1   8632.0   8632.0   0.20   0.21   0.20    0.2  249.0  249.0   
41             1  10712.0  10712.0   0.20   0.21   0.20    0.2  293.0  293.0   
42             1  10729.0  10729.0   0.20   0.21   0.19    0.2  293.0  293.0   
52             1  12261.0  12261.0   0.19   0.21   0.19    0.2  330.0  330.0   
53             1  12283.0  12283.0   0.20   0.21   0.20    0.2  330.0  330.0   
54             1  12305.0  12305.0   0.19   0.21   0.19    0.2  330.0  330.0   
61             1  17990.0  17990.0   0.20   0.21   0.20    0.2  436.0  436.0   
64             1  18026.0  18026.0   0.20   0.21   0.20    0.2  437.0  437.0   
65             1  18220.0  18220.0   0.20   0.21   0.20    0.2  441.0  441.0   
66             1  18514.0  18514.0   0.20   0.21   0.20    0.2  446.0  446.0   

    X_138  ...  X_2862  X_2863      X_2864  X_2865  X_2866  X_2867  X_2868  \
7   354.0  ...   168.3   384.0  369.462963   354.0   57.74   52.51   54.45   
8   355.0  ...   169.8   384.0  370.259259   353.0   53.18   56.02   41.79   
14   60.0  ...   139.5   384.0  369.377359   353.0   49.77   54.93   49.85   
35  249.0  ...   103.5   384.0  369.660377   352.0   55.22   58.14   48.93   
41  293.0  ...   165.6   383.0  368.018519   352.0   49.67   45.00   49.81   
42  293.0  ...   171.8   384.0  368.452830   353.0   51.30   47.66   60.00   
52  330.0  ...   161.0   384.0  368.320755   353.0   54.06   51.18   52.17   
53  330.0  ...   175.1   384.0  361.226415   342.0   54.04   51.25   54.98   
54  330.0  ...   175.1   384.0  367.849057   352.0   55.72   57.57   42.08   
61  436.0  ...   115.9   384.0  370.000000   354.0    0.00    0.00    0.00   
64  437.0  ...   147.1   384.0  367.943396   352.0    0.00    0.00    0.00   
65  441.0  ...   118.9   383.0  368.056604   352.0   51.55   55.55   39.85   
66  446.0  ...   177.0   384.0  369.111111   353.0   51.37   55.70   52.49   

    X_2869  X_2870  X_2871  
7    57.99   63.16     1.0  
8    47.94   60.72     1.0  
14   48.62   63.18     1.0  
35   56.16   64.25     1.0  
41   55.19   67.17     1.0  
42   53.75   62.58     1.0  
52   57.75   63.94     1.0  
53   57.22   63.33     1.0  
54   55.19   66.06     1.0  
61    0.00    0.00     1.0  
64    0.00    0.00     1.0  
65   47.82   61.59     1.0  
66   48.34   62.12     1.0  

[13 rows x 1969 columns]

In [246]:
TT050304 = TT050304.fillna(T050304.mean())
TT050307 = TT050307.fillna(T050307.mean())
TT010305 = TT010305.fillna(T010305.mean())
TT010306 = TT010306.fillna(T010306.mean())
TT100304 = TT100304.fillna(T100304.mean())
TT100306 = TT100306.fillna(T100306.mean())
TT050304

PRODUCT_CODE    X_128    X_129  X_132  X_133  X_134  X_135  X_136  X_137  \
7              1  18031.0  18031.0   0.19   0.20   0.19    0.2  354.0  354.0   
8              1  18064.0  18064.0   0.19   0.20   0.19    0.2  355.0  354.0   
14             1    295.0    295.0   0.19   0.21   0.19    0.2   60.0   60.0   
35             1   8632.0   8632.0   0.20   0.21   0.20    0.2  249.0  249.0   
41             1  10712.0  10712.0   0.20   0.21   0.20    0.2  293.0  293.0   
42             1  10729.0  10729.0   0.20   0.21   0.19    0.2  293.0  293.0   
52             1  12261.0  12261.0   0.19   0.21   0.19    0.2  330.0  330.0   
53             1  12283.0  12283.0   0.20   0.21   0.20    0.2  330.0  330.0   
54             1  12305.0  12305.0   0.19   0.21   0.19    0.2  330.0  330.0   
61             1  17990.0  17990.0   0.20   0.21   0.20    0.2  436.0  436.0   
64             1  18026.0  18026.0   0.20   0.21   0.20    0.2  437.0  437.0   
65             1  18220.0  18220.0   0.20   0.21   0.20    0.2  441.0  441.0   
66             1  18514.0  18514.0   0.20   0.21   0.20    0.2  446.0  446.0   

    X_138  ...  X_2862  X_2863      X_2864  X_2865     X_2866     X_2867  \
7   354.0  ...   168.3   384.0  369.462963   354.0  57.740000  52.510000   
8   355.0  ...   169.8   384.0  370.259259   353.0  53.180000  56.020000   
14   60.0  ...   139.5   384.0  369.377359   353.0  49.770000  54.930000   
35  249.0  ...   103.5   384.0  369.660377   352.0  55.220000  58.140000   
41  293.0  ...   165.6   383.0  368.018519   352.0  49.670000  45.000000   
42  293.0  ...   171.8   384.0  368.452830   353.0  51.300000  47.660000   
52  330.0  ...   161.0   384.0  368.320755   353.0  54.060000  51.180000   
53  330.0  ...   175.1   384.0  361.226415   342.0  54.040000  51.250000   
54  330.0  ...   175.1   384.0  367.849057   352.0  55.720000  57.570000   
61  436.0  ...   115.9   384.0  370.000000   354.0  51.557313  54.230149   
64  437.0  ...   147.1   384.0  367.943396   352.0  51.557313  54.230149   
65  441.0  ...   118.9   383.0  368.056604   352.0  51.550000  55.550000   
66  446.0  ...   177.0   384.0  369.111111   353.0  51.370000  55.700000   

       X_2868     X_2869    X_2870  X_2871  
7   54.450000  57.990000  63.16000     1.0  
8   41.790000  47.940000  60.72000     1.0  
14  49.850000  48.620000  63.18000     1.0  
35  48.930000  56.160000  64.25000     1.0  
41  49.810000  55.190000  67.17000     1.0  
42  60.000000  53.750000  62.58000     1.0  
52  52.170000  57.750000  63.94000     1.0  
53  54.980000  57.220000  63.33000     1.0  
54  42.080000  55.190000  66.06000     1.0  
61  48.665224  52.332537  66.68597     1.0  
64  48.665224  52.332537  66.68597     1.0  
65  39.850000  47.820000  61.59000     1.0  
66  52.490000  48.340000  62.12000     1.0  

[13 rows x 1969 columns]

In [247]:
TT050304_prediction = predict_model(T050304_final_classification_model, data=TT050304)
TT050307_prediction = predict_model(T050307_final_classification_model, data=TT050307)
TT010305_prediction = predict_model(T010305_final_classification_model, data=TT010305)
TT010306_prediction = predict_model(T010306_final_classification_model, data=TT010306)
TT100304_prediction = predict_model(T100304_final_classification_model, data=TT100304)
TT100306_prediction = predict_model(T100306_final_classification_model, data=TT100306)

In [248]:
TT050304_y_class = pd.DataFrame(TT050304, columns = ['PRODUCT_CODE'])
TT050304_idx = TT050304_y_class.index
TT050304_y_class = TT050304_y_class.reset_index()
TT050304_prediction = pd.concat([TT050304_prediction, TT050304_y_class], axis = 1)
TT050304_prediction = TT050304_prediction.set_index('index')
TT050304_prediction.drop(['PRODUCT_CODE'], axis = 1, inplace = True)
TT050304_prediction

X_128    X_129  X_132  X_133  X_134  X_135  X_136  X_137  X_138  \
index                                                                      
7      18031.0  18031.0   0.19   0.20   0.19    0.2  354.0  354.0  354.0   
8      18064.0  18064.0   0.19   0.20   0.19    0.2  355.0  354.0  355.0   
14       295.0    295.0   0.19   0.21   0.19    0.2   60.0   60.0   60.0   
35      8632.0   8632.0   0.20   0.21   0.20    0.2  249.0  249.0  249.0   
41     10712.0  10712.0   0.20   0.21   0.20    0.2  293.0  293.0  293.0   
42     10729.0  10729.0   0.20   0.21   0.19    0.2  293.0  293.0  293.0   
52     12261.0  12261.0   0.19   0.21   0.19    0.2  330.0  330.0  330.0   
53     12283.0  12283.0   0.20   0.21   0.20    0.2  330.0  330.0  330.0   
54     12305.0  12305.0   0.19   0.21   0.19    0.2  330.0  330.0  330.0   
61     17990.0  17990.0   0.20   0.21   0.20    0.2  436.0  436.0  436.0   
64     18026.0  18026.0   0.20   0.21   0.20    0.2  437.0  437.0  437.0   
65     18220.0  18220.0   0.20   0.21   0.20    0.2  441.0  441.0  441.0   
66     18514.0  18514.0   0.20   0.21   0.20    0.2  446.0  446.0  446.0   

            X_139  ...      X_2864  X_2865     X_2866     X_2867     X_2868  \
index              ...                                                        
7      591.500000  ...  369.462952   354.0  57.740002  52.509998  54.450001   
8      591.500000  ...  370.259247   353.0  53.180000  56.020000  41.790001   
14     558.400024  ...  369.377350   353.0  49.770000  54.930000  49.849998   
35     583.099976  ...  369.660370   352.0  55.220001  58.139999  48.930000   
41     580.900024  ...  368.018524   352.0  49.669998  45.000000  49.810001   
42     581.000000  ...  368.452820   353.0  51.299999  47.660000  60.000000   
52     582.900024  ...  368.320740   353.0  54.060001  51.180000  52.169998   
53     583.400024  ...  361.226410   342.0  54.040001  51.250000  54.980000   
54     583.000000  ...  367.849060   352.0  55.720001  57.570000  42.080002   
61     592.099976  ...  370.000000   354.0  51.557312  54.230148  48.665222   
64     593.700012  ...  367.943390   352.0  51.557312  54.230148  48.665222   
65     593.799988  ...  368.056610   352.0  51.549999  55.549999  39.849998   
66     593.200012  ...  369.111115   353.0  51.369999  55.700001  52.490002   

          X_2869     X_2870  X_2871  prediction_label  prediction_score  
index                                                                    
7      57.990002  63.160000     1.0                 0              0.64  
8      47.939999  60.720001     1.0                 0              0.57  
14     48.619999  63.180000     1.0                 0              0.56  
35     56.160000  64.250000     1.0                 0              0.65  
41     55.189999  67.169998     1.0                 0              0.45  
42     53.750000  62.580002     1.0                 0              0.46  
52     57.750000  63.939999     1.0                 0              0.58  
53     57.220001  63.330002     1.0                 0              0.56  
54     55.189999  66.059998     1.0                 0              0.54  
61     52.332539  66.685966     1.0                 1              0.49  
64     52.332539  66.685966     1.0                 0              0.53  
65     47.820000  61.590000     1.0                 0              0.76  
66     48.340000  62.119999     1.0                 0              0.72  

[13 rows x 1970 columns]

In [249]:
TT050307_y_class = pd.DataFrame(TT050307, columns = ['PRODUCT_CODE'])
TT050307_idx = TT050307_y_class.index
TT050307_y_class = TT050307_y_class.reset_index()
TT050307_prediction = pd.concat([TT050307_prediction, TT050307_y_class], axis = 1)
TT050307_prediction = TT050307_prediction.set_index('index')
TT050307_prediction.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

In [250]:
TT010305_y_class = pd.DataFrame(TT010305, columns = ['PRODUCT_CODE'])
TT010305_idx = TT010305_y_class.index
TT010305_y_class = TT010305_y_class.reset_index()
TT010305_prediction = pd.concat([TT010305_prediction, TT010305_y_class], axis = 1)
TT010305_prediction = TT010305_prediction.set_index('index')
TT010305_prediction.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

In [251]:
TT010306_y_class = pd.DataFrame(TT010306, columns = ['PRODUCT_CODE'])
TT010306_idx = TT010306_y_class.index
TT010306_y_class = TT010306_y_class.reset_index()
TT010306_prediction = pd.concat([TT010306_prediction, TT010306_y_class], axis = 1)
TT010306_prediction = TT010306_prediction.set_index('index')
TT010306_prediction.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

In [252]:
TT100304_y_class = pd.DataFrame(TT100304, columns = ['PRODUCT_CODE'])
TT100304_idx = TT100304_y_class.index
TT100304_y_class = TT100304_y_class.reset_index()
TT100304_prediction = pd.concat([TT100304_prediction, TT100304_y_class], axis = 1)
TT100304_prediction = TT100304_prediction.set_index('index')
TT100304_prediction.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

In [253]:
TT100306_y_class = pd.DataFrame(TT100306, columns = ['PRODUCT_CODE'])
TT100306_idx = TT100306_y_class.index
TT100306_y_class = TT100306_y_class.reset_index()
TT100306_prediction = pd.concat([TT100306_prediction, TT100306_y_class], axis = 1)
TT100306_prediction = TT100306_prediction.set_index('index')
TT100306_prediction.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

In [254]:
final_test = pd.concat([TT050304_prediction, TT050307_prediction, TT010305_prediction, TT010306_prediction, TT100304_prediction, TT100306_prediction])
final_test

X_128    X_129  X_132  X_133  X_134  X_135  X_136  X_137  X_138  \
index                                                                      
7      18031.0  18031.0   0.19   0.20   0.19    0.2  354.0  354.0  354.0   
8      18064.0  18064.0   0.19   0.20   0.19    0.2  355.0  354.0  355.0   
14       295.0    295.0   0.19   0.21   0.19    0.2   60.0   60.0   60.0   
35      8632.0   8632.0   0.20   0.21   0.20    0.2  249.0  249.0  249.0   
41     10712.0  10712.0   0.20   0.21   0.20    0.2  293.0  293.0  293.0   
...        ...      ...    ...    ...    ...    ...    ...    ...    ...   
301        NaN      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
305        NaN      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
307        NaN      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
308        NaN      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
309        NaN      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   

            X_139  ...  X_930  X_931      X_932  X_933  X_93  X_94  X_95  \
index              ...                                                     
7      591.500000  ...    NaN    NaN        NaN    NaN   NaN   NaN   NaN   
8      591.500000  ...    NaN    NaN        NaN    NaN   NaN   NaN   NaN   
14     558.400024  ...    NaN    NaN        NaN    NaN   NaN   NaN   NaN   
35     583.099976  ...    NaN    NaN        NaN    NaN   NaN   NaN   NaN   
41     580.900024  ...    NaN    NaN        NaN    NaN   NaN   NaN   NaN   
...           ...  ...    ...    ...        ...    ...   ...   ...   ...   
301           NaN  ...  298.0   13.6  13.380645   13.2  0.19  0.19  0.19   
305           NaN  ...  294.0   13.6  13.341935   13.2  0.19  0.19  0.19   
307           NaN  ...  289.0   13.6  13.361290   13.2  0.19  0.19  0.19   
308           NaN  ...  290.0   13.6  13.335484   13.2  0.19  0.19  0.19   
309           NaN  ...  289.0   13.6  13.343333   13.2  0.19  0.19  0.19   

       X_104    X_126    X_127  
index                           
7        NaN      NaN      NaN  
8        NaN      NaN      NaN  
14       NaN      NaN      NaN  
35       NaN      NaN      NaN  
41       NaN      NaN      NaN  
...      ...      ...      ...  
301     28.0  34979.0  34979.0  
305     28.0  35871.0  35871.0  
307     28.0  36150.0  36150.0  
308     28.0  36399.0  36399.0  
309     28.0  36414.0  36414.0  

[310 rows x 2795 columns]

In [255]:
final_test = final_test.sort_index(ascending=True)
final_test['prediction_label']

index
0      1
1      1
2      1
3      1
4      1
      ..
305    1
306    1
307    1
308    1
309    1
Name: prediction_label, Length: 310, dtype: int32

In [256]:
#52
sample_submission = pd.read_csv('sample_submission.csv')
sample_submission['Y_Class'] = final_test['prediction_label']
display(sample_submission.head())
sample_submission.to_csv('line6classmean_submission.csv',index=False)

PRODUCT_ID  Y_Class
0   TEST_000        1
1   TEST_001        1
2   TEST_002        1
3   TEST_003        1
4   TEST_004        1

In [257]:
final_test['prediction_label'].value_counts()

1    264
0     30
2     16
Name: prediction_label, dtype: int64

In [258]:
np.array(final_test['prediction_label'])

array([1, 1, 1, 1, 1, 1, 1, 0, 0, 1, 1, 1, 1, 2, 0, 1, 1, 1, 1, 1, 1, 2,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 0, 1, 1, 1, 0, 0, 1,
       1, 1, 2, 1, 1, 1, 1, 1, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 0, 0, 0, 0,
       0, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 0,
       0, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 2, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 2, 0, 2, 2, 2, 0, 2, 2, 1, 1, 1, 1, 2, 1, 1, 0,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 0, 2, 0, 0,
       0, 1, 1, 1, 1, 1, 0, 0, 1, 1, 1, 1, 1, 1, 1,